# Stress Testing Facial Recognition with Adversarial Examples
By Emily Strong


Adversarial examples are inputs to a convolutional neural network that are designed to trick it. Because CNNs examine images for patterns of edges, minor changes to individual pixels can change where the edges are detected and thus the overall pattern. For a facial recognition model this translates to a change in the detected face morphology which causes a picture of one person to be labeled as someone else, or it can even cause a face in the image to not be detected.

Facial recognition is typically a pipeline rather than a single model. For this project I am using the open source [OpenFace](http://cmusatyalab.github.io/openface/) which provides a full pipeline. The first step in this process is to detect a face. The image is converted to a histogram of oriented gradients and then run through an SVM classifier trained on the pattern of the human face.

![HOG Example](https://i1.wp.com/www.hackevolve.com/wp-content/uploads/2017/09/face_hog.png)
<p style="text-align: center;">Image source: http://www.hackevolve.com/face-recognition-deep-learning/</p>

The next step is to align and normalize the image. Kazemi and Sullivan (2014) found that there are 68 facial landmarks that exist on every face and can be used to perform affine transformations so that the placement of the landmarks is standardized among a set of images. Here the outer corners of the eyes and the tip of the nose are used. Each image also needs to be cropped to the face area and resized to 96 x 96 pixels.

![Landmarks](http://openface-api.readthedocs.io/en/latest/_images/dlib-landmark-mean.png)
<p style="text-align: center;">Image source: http://openface-api.readthedocs.io/en/latest/openface.html#openface-aligndlib-class</p>

Once all of the images are normalized they are run through a CNN that measures distances between facial features. Schroff, Kalenichenko, and Philbin (2015) found that 128 measurements are sufficient to accurately distinguish different people. The final step in the pipeline is to input the measurements to an SVM classifier which returns the closest match based on the people it has been trained on. 

I have trained two different models that are available in the generated-embeddings folder. One is trained only on the eight people used as test subjects in this project, the other is trained on the [FaceScrub data set](http://vintage.winklerbros.net/facescrub.html) which contains 530 people. If you would like to test out training the model yourself, you need to download the FaceScrub data set and the supplemental images of Keira Knightley and Natalie Portman using the scripts and csvs in datascraping and then follow the OpenFace tutorial on [training a classifier](http://cmusatyalab.github.io/openface/demo-3-classifier/).

This project takes two different approaches to adversarial examples. In Part A, a variety of simple augmentations are made to the images such as changing the values of individual color channels or blurring the image to identify how these changes affect the performance of the facial recognition model. In Part B, images are modified by strategically adding random noise to target a source image being mislabeled as a target person. This type of adversarial example is usually done by adding textures to images based on gradient feedback from the neural network, however the OpenFace API does not include a method for accessing this feedback, so instead the images are optimized through a genetic algorithm followed by brute force attacks.

## Validating the Pipeline
For instructions on how to set up the environment for running this notebook, please see the project [README](https://github.com/erstrong/BigDataSystemsandIntelligenceAnalytics/tree/master/AdversarialFaceRecognition). 

OpenFace comes with demo code for face classification. One of the examples included is of Steve Carell shown below. OpenFace uses older versions of several Python libraries so running the script returns warnings about depreciated features. I have suppressed these to make the output easier to read.

In [2]:
import warnings
warnings.simplefilter('ignore')

In [3]:
%run ./demos/classifier.py infer models/openface/celeb-classifier.nn4.small2.v1.pkl ./images/examples/carell.jpg


=== ./images/examples/carell.jpg ===
Predict SteveCarell with 0.99 confidence.


I can run this same script with a model I have trained on my own data to identify an image of Colin Firth. In this project I am using two models, one trained only on the people used as subjects for my test cases, and one trained on the full FaceScrub data set.

In [12]:
%run ./demos/classifier.py infer ./generated-embeddings/limited/classifier.pkl test-images/colin_firth.jpg


=== test-images/colin_firth.jpg ===
Predict colin-firth with 0.98 confidence.


In [13]:
%run ./demos/classifier.py infer ./generated-embeddings/fullfacescrub/classifier.pkl test-images/colin_firth.jpg


=== test-images/colin_firth.jpg ===
Predict colin-firth with 0.61 confidence.


### Face Classification Workflow

For using this pipeline in the methods I create for the stress tests, I need to adapt the portions of "/demos/classifyer.py" used for testing a trained model so that the %run magic command doesn't have to be used every time.

First import the dependencies and set the paths for the models used in the pipeline:

In [1]:
# Adapted from https://github.com/cmusatyalab/openface/blob/master/demos/classifier.py
import random 
import cv2
import os
import pickle
import sys

from operator import itemgetter

import numpy as np
np.set_printoptions(precision=2)
import pandas as pd

import openface

from sklearn.pipeline import Pipeline
from sklearn.discriminant_analysis import LinearDiscriminantAnalysis as LDA
from sklearn.preprocessing import LabelEncoder
from sklearn.svm import SVC
from sklearn.grid_search import GridSearchCV
from sklearn.mixture import GMM
from sklearn.tree import DecisionTreeClassifier
from sklearn.naive_bayes import GaussianNB

from PIL import Image
import PIL.ImageOps    
from scipy.misc import imsave

In [3]:
# Get the current path
fileDir = os.path.dirname(os.path.realpath('FacialRecognition.ipynb'))

# Define the paths for the dlib and openface models
modelDir = os.path.join(fileDir, 'models')
dlibModelDir = os.path.join(modelDir, 'dlib')
openfaceModelDir = os.path.join(modelDir, 'openface')

# Get the models
align = openface.AlignDlib(os.path.join(dlibModelDir,"shape_predictor_68_face_landmarks.dat"))
net = openface.TorchNeuralNet(os.path.join(openfaceModelDir,'nn4.small2.v1.t7'), imgDim=96)

Next the getRep and infer methods from the classification script need to be recreated. If you compare these methods to those in the script, some portions of code have been removed that are unnecessary for my purposes. I have also added a simple run method for validating that the methods work.

In [4]:
def getRep(imgPath):

    bgrImg = cv2.imread(imgPath)
    if bgrImg is None:
        raise Exception("Unable to load image: {}".format(imgPath))

    rgbImg = cv2.cvtColor(bgrImg, cv2.COLOR_BGR2RGB)


    bb1 = align.getLargestFaceBoundingBox(rgbImg)
    
    if bb1 is None:
        raise Exception("Unable to find a face: {}".format(imgPath))
    bbs = [bb1]
    reps = []
    for bb in bbs:
        alignedFace = align.align(
            96,
            rgbImg,
            bb,
            landmarkIndices=openface.AlignDlib.OUTER_EYES_AND_NOSE)
        if alignedFace is None:
            raise Exception("Unable to align image: {}".format(imgPath))

        rep = net.forward(alignedFace)

        reps.append((bb.center().x, rep))
    sreps = sorted(reps, key=lambda x: x[0])
    return sreps

def infer(model, image):
    with open(model, 'rb') as f:
        if sys.version_info[0] < 3:
                (le, clf) = pickle.load(f)
        else:
                (le, clf) = pickle.load(f, encoding='latin1')

    
    print("\n=== {} ===".format(image))
    reps = getRep(image)
        
    for r in reps:
        rep = r[1].reshape(1, -1)
        bbx = r[0]
        predictions = clf.predict_proba(rep).ravel()
        maxI = np.argmax(predictions)
        person = le.inverse_transform(maxI)
        #confidence = predictions[maxI]
        #print("Predict {} with {:.2f} confidence.".format(person.decode('utf-8'), confidence))
        return person.decode('utf-8')

def run(model, image):
    output = infer(model, image)
    print(output)

We can validate that the methods work with our image of Colin Firth:

In [5]:
run('generated-embeddings/fullfacescrub/classifier.pkl', 'test-images/colin_firth.jpg')


=== test-images/colin_firth.jpg ===
colin-firth


## Part A: Image Augmentation
In the first part of this project I am stress testing the classification model by augmenting the image in ways that should decrease the image quality or otherwise make it more difficult to obtain the measurements that OpenFace uses to identify the faces. I am testing each method with two subjects:

<img src="test-images/colin_firth.jpg" width="200"/>
<center>Colin Firth</center>

<img src="test-images/george_lopez.jpg" width="200"/>
<center>George Lopez</center>

### Test Case A1: Inversion

In [20]:
# Adapted from https://pillow.readthedocs.io/en/3.1.x/reference/Image.html

def invert(model, image, name):
    temp = Image.open(image)
    inverted_image = PIL.ImageOps.invert(temp)
    image2 = 'output/' + name + '-invert.jpg'
    inverted_image.save(image2)
    output = infer(model, image2)
    print(output)
    

First we try the inversion method on Colin Firth:

In [21]:
invert('generated-embeddings/fullfacescrub/classifier.pkl', 'test-images/colin_firth.jpg','colin-firth')


=== output/colin-firth-invert.jpg ===


Exception: Unable to find a face: output/colin-firth-invert.jpg

Inverting this particular image apparently tricks the face detection model. In looking at the inverted image it still looks like a face to the human eye, though obviously the image has been modified.
<img src="https://github.com/erstrong/BigDataSystemsandIntelligenceAnalytics/blob/master/AdversarialFaceRecognition/examples/colin-firth-invert.jpg?raw=true" width="200"/>
Next we try the same method on George Lopez:

In [24]:
invert('generated-embeddings/fullfacescrub/classifier.pkl', 'test-images/george_lopez.jpg','george-lopez')


=== output/george-lopez-invert.jpg ===
hayden-christensen


The inverted image of George Lopez is still detected as a face, but it is no longer correctly identified. Next we look at the effects of inverting individual channels:

In [39]:
# Adapted from https://pillow.readthedocs.io/en/3.1.x/reference/Image.html

def invertchannels(model, image, name):
    temp = Image.open(image)
    r, g, b = temp.split()
    r = np.asarray(r)
    g = np.asarray(g)
    b = np.asarray(b)
    r_i = 255-r
    g_i = 255-g
    b_i = 255-b
    temp_r = np.dstack((r_i,g,b))
    temp_g = np.dstack((r,g_i,b))
    temp_b = np.dstack((r,g,b_i))
    mergedR = Image.fromarray(temp_r, 'RGB')
    mergedG = Image.fromarray(temp_g, 'RGB')
    mergedB = Image.fromarray(temp_b, 'RGB')
     
    imageR = 'output/' + name + '-invertR.jpg'
    mergedR.save(imageR)
    outputR = infer(model, imageR)
    print(outputR)
    imageG = 'output/' + name + '-invertG.jpg'
    mergedG.save(imageG)
    outputG = infer(model, imageG)
    print(outputG)
    imageB = 'output/' + name + '-invertB.jpg'
    mergedB.save(imageB)
    outputB = infer(model, imageB)
    print(outputB)

In [40]:
invertchannels('generated-embeddings/fullfacescrub/classifier.pkl', 'test-images/colin_firth.jpg','colin-firth')


=== output/colin-firth-invertR.jpg ===
jonathan-sadowski

=== output/colin-firth-invertG.jpg ===
ben-kingsley

=== output/colin-firth-invertB.jpg ===
colin-firth


In [41]:
invertchannels('generated-embeddings/fullfacescrub/classifier.pkl', 'test-images/george_lopez.jpg','george-lopez')


=== output/george-lopez-invertR.jpg ===
peggy-lipton

=== output/george-lopez-invertG.jpg ===
george-clooney

=== output/george-lopez-invertB.jpg ===
burt-reynolds


As with the total inversion, the effects are slightly different for each of the two images, but apparently inverting a single channel isn't enough to cause a face to no longer be detected.

### Test Case A2: Add and add per channel
In this second test case we iteratively add to the total image or each color channel until the face is no longer correctly identified.

In [42]:
# Adapted from https://pillow.readthedocs.io/en/3.1.x/reference/Image.html
def addTotal(model, image, name):
    output = infer(model, image)
    count = 0
    while(output==name and count < 10):
        temp = Image.open(image)
        temp = np.asarray(temp)
        temp = temp + 10
        temp[temp>255] = 255
        temp = Image.fromarray(temp, 'RGB')
        image = 'output/' + name + str(count) + '-addT.jpg'
        temp.save(image)
        output = infer(model, image)
        
        print(output)
        count += 1

def addR(model, image, name):
    output = infer(model, image)
    count = 0
    while(output==name and count < 10):
        
        temp = Image.open(image)
        r, g, b = temp.split()
        r = np.asarray(r)
        g = np.asarray(g)
        b = np.asarray(b)
        r = r + 10
        r[r>255] = 255
        merged = np.dstack((r,g,b))
        merged = Image.fromarray(merged, 'RGB')
        image = 'output/' + name + str(count) + '-addR.jpg'
        merged.save(image)
        output = infer(model, image)
        
        print(output)
        count += 1
        
def addG(model, image, name):
    output = infer(model, image)
    count = 0
    while(output==name and count < 10):
        
        temp = Image.open(image)
        r, g, b = temp.split()
        r = np.asarray(r)
        g = np.asarray(g)
        b = np.asarray(b)
        g = g + 10
        g[g>255] = 255
        merged = np.dstack((r,g,b))
        merged = Image.fromarray(merged, 'RGB')
        image = 'output/' + name + str(count) + '-addG.jpg'
        merged.save(image)
        output = infer(model, image)
        
        print(output)
        count += 1        
        
def addB(model, image, name):
    output = infer(model, image)
    count = 0
    while(output==name and count < 10):
        
        temp = Image.open(image)
        r, g, b = temp.split()
        r = np.asarray(r)
        g = np.asarray(g)
        b = np.asarray(b)
        b = b + 10
        b[b>255] = 255
        merged = np.dstack((r,g,b))
        merged = Image.fromarray(merged, 'RGB')
        image = 'output/' + name + str(count) + '-addB.jpg'
        merged.save(image)
        output = infer(model, image)
        
        print(output)
        count += 1

In [43]:
addTotal('generated-embeddings/fullfacescrub/classifier.pkl', 'test-images/colin_firth.jpg','colin-firth')


=== test-images/colin_firth.jpg ===

=== output/colin-firth0-addT.jpg ===
colin-firth

=== output/colin-firth1-addT.jpg ===
colin-firth

=== output/colin-firth2-addT.jpg ===
colin-firth

=== output/colin-firth3-addT.jpg ===
colin-firth

=== output/colin-firth4-addT.jpg ===
colin-firth

=== output/colin-firth5-addT.jpg ===
bruce-greenwood


In [44]:
addR('generated-embeddings/fullfacescrub/classifier.pkl', 'test-images/colin_firth.jpg','colin-firth')


=== test-images/colin_firth.jpg ===

=== output/colin-firth0-addR.jpg ===
colin-firth

=== output/colin-firth1-addR.jpg ===
colin-firth

=== output/colin-firth2-addR.jpg ===
colin-firth

=== output/colin-firth3-addR.jpg ===
colin-firth

=== output/colin-firth4-addR.jpg ===
colin-firth

=== output/colin-firth5-addR.jpg ===
jack-nicholson


In [45]:
addG('generated-embeddings/fullfacescrub/classifier.pkl', 'test-images/colin_firth.jpg','colin-firth')


=== test-images/colin_firth.jpg ===

=== output/colin-firth0-addG.jpg ===
colin-firth

=== output/colin-firth1-addG.jpg ===
colin-firth

=== output/colin-firth2-addG.jpg ===
colin-firth

=== output/colin-firth3-addG.jpg ===
colin-firth

=== output/colin-firth4-addG.jpg ===
colin-firth

=== output/colin-firth5-addG.jpg ===
colin-firth

=== output/colin-firth6-addG.jpg ===
sean-bean


In [46]:
addB('generated-embeddings/fullfacescrub/classifier.pkl', 'test-images/colin_firth.jpg','colin-firth')


=== test-images/colin_firth.jpg ===

=== output/colin-firth0-addB.jpg ===
colin-firth

=== output/colin-firth1-addB.jpg ===
colin-firth

=== output/colin-firth2-addB.jpg ===
colin-firth

=== output/colin-firth3-addB.jpg ===
colin-firth

=== output/colin-firth4-addB.jpg ===
colin-firth

=== output/colin-firth5-addB.jpg ===
colin-firth

=== output/colin-firth6-addB.jpg ===
colin-firth

=== output/colin-firth7-addB.jpg ===
colin-firth

=== output/colin-firth8-addB.jpg ===
colin-firth

=== output/colin-firth9-addB.jpg ===
colin-firth


In [47]:
addTotal('generated-embeddings/fullfacescrub/classifier.pkl', 'test-images/george_lopez.jpg','george-lopez')


=== test-images/george_lopez.jpg ===

=== output/george-lopez0-addT.jpg ===
george-lopez

=== output/george-lopez1-addT.jpg ===
george-lopez

=== output/george-lopez2-addT.jpg ===
george-lopez

=== output/george-lopez3-addT.jpg ===
george-lopez

=== output/george-lopez4-addT.jpg ===
george-lopez

=== output/george-lopez5-addT.jpg ===
tom-hanks


In [48]:
addR('generated-embeddings/fullfacescrub/classifier.pkl', 'test-images/george_lopez.jpg','george-lopez')


=== test-images/george_lopez.jpg ===

=== output/george-lopez0-addR.jpg ===
george-lopez

=== output/george-lopez1-addR.jpg ===
george-lopez

=== output/george-lopez2-addR.jpg ===
george-lopez

=== output/george-lopez3-addR.jpg ===
george-lopez

=== output/george-lopez4-addR.jpg ===
george-lopez

=== output/george-lopez5-addR.jpg ===
tom-hanks


In [49]:
addG('generated-embeddings/fullfacescrub/classifier.pkl', 'test-images/george_lopez.jpg','george-lopez')


=== test-images/george_lopez.jpg ===

=== output/george-lopez0-addG.jpg ===
george-lopez

=== output/george-lopez1-addG.jpg ===
george-lopez

=== output/george-lopez2-addG.jpg ===
george-lopez

=== output/george-lopez3-addG.jpg ===
george-lopez

=== output/george-lopez4-addG.jpg ===
george-lopez

=== output/george-lopez5-addG.jpg ===
george-lopez

=== output/george-lopez6-addG.jpg ===
robert-downey-jr.


In [53]:
addB('generated-embeddings/fullfacescrub/classifier.pkl', 'test-images/george_lopez.jpg','george-lopez')


=== test-images/george_lopez.jpg ===

=== output/george-lopez0-addB.jpg ===
george-lopez

=== output/george-lopez1-addB.jpg ===
george-lopez

=== output/george-lopez2-addB.jpg ===
george-lopez

=== output/george-lopez3-addB.jpg ===
george-lopez

=== output/george-lopez4-addB.jpg ===
george-lopez

=== output/george-lopez5-addB.jpg ===
george-lopez

=== output/george-lopez6-addB.jpg ===
george-lopez

=== output/george-lopez7-addB.jpg ===
george-lopez

=== output/george-lopez8-addB.jpg ===
george-lopez

=== output/george-lopez9-addB.jpg ===
george-lopez


Again the effects are slightly different for each of them, though for both adding 100 to the blue channel didn't cause misidentification. An example of what this looks like:

<img src="https://github.com/erstrong/BigDataSystemsandIntelligenceAnalytics/blob/master/AdversarialFaceRecognition/examples/george-lopez9-addB.jpg?raw=true" width="200"/>

### Test Case A3: Multiply and multiply per channel
The third test case is doubling the value of the channels, again on all channels together and individually.

In [51]:
# Adapted from https://pillow.readthedocs.io/en/3.1.x/reference/Image.html
def multiplyTotal(model, image, name):
    temp = Image.open(image)
    temp = np.asarray(temp)
    temp = temp * 2
    temp[temp>255] = 255
    temp = Image.fromarray(temp, 'RGB')
    image = 'output/' + name + '-multiplyT.jpg'
    temp.save(image)
    output = infer(model, image)
    print(output)
        

def multiplyR(model, image, name):
    temp = Image.open(image)
    r, g, b = temp.split()
    r = np.asarray(r)
    g = np.asarray(g)
    b = np.asarray(b)
    r = r * 2
    r[r>255] = 255
    merged = np.dstack((r,g,b))
    merged = Image.fromarray(merged, 'RGB')
    image = 'output/' + name + '-multiplyR.jpg'
    temp.save(image)
    output = infer(model, image) 
    print(output)
        
        
def multiplyG(model, image, name):
    temp = Image.open(image)
    r, g, b = temp.split()
    r = np.asarray(r)
    g = np.asarray(g)
    b = np.asarray(b)
    g = g * 2
    g[g>255] = 255
    merged = np.dstack((r,g,b))
    merged = Image.fromarray(merged, 'RGB')
    image = 'output/' + name + '-multiplyG.jpg'
    temp.save(image)
    output = infer(model, image)    
    print(output)
                
        
def multiplyB(model, image, name):
    temp = Image.open(image)
    r, g, b = temp.split()
    r = np.asarray(r)
    g = np.asarray(g)
    b = np.asarray(b)
    b = b * 2
    b[b>255] = 255
    merged = np.dstack((r,g,b))
    merged = Image.fromarray(merged, 'RGB')
    image = 'output/' + name + '-multiplyB.jpg'
    temp.save(image)
    output = infer(model, image)    
    print(output)
        

In [52]:
multiplyTotal('generated-embeddings/fullfacescrub/classifier.pkl', 'test-images/colin_firth.jpg','colin-firth')


=== output/colin-firth-multiplyT.jpg ===


Exception: Unable to find a face: output/colin-firth-multiplyT.jpg

In [54]:
multiplyR('generated-embeddings/fullfacescrub/classifier.pkl', 'test-images/colin_firth.jpg','colin-firth')


=== output/colin-firth-multiplyR.jpg ===
colin-firth


In [55]:
multiplyG('generated-embeddings/fullfacescrub/classifier.pkl', 'test-images/colin_firth.jpg','colin-firth')


=== output/colin-firth-multiplyG.jpg ===
colin-firth


In [56]:
multiplyB('generated-embeddings/fullfacescrub/classifier.pkl', 'test-images/colin_firth.jpg','colin-firth')


=== output/colin-firth-multiplyB.jpg ===
colin-firth


In [57]:
multiplyTotal('generated-embeddings/fullfacescrub/classifier.pkl', 'test-images/george_lopez.jpg','george-lopez')


=== output/george-lopez-multiplyT.jpg ===
dustin-hoffman


In [58]:
multiplyR('generated-embeddings/fullfacescrub/classifier.pkl', 'test-images/george_lopez.jpg','george-lopez')


=== output/george-lopez-multiplyR.jpg ===
george-lopez


In [59]:
multiplyG('generated-embeddings/fullfacescrub/classifier.pkl', 'test-images/george_lopez.jpg','george-lopez')


=== output/george-lopez-multiplyG.jpg ===
george-lopez


In [60]:
multiplyB('generated-embeddings/fullfacescrub/classifier.pkl', 'test-images/george_lopez.jpg','george-lopez')


=== output/george-lopez-multiplyB.jpg ===
george-lopez


Interestingly, the "total" change again caused Colin Firth's face to not be detected whereas for George Lopez it simply caused a misidentification similar to what happened with inversion. In addition, the individual channel doublings did not cause either to be misidentified.

### Test Case A4: Subtract and subtract per channel
Our fourth test case is to iteratively subtract similar to what was done in the test case 2 addition.

In [61]:
# Adapted from https://pillow.readthedocs.io/en/3.1.x/reference/Image.html
def subtractTotal(model, image, name):
    output = infer(model, image)
    count = 0
    while(output==name and count < 10):
        temp = Image.open(image)
        temp = np.asarray(temp)
        temp = temp - 10
        temp[temp<0] = 0
        temp = Image.fromarray(temp, 'RGB')
        image = 'output/' + name + str(count) + '-subT.jpg'
        temp.save(image)
        output = infer(model, image)
        
        print(output)
        count += 1

def subtractR(model, image, name):
    output = infer(model, image)
    count = 0
    while(output==name and count < 10):
        
        temp = Image.open(image)
        r, g, b = temp.split()
        r = np.asarray(r)
        g = np.asarray(g)
        b = np.asarray(b)
        r = r - 10
        r[r<0] = 0
        merged = np.dstack((r,g,b))
        merged = Image.fromarray(merged, 'RGB')
        image = 'output/' + name + str(count) + '-subR.jpg'
        merged.save(image)
        output = infer(model, image)
        
        print(output)
        count += 1
        
def subtractG(model, image, name):
    output = infer(model, image)
    count = 0
    while(output==name and count < 10):
        
        temp = Image.open(image)
        r, g, b = temp.split()
        r = np.asarray(r)
        g = np.asarray(g)
        b = np.asarray(b)
        g = g - 10
        g[g<0] = 0
        merged = np.dstack((r,g,b))
        merged = Image.fromarray(merged, 'RGB')
        image = 'output/' + name + str(count) + '-subG.jpg'
        merged.save(image)
        output = infer(model, image)
        
        print(output)
        count += 1        
        
def subtractB(model, image, name):
    output = infer(model, image)
    count = 0
    while(output==name and count < 10):
        
        temp = Image.open(image)
        r, g, b = temp.split()
        r = np.asarray(r)
        g = np.asarray(g)
        b = np.asarray(b)
        b = b - 10
        b[b<0] = 0
        merged = np.dstack((r,g,b))
        merged = Image.fromarray(merged, 'RGB')
        image = 'output/' + name + str(count) + '-subB.jpg'
        merged.save(image)
        output = infer(model, image)
        
        print(output)
        count += 1

In [62]:
subtractTotal('generated-embeddings/fullfacescrub/classifier.pkl', 'test-images/colin_firth.jpg','colin-firth')


=== test-images/colin_firth.jpg ===

=== output/colin-firth0-subT.jpg ===
colin-firth

=== output/colin-firth1-subT.jpg ===
colin-firth

=== output/colin-firth2-subT.jpg ===
alan-alda


In [63]:
subtractR('generated-embeddings/fullfacescrub/classifier.pkl', 'test-images/colin_firth.jpg','colin-firth')


=== test-images/colin_firth.jpg ===

=== output/colin-firth0-subR.jpg ===
colin-firth

=== output/colin-firth1-subR.jpg ===
colin-firth

=== output/colin-firth2-subR.jpg ===
colin-firth

=== output/colin-firth3-subR.jpg ===
colin-firth

=== output/colin-firth4-subR.jpg ===
colin-firth

=== output/colin-firth5-subR.jpg ===
colin-firth

=== output/colin-firth6-subR.jpg ===
colin-firth

=== output/colin-firth7-subR.jpg ===
ben-kingsley


In [64]:
subtractG('generated-embeddings/fullfacescrub/classifier.pkl', 'test-images/colin_firth.jpg','colin-firth')


=== test-images/colin_firth.jpg ===

=== output/colin-firth0-subG.jpg ===
colin-firth

=== output/colin-firth1-subG.jpg ===
colin-firth

=== output/colin-firth2-subG.jpg ===
colin-firth

=== output/colin-firth3-subG.jpg ===
colin-firth

=== output/colin-firth4-subG.jpg ===
neal-mcdonough


In [65]:
subtractB('generated-embeddings/fullfacescrub/classifier.pkl', 'test-images/colin_firth.jpg','colin-firth')


=== test-images/colin_firth.jpg ===

=== output/colin-firth0-subB.jpg ===
colin-firth

=== output/colin-firth1-subB.jpg ===
colin-firth

=== output/colin-firth2-subB.jpg ===
colin-firth

=== output/colin-firth3-subB.jpg ===
colin-firth

=== output/colin-firth4-subB.jpg ===
colin-firth

=== output/colin-firth5-subB.jpg ===
colin-firth

=== output/colin-firth6-subB.jpg ===
colin-firth

=== output/colin-firth7-subB.jpg ===
colin-firth

=== output/colin-firth8-subB.jpg ===
aaron-eckhart


In [66]:
subtractTotal('generated-embeddings/fullfacescrub/classifier.pkl', 'test-images/george_lopez.jpg','george-lopez')


=== test-images/george_lopez.jpg ===

=== output/george-lopez0-subT.jpg ===
george-lopez

=== output/george-lopez1-subT.jpg ===
george-lopez

=== output/george-lopez2-subT.jpg ===
josh-brolin


In [67]:
subtractR('generated-embeddings/fullfacescrub/classifier.pkl', 'test-images/george_lopez.jpg','george-lopez')


=== test-images/george_lopez.jpg ===

=== output/george-lopez0-subR.jpg ===
george-lopez

=== output/george-lopez1-subR.jpg ===
george-lopez

=== output/george-lopez2-subR.jpg ===
george-lopez

=== output/george-lopez3-subR.jpg ===
george-lopez

=== output/george-lopez4-subR.jpg ===
george-lopez

=== output/george-lopez5-subR.jpg ===
george-lopez

=== output/george-lopez6-subR.jpg ===
george-lopez

=== output/george-lopez7-subR.jpg ===
george-lopez

=== output/george-lopez8-subR.jpg ===
george-lopez

=== output/george-lopez9-subR.jpg ===
robert-downey-jr.


In [68]:
subtractG('generated-embeddings/fullfacescrub/classifier.pkl', 'test-images/george_lopez.jpg','george-lopez')


=== test-images/george_lopez.jpg ===

=== output/george-lopez0-subG.jpg ===
george-lopez

=== output/george-lopez1-subG.jpg ===
george-lopez

=== output/george-lopez2-subG.jpg ===
george-lopez

=== output/george-lopez3-subG.jpg ===
mel-gibson


In [69]:
subtractB('generated-embeddings/fullfacescrub/classifier.pkl', 'test-images/george_lopez.jpg','george-lopez')


=== test-images/george_lopez.jpg ===

=== output/george-lopez0-subB.jpg ===
george-lopez

=== output/george-lopez1-subB.jpg ===
george-lopez

=== output/george-lopez2-subB.jpg ===
george-lopez

=== output/george-lopez3-subB.jpg ===
george-lopez

=== output/george-lopez4-subB.jpg ===
george-lopez

=== output/george-lopez5-subB.jpg ===


Exception: Unable to find a face: output/george-lopez5-subB.jpg

The overall trend of the first four test cases is that changing one channel has less of an effect than changing all three, even when the individual channel changes are done to extreme values. No single color channel seems to dominate edge detection for the labeling, though skin tone differences may account for why a change will cause one test subject's face to no longer be detected but not the other.

### Test Case A5: Gaussian blur
The next test case is to blur the images.

In [10]:
# Adapted from https://stackoverflow.com/questions/17595912/gaussian-smoothing-an-image-in-python

import scipy.ndimage as ndimage

def blur(model, image, name):
    img = ndimage.imread(image)
    img = ndimage.gaussian_filter(img, sigma=(5, 5, 0), order=0)
    imgout = Image.fromarray(img, 'RGB')
    filename = 'output/gaussianblur' + name + '.jpg'
    imgout.save(filename)
    output = infer(model, filename)
    print(output)


In [11]:
blur('generated-embeddings/fullfacescrub/classifier.pkl', 'test-images/colin_firth.jpg','colin-firth')


=== output/gaussianblurcolin-firth.jpg ===
colin-firth


In [12]:
blur('generated-embeddings/fullfacescrub/classifier.pkl', 'test-images/george_lopez.jpg','george-lopez')


=== output/gaussianblurgeorge-lopez.jpg ===
george-lopez


The lack of effect is likely related to the scale at which the images are resized to during the normalization step.
### Test Case A6: Gaussian Noise

In [46]:
# Adapted from https://stackoverflow.com/questions/22937589/how-to-add-noise-gaussian-salt-and-pepper-etc-to-image-in-python-with-opencv

def gaussianNoise(model, image, name):
    img = Image.open(image)
    img.load()
    mean = 0.0
    var = 255
    sigma = var**0.5
    img = np.asarray(img)
    l, w, d = img.shape
    gauss = np.random.normal(mean,sigma,(l, w, d)).astype('uint8')
    gauss = gauss.reshape(l, w, d)
    noisy = img.astype('uint8') + gauss
    img = Image.fromarray(noisy, 'RGB')
    filename = 'test-images/gaussiannoise' + name + '.jpg'
    img.save(filename)
    output = infer(model, filename)
    print(output)

In [47]:
gaussianNoise('generated-embeddings/fullfacescrub/classifier.pkl', 'test-images/colin_firth.jpg','colin-firth')


=== test-images/gaussiannoisecolin-firth.jpg ===
colin-firth


In [48]:
gaussianNoise('generated-embeddings/fullfacescrub/classifier.pkl', 'test-images/george_lopez.jpg','george-lopez')


=== test-images/gaussiannoisegeorge-lopez.jpg ===
george-lopez


### Test Case A7: Salt and pepper noise
To contrast with the Guassian noise results, we can next try salt and pepper noise.

In [29]:
# Adapted from https://stackoverflow.com/questions/22937589/how-to-add-noise-gaussian-salt-and-pepper-etc-to-image-in-python-with-opencv

def saltAndPepper(model, image, name):
    img = Image.open(image)
    img.load()
    img_a = np.asarray(img)
    r, g, b = img.split()
    r = np.asarray(r)
    g = np.asarray(g)
    b = np.asarray(b)
    rsp = np.zeros(r.shape,np.uint8)
    gsp = np.zeros(g.shape,np.uint8)
    bsp = np.zeros(r.shape,np.uint8)
    for i in range(img_a.shape[0]):
        for j in range(img_a.shape[1]):
            rdn = random.random()
            if rdn < .05:
                rsp[i][j] = 0
            elif rdn > .95:
                rsp[i][j] = 255
            else:
                rsp[i][j] = r[i][j]
    for i in range(img_a.shape[0]):
        for j in range(img_a.shape[1]):
            rdn = random.random()
            if rdn < .05:
                gsp[i][j] = 0
            elif rdn > .95:
                gsp[i][j] = 255
            else:
                gsp[i][j] = g[i][j]
    for i in range(img_a.shape[0]):
        for j in range(img_a.shape[1]):
            rdn = random.random()
            if rdn < .05:
                bsp[i][j] = 0
            elif rdn > .95:
                bsp[i][j] = 255
            else:
                bsp[i][j] = b[i][j]
    merged = np.dstack((rsp,gsp,bsp))
    merged = Image.fromarray(merged, 'RGB')
    filename = 'output/snp' + name + '.jpg'
    merged.save(filename)
    output = infer(model, filename)
        
    print(output)


In [73]:
saltAndPepper('generated-embeddings/fullfacescrub/classifier.pkl', 'test-images/colin_firth.jpg','colin-firth')


=== output/snpcolin-firth.jpg ===
jack-nicholson


In [74]:
saltAndPepper('generated-embeddings/fullfacescrub/classifier.pkl', 'test-images/george_lopez.jpg','george-lopez')


=== output/snpgeorge-lopez.jpg ===
jackie-chan


To the human eye there is little difference between the Gaussian noise and salt and pepper noise:

<img src="https://github.com/erstrong/BigDataSystemsandIntelligenceAnalytics/blob/master/AdversarialFaceRecognition/examples/gaussiannoisecolin-firth.jpg?raw=true" width="200"/>
<p style="text-align: center;">Colin Firth with Gaussian noise</p>
<img src="https://github.com/erstrong/BigDataSystemsandIntelligenceAnalytics/blob/master/AdversarialFaceRecognition/examples/snpcolin-firth.jpg?raw=true" width="200"/>
<p style="text-align: center;">Colin Firth with salt and pepper noise</p>
It's interesting that the first example doesn't have any effect on the image classification, but the second does.
### Test Case A8: Contrast 
The final augmentation test case is changing the image contrast. We'll try two modifications - high contrast and low contrast.

In [23]:
# Adapted from https://stackoverflow.com/questions/42045362/change-contrast-of-image-in-pil
# Consulted http://www.dfstudios.co.uk/articles/programming/image-programming-algorithms/image-processing-algorithms-part-5-contrast-adjustment/
def highContrast(model, image, name):
    img = Image.open(image)
    factor = (259 * (200 + 255)) / (255 * (259 - 200))
    def contrast(c):
        return 128 + factor * (c - 128)
    contrastimg = img.point(contrast)
    filename = 'output/highcontrast-'+ name +'.jpg'
    contrastimg.save(filename)
    output = infer(model, filename)
    print(output)
    
def lowContrast(model, image, name):
    img = Image.open(image)
    factor = (259 * (255 - 200)) / (255 * (259 + 200))
    def contrast(c):
        return 128 + factor * (c - 128)
    contrastimg = img.point(contrast)
    filename = 'output/lowcontrast-'+ name +'.jpg'
    contrastimg.save(filename)
    output = infer(model, filename)
    print(output)
    

In [24]:
highContrast('generated-embeddings/fullfacescrub/classifier.pkl', 'test-images/colin_firth.jpg','colin-firth')


=== output/highcontrast-colin-firth.jpg ===
colin-firth


In [25]:
lowContrast('generated-embeddings/fullfacescrub/classifier.pkl', 'test-images/colin_firth.jpg','colin-firth')


=== output/lowcontrast-colin-firth.jpg ===


Exception: Unable to find a face: output/lowcontrast-colin-firth.jpg

In [26]:
highContrast('generated-embeddings/fullfacescrub/classifier.pkl', 'test-images/george_lopez.jpg','george-lopez')


=== output/highcontrast-george-lopez.jpg ===
kal-penn


In [27]:
lowContrast('generated-embeddings/fullfacescrub/classifier.pkl', 'test-images/george_lopez.jpg','george-lopez')


=== output/lowcontrast-george-lopez.jpg ===


Exception: Unable to find a face: output/lowcontrast-george-lopez.jpg

Let's look at the images:
<img src="https://github.com/erstrong/BigDataSystemsandIntelligenceAnalytics/blob/master/AdversarialFaceRecognition/examples/lowcontrast-george-lopez.jpg?raw=true" width="200"/>
<p style="text-align: center;">George Lopez with low contrast</p>
<img src="https://github.com/erstrong/BigDataSystemsandIntelligenceAnalytics/blob/master/AdversarialFaceRecognition/examples/highcontrast-george-lopez.jpg?raw=true" width="200"/>
<p style="text-align: center;">George Lopez with high contrast</p>

It's no wonder the model can't find a face in the low contrast image! 

This wraps up the image augmentation test cases. These test cases have highlighted that different methods of augmentation can be used to trick the CNN into mislabeling a face or not detecting a face at all, but the degree of effectiveness and how much change needs to be made to the image depends on the particular image and very likely the skin tone of the person pictured.

## Part B: Targeted Examples
In this second part of the project, I am modifying images specifically to trick the network into identifying a target label. As I previously mentioned, the standard way of accomplishing this won't work with the OpenFace model but we can still modify the images with random noise to achieve different labels as demonstrated with the salt and pepper example, and we can use a genetic algorithm to optimize the noise.

### Genetic Algorithm
In addition to the classsifier script that I adapted the infer method from, OpenFace comes with a compare script that measures the difference between two faces. The basic operation of this script is to use the getRep method on each image and calculate their difference. The resulting vector is converted to a dot product to give a single value. We can use this same process to design a simple genetic algorithm. 

[Genetic algorithms](https://en.wikipedia.org/wiki/Genetic_algorithm) are used in optimization problems by starting with a "population", using asexual reproduction (mutation) and/or sexual reproduction to generate new members of the population and assigning them fitness scores. The population can then be culled so that only the most fit members survive to the next generation. In this case, the initial population is the image being transformed, in each generation 20 children are created through random mutation, and the fitness score is the dot product of the difference between the embeddings of the image and an image of the target person. With each generation only the most fit member of the population is retained to seed the next one.

The creators of OpenFace found that [0.99 is the average threshold](https://cmusatyalab.github.io/openface/demo-2-comparison/) for distinguishing pictures of different people, however in running the comparison on my test subjects with similar faces who the classifier correctly distinguishes between, their difference is 0.53, so I am using 0.25 as a cutoff. If the minimum fitness score ever reaches 0.25 the algorithm will terminate and that fittest image is the best candidate for being able to trick the classification model. If no solution is found after 250 generations the algorithm will terminate, and the fittest image from the final generation can be run through a brute force method to see if it can be further improved.

In [5]:
# Adapted from https://github.com/cmusatyalab/openface/blob/master/demos/compare.py
def compare(img1, img2):
    d = getRep(img1)[0][1] - getRep(img2)[0][1]
    return np.dot(d, d)

# Clipping adapted from https://medium.com/@ageitgey/machine-learning-is-fun-part-8-how-to-intentionally-trick-neural-networks-b55da32b7196
# Tuple sort adapted from https://stackoverflow.com/questions/3121979/how-to-sort-list-tuple-of-lists-tuples  
def evolve(img1, img2, label, suffix):
    min_fitness = compare(img1, img2)
    fittest = img1
    population = [(fittest, min_fitness)]
    
    print("Start: " + str(min_fitness))
    count = 0 # generation number
    
    original = Image.open(img1)
    original.load()
    original = np.asarray(original)
    max_change_above = original + 10
    max_change_below = original - 10
    
    while (min_fitness >= 0.25 and count < 250):
        count2 = 0 # child number
        while(count2 < 20):
            count2 +=1
            imgSeed = Image.open(fittest)
            imgSeed.load()
            imgSeedArray = np.asarray(imgSeed)
            l, w, d = imgSeedArray.shape
            mult = np.random.randint(5, size=(l, w, d), dtype=np.uint8)
            r = random.randint(0,1)
            if r == 0:
                imgSeedArray = imgSeedArray + mult
            else:
                imgSeedArray = imgSeedArray - mult
            imgSeedArray = np.clip(imgSeedArray, max_change_below, max_change_above)
            imgSeedArray = np.clip(imgSeedArray, 0, 255)
            img = Image.fromarray(imgSeedArray, 'RGB')
            filename = 'output/compare' + label + suffix + str(count) + '_'+ str(count2) + '.jpg'
            img.save(filename)
            d = compare(filename, img2)
            print(filename + ': ' + str(d))
            population.append((filename, d))
        population.sort(key=lambda tup: tup[1]) 
        fittest, min_fitness = population[0]
        population = [(fittest, min_fitness)]
        print("Fittest: " + fittest + " " + str(min_fitness))
        count +=1
        

In [6]:
random.seed(10)

If we check the compare method on images of Natalie Portman and Keira Knightley it returns a difference of 0.53, consistent with the high level of similarity between the two actresses:

In [10]:
compare('test-images/natalie_portman2.jpg','test-images/keira_knightley2.jpg')

0.5258493569646716

Next we can run the genetic algorithm on the various combinations of test subjects we will be using:
* People with similar faces: Keira Knightley + Natalie Portman
* People with disimilar faces: Keira Knightley + Kristin Chenoweth, Colin Firth + Matthew Perry
* People of the same race with different genders: Kristin Chenoweth + Colin Firth, Tatyan M. Ali + Samuel L. Jackson
* People with different races and the same gender: Kristin Chenowth + Tatyana M. Ali, Colin Firth + George Lopez, George Lopez + Ken Watanabe
* People with different races adn genders: Kristin Chenowth + George Lopez, Tatyana M. Ali + Ken Watanabe

Each evolution will take 3-4 hours to run.

In [9]:
evolve('test-images/natalie_portman1.jpg','test-images/keira_knightley2.jpg','natalie-portman','R')

Start: 0.5704676020760274
output/comparenatalie-portmanR0_1.jpg: 0.7982226124513393
output/comparenatalie-portmanR0_2.jpg: 1.0115083272560228
output/comparenatalie-portmanR0_3.jpg: 0.8266914451898826
output/comparenatalie-portmanR0_4.jpg: 0.9644933430748999
output/comparenatalie-portmanR0_5.jpg: 0.86940233380069
output/comparenatalie-portmanR0_6.jpg: 0.8916942417475773
output/comparenatalie-portmanR0_7.jpg: 0.9475142967511488
output/comparenatalie-portmanR0_8.jpg: 0.8309841406129557
output/comparenatalie-portmanR0_9.jpg: 0.8794442905034705
output/comparenatalie-portmanR0_10.jpg: 0.7831146397279956
output/comparenatalie-portmanR0_11.jpg: 0.9402458158751565
output/comparenatalie-portmanR0_12.jpg: 0.9606700861392455
output/comparenatalie-portmanR0_13.jpg: 0.8210317048778304
output/comparenatalie-portmanR0_14.jpg: 0.7779707839596139
output/comparenatalie-portmanR0_15.jpg: 1.018760602770291
output/comparenatalie-portmanR0_16.jpg: 0.8695964339100901
output/comparenatalie-portmanR0_17.jpg: 0.

output/comparenatalie-portmanR6_15.jpg: 0.7420495948325164
output/comparenatalie-portmanR6_16.jpg: 0.8772527309833915
output/comparenatalie-portmanR6_17.jpg: 0.8565942482902691
output/comparenatalie-portmanR6_18.jpg: 0.9212025651907909
output/comparenatalie-portmanR6_19.jpg: 0.8012552750903087
output/comparenatalie-portmanR6_20.jpg: 0.7981822157181546
Fittest: test-images/natalie_portman1.jpg 0.5704676020760274
output/comparenatalie-portmanR7_1.jpg: 0.8718413333683455
output/comparenatalie-portmanR7_2.jpg: 0.8426349289092344
output/comparenatalie-portmanR7_3.jpg: 0.7698373410453072
output/comparenatalie-portmanR7_4.jpg: 1.0126807197332277
output/comparenatalie-portmanR7_5.jpg: 0.8536233098920631
output/comparenatalie-portmanR7_6.jpg: 0.9604409929202123
output/comparenatalie-portmanR7_7.jpg: 0.8934372916674251
output/comparenatalie-portmanR7_8.jpg: 0.9649886997756637
output/comparenatalie-portmanR7_9.jpg: 0.8040157137867208
output/comparenatalie-portmanR7_10.jpg: 0.854027058493321
outpu

output/comparenatalie-portmanR13_7.jpg: 0.9037229754250657
output/comparenatalie-portmanR13_8.jpg: 0.9811259191903248
output/comparenatalie-portmanR13_9.jpg: 0.8346143383344652
output/comparenatalie-portmanR13_10.jpg: 0.8174365067042582
output/comparenatalie-portmanR13_11.jpg: 0.8528056811732128
output/comparenatalie-portmanR13_12.jpg: 0.8898734830097839
output/comparenatalie-portmanR13_13.jpg: 0.7460071477294865
output/comparenatalie-portmanR13_14.jpg: 0.797528349897485
output/comparenatalie-portmanR13_15.jpg: 0.812263298277583
output/comparenatalie-portmanR13_16.jpg: 1.000161206208977
output/comparenatalie-portmanR13_17.jpg: 0.8920333778492372
output/comparenatalie-portmanR13_18.jpg: 0.785762811742239
output/comparenatalie-portmanR13_19.jpg: 0.8836347227828729
output/comparenatalie-portmanR13_20.jpg: 0.9861821475499478
Fittest: test-images/natalie_portman1.jpg 0.5704676020760274
output/comparenatalie-portmanR14_1.jpg: 0.8322685931328362
output/comparenatalie-portmanR14_2.jpg: 0.97696

output/comparenatalie-portmanR19_19.jpg: 0.8050838910334939
output/comparenatalie-portmanR19_20.jpg: 0.9776192593591138
Fittest: test-images/natalie_portman1.jpg 0.5704676020760274
output/comparenatalie-portmanR20_1.jpg: 0.9118795827849169
output/comparenatalie-portmanR20_2.jpg: 0.8893646998799083
output/comparenatalie-portmanR20_3.jpg: 0.9701429799739827
output/comparenatalie-portmanR20_4.jpg: 0.8439688778395723
output/comparenatalie-portmanR20_5.jpg: 0.7803759001670825
output/comparenatalie-portmanR20_6.jpg: 0.8007418749652584
output/comparenatalie-portmanR20_7.jpg: 0.9185743398787926
output/comparenatalie-portmanR20_8.jpg: 0.9501979071232489
output/comparenatalie-portmanR20_9.jpg: 0.8763545000909068
output/comparenatalie-portmanR20_10.jpg: 0.9018701735987762
output/comparenatalie-portmanR20_11.jpg: 0.7860098490434106
output/comparenatalie-portmanR20_12.jpg: 1.0029866595657841
output/comparenatalie-portmanR20_13.jpg: 0.8669036674455315
output/comparenatalie-portmanR20_14.jpg: 0.90226

output/comparenatalie-portmanR26_10.jpg: 0.8058642423585213
output/comparenatalie-portmanR26_11.jpg: 0.7145526549307004
output/comparenatalie-portmanR26_12.jpg: 0.8600682424290791
output/comparenatalie-portmanR26_13.jpg: 0.8350321564092467
output/comparenatalie-portmanR26_14.jpg: 0.9552040094407582
output/comparenatalie-portmanR26_15.jpg: 0.9628102854830797
output/comparenatalie-portmanR26_16.jpg: 0.7503379998210175
output/comparenatalie-portmanR26_17.jpg: 0.9433503130955787
output/comparenatalie-portmanR26_18.jpg: 0.8095439828761163
output/comparenatalie-portmanR26_19.jpg: 0.7639307727831237
output/comparenatalie-portmanR26_20.jpg: 0.8792997223185849
Fittest: test-images/natalie_portman1.jpg 0.5704676020760274
output/comparenatalie-portmanR27_1.jpg: 0.9691158569637603
output/comparenatalie-portmanR27_2.jpg: 1.0067413151057123
output/comparenatalie-portmanR27_3.jpg: 0.7368381581459208
output/comparenatalie-portmanR27_4.jpg: 0.8781230569549372
output/comparenatalie-portmanR27_5.jpg: 0.8

...

output/comparenatalie-portmanR222_1.jpg: 0.7880365203125678
output/comparenatalie-portmanR222_2.jpg: 0.9852597730567643
output/comparenatalie-portmanR222_3.jpg: 0.7993758793778714
output/comparenatalie-portmanR222_4.jpg: 0.9795800233608134
output/comparenatalie-portmanR222_5.jpg: 0.8418766855569515
output/comparenatalie-portmanR222_6.jpg: 0.8037627091697881
output/comparenatalie-portmanR222_7.jpg: 0.8272539779183683
output/comparenatalie-portmanR222_8.jpg: 0.9633420039951217
output/comparenatalie-portmanR222_9.jpg: 0.9605917339025245
output/comparenatalie-portmanR222_10.jpg: 0.8452587512244917
output/comparenatalie-portmanR222_11.jpg: 0.9045299472297882
output/comparenatalie-portmanR222_12.jpg: 0.9773603959614474
output/comparenatalie-portmanR222_13.jpg: 0.9161386256741453
output/comparenatalie-portmanR222_14.jpg: 0.8663115452964771
output/comparenatalie-portmanR222_15.jpg: 0.8066828719982022
output/comparenatalie-portmanR222_16.jpg: 0.9444823864253824
output/comparenatalie-portmanR222

output/comparenatalie-portmanR228_11.jpg: 0.8936322354455136
output/comparenatalie-portmanR228_12.jpg: 0.8761045181524592
output/comparenatalie-portmanR228_13.jpg: 0.8695992200820772
output/comparenatalie-portmanR228_14.jpg: 0.9192450349232639
output/comparenatalie-portmanR228_15.jpg: 0.7760655463673574
output/comparenatalie-portmanR228_16.jpg: 0.825902779345696
output/comparenatalie-portmanR228_17.jpg: 0.7630802486753234
output/comparenatalie-portmanR228_18.jpg: 0.7537857470439051
output/comparenatalie-portmanR228_19.jpg: 0.9547179723631147
output/comparenatalie-portmanR228_20.jpg: 0.8093609841462232
Fittest: test-images/natalie_portman1.jpg 0.5704676020760274
output/comparenatalie-portmanR229_1.jpg: 0.8339789295567954
output/comparenatalie-portmanR229_2.jpg: 0.7871414502617662
output/comparenatalie-portmanR229_3.jpg: 0.942245724191761
output/comparenatalie-portmanR229_4.jpg: 0.8209658016046613
output/comparenatalie-portmanR229_5.jpg: 0.967314466838136
output/comparenatalie-portmanR22

output/comparenatalie-portmanR235_1.jpg: 0.8069803050351146
output/comparenatalie-portmanR235_2.jpg: 0.8548817248281914
output/comparenatalie-portmanR235_3.jpg: 0.8647501651744627
output/comparenatalie-portmanR235_4.jpg: 0.8879722669372552
output/comparenatalie-portmanR235_5.jpg: 0.8741298537133397
output/comparenatalie-portmanR235_6.jpg: 0.7737965958058665
output/comparenatalie-portmanR235_7.jpg: 0.8088465917504718
output/comparenatalie-portmanR235_8.jpg: 0.870835624411758
output/comparenatalie-portmanR235_9.jpg: 0.932461853203336
output/comparenatalie-portmanR235_10.jpg: 0.8718212601141511
output/comparenatalie-portmanR235_11.jpg: 0.9493473144547743
output/comparenatalie-portmanR235_12.jpg: 0.7588279341066918
output/comparenatalie-portmanR235_13.jpg: 0.8424549608164629
output/comparenatalie-portmanR235_14.jpg: 0.9621697567188742
output/comparenatalie-portmanR235_15.jpg: 0.7984341146701011
output/comparenatalie-portmanR235_16.jpg: 0.7537859511282243
output/comparenatalie-portmanR235_1

output/comparenatalie-portmanR241_11.jpg: 0.8278574202144396
output/comparenatalie-portmanR241_12.jpg: 0.7847555228747654
output/comparenatalie-portmanR241_13.jpg: 0.890460322810622
output/comparenatalie-portmanR241_14.jpg: 0.9157371030943706
output/comparenatalie-portmanR241_15.jpg: 0.8368099891563268
output/comparenatalie-portmanR241_16.jpg: 0.8900411306410434
output/comparenatalie-portmanR241_17.jpg: 0.8851081260284821
output/comparenatalie-portmanR241_18.jpg: 0.9330999178836756
output/comparenatalie-portmanR241_19.jpg: 0.8080429691567712
output/comparenatalie-portmanR241_20.jpg: 0.7768430586176232
Fittest: test-images/natalie_portman1.jpg 0.5704676020760274
output/comparenatalie-portmanR242_1.jpg: 0.8516134780200731
output/comparenatalie-portmanR242_2.jpg: 0.8892990406354151
output/comparenatalie-portmanR242_3.jpg: 0.820553408274197
output/comparenatalie-portmanR242_4.jpg: 0.9222063593583066
output/comparenatalie-portmanR242_5.jpg: 0.7990310459387255
output/comparenatalie-portmanR2

output/comparenatalie-portmanR248_1.jpg: 0.7867353594340312
output/comparenatalie-portmanR248_2.jpg: 0.791653628348751
output/comparenatalie-portmanR248_3.jpg: 0.8091821677698718
output/comparenatalie-portmanR248_4.jpg: 0.9139494439340907
output/comparenatalie-portmanR248_5.jpg: 0.889955487117673
output/comparenatalie-portmanR248_6.jpg: 0.8728744655417755
output/comparenatalie-portmanR248_7.jpg: 0.9918435101264651
output/comparenatalie-portmanR248_8.jpg: 0.9328791147383477
output/comparenatalie-portmanR248_9.jpg: 0.8093908821990407
output/comparenatalie-portmanR248_10.jpg: 0.9084834536972243
output/comparenatalie-portmanR248_11.jpg: 0.8034237074399231
output/comparenatalie-portmanR248_12.jpg: 0.8339193235533555
output/comparenatalie-portmanR248_13.jpg: 0.8313751134436042
output/comparenatalie-portmanR248_14.jpg: 0.8580575152685201
output/comparenatalie-portmanR248_15.jpg: 0.8211066322383125
output/comparenatalie-portmanR248_16.jpg: 0.8333762821097257
output/comparenatalie-portmanR248_1

In [10]:
evolve('test-images/keira_knightley2.jpg', 'test-images/natalie_portman2.jpg','keira-knightley','R')

Start: 0.5258493569646716
output/comparekeira-knightleyR0_1.jpg: 1.7755371690924422
output/comparekeira-knightleyR0_2.jpg: 1.7657467974898657
output/comparekeira-knightleyR0_3.jpg: 1.6083238781689946
output/comparekeira-knightleyR0_4.jpg: 1.7789343544554606
output/comparekeira-knightleyR0_5.jpg: 1.589506782620704
output/comparekeira-knightleyR0_6.jpg: 1.760315769292779
output/comparekeira-knightleyR0_7.jpg: 1.7011328388994498
output/comparekeira-knightleyR0_8.jpg: 1.7260744452104855
output/comparekeira-knightleyR0_9.jpg: 1.6511579402649792
output/comparekeira-knightleyR0_10.jpg: 1.5327902118644623
output/comparekeira-knightleyR0_11.jpg: 1.6024073004392525
output/comparekeira-knightleyR0_12.jpg: 1.7780285062635834
output/comparekeira-knightleyR0_13.jpg: 1.7068344223908194
output/comparekeira-knightleyR0_14.jpg: 1.6467752684643815
output/comparekeira-knightleyR0_15.jpg: 1.6421441130800716
output/comparekeira-knightleyR0_16.jpg: 1.696743561399875
output/comparekeira-knightleyR0_17.jpg: 1.

output/comparekeira-knightleyR6_15.jpg: 1.620048180006209
output/comparekeira-knightleyR6_16.jpg: 1.615504595864027
output/comparekeira-knightleyR6_17.jpg: 1.740219920568078
output/comparekeira-knightleyR6_18.jpg: 1.673755340898783
output/comparekeira-knightleyR6_19.jpg: 1.5920983720181945
output/comparekeira-knightleyR6_20.jpg: 1.6843113416657143
Fittest: test-images/keira_knightley2.jpg 0.5258493569646716
output/comparekeira-knightleyR7_1.jpg: 1.6102133794817584
output/comparekeira-knightleyR7_2.jpg: 1.5912424083399181
output/comparekeira-knightleyR7_3.jpg: 1.7271902155157015
output/comparekeira-knightleyR7_4.jpg: 1.7798132881600406
output/comparekeira-knightleyR7_5.jpg: 1.5725745497221557
output/comparekeira-knightleyR7_6.jpg: 1.6838015694975441
output/comparekeira-knightleyR7_7.jpg: 1.7875045761035007
output/comparekeira-knightleyR7_8.jpg: 1.6888960117794962
output/comparekeira-knightleyR7_9.jpg: 1.806306379839369
output/comparekeira-knightleyR7_10.jpg: 1.7259396412110906
output/co

output/comparekeira-knightleyR13_8.jpg: 1.7340069138281544
output/comparekeira-knightleyR13_9.jpg: 1.7776290731643298
output/comparekeira-knightleyR13_10.jpg: 1.663080491821563
output/comparekeira-knightleyR13_11.jpg: 1.433836434830646
output/comparekeira-knightleyR13_12.jpg: 1.7526054418157897
output/comparekeira-knightleyR13_13.jpg: 1.6534299830154406
output/comparekeira-knightleyR13_14.jpg: 1.598360225032214
output/comparekeira-knightleyR13_15.jpg: 1.6886374432334268
output/comparekeira-knightleyR13_16.jpg: 1.6191355773999447
output/comparekeira-knightleyR13_17.jpg: 1.5688482168657192
output/comparekeira-knightleyR13_18.jpg: 1.6360853372489705
output/comparekeira-knightleyR13_19.jpg: 1.713837551233897
output/comparekeira-knightleyR13_20.jpg: 1.7707747118927664
Fittest: test-images/keira_knightley2.jpg 0.5258493569646716
output/comparekeira-knightleyR14_1.jpg: 1.7542540706979446
output/comparekeira-knightleyR14_2.jpg: 1.564852204397829
output/comparekeira-knightleyR14_3.jpg: 1.494738

output/comparekeira-knightleyR20_1.jpg: 1.528563176159421
output/comparekeira-knightleyR20_2.jpg: 1.6904032349597617
output/comparekeira-knightleyR20_3.jpg: 1.7656354692153133
output/comparekeira-knightleyR20_4.jpg: 1.6433534542202344
output/comparekeira-knightleyR20_5.jpg: 1.6300268370998816
output/comparekeira-knightleyR20_6.jpg: 1.6353930182644005
output/comparekeira-knightleyR20_7.jpg: 1.4885288533583205
output/comparekeira-knightleyR20_8.jpg: 1.6013977815124423
output/comparekeira-knightleyR20_9.jpg: 1.6713243754246117
output/comparekeira-knightleyR20_10.jpg: 1.758147920386819
output/comparekeira-knightleyR20_11.jpg: 1.5050128062487653
output/comparekeira-knightleyR20_12.jpg: 1.730909670861061
output/comparekeira-knightleyR20_13.jpg: 1.6725751205670472
output/comparekeira-knightleyR20_14.jpg: 1.6164574460981918
output/comparekeira-knightleyR20_15.jpg: 1.470185582271406
output/comparekeira-knightleyR20_16.jpg: 1.5299803762831332
output/comparekeira-knightleyR20_17.jpg: 1.6463233630

output/comparekeira-knightleyR26_14.jpg: 1.6646321048540935
output/comparekeira-knightleyR26_15.jpg: 1.5060632365036053
output/comparekeira-knightleyR26_16.jpg: 1.7538985073700684
output/comparekeira-knightleyR26_17.jpg: 1.6787458043606185
output/comparekeira-knightleyR26_18.jpg: 1.6232179207014756
output/comparekeira-knightleyR26_19.jpg: 1.7165205634266907
output/comparekeira-knightleyR26_20.jpg: 1.6968078205255122
Fittest: test-images/keira_knightley2.jpg 0.5258493569646716
output/comparekeira-knightleyR27_1.jpg: 1.7064991487680718
output/comparekeira-knightleyR27_2.jpg: 1.8036380058309225
output/comparekeira-knightleyR27_3.jpg: 1.7142024925574533
output/comparekeira-knightleyR27_4.jpg: 1.5958261261562234
output/comparekeira-knightleyR27_5.jpg: 1.5670442640606572
output/comparekeira-knightleyR27_6.jpg: 1.5557952748935746
output/comparekeira-knightleyR27_7.jpg: 1.6804679263099072
output/comparekeira-knightleyR27_8.jpg: 1.700601625619914
output/comparekeira-knightleyR27_9.jpg: 1.765912

...

output/comparekeira-knightleyR222_11.jpg: 1.7640567456073133
output/comparekeira-knightleyR222_12.jpg: 1.7309751934767554
output/comparekeira-knightleyR222_13.jpg: 1.7601149370469316
output/comparekeira-knightleyR222_14.jpg: 1.7405621617502154
output/comparekeira-knightleyR222_15.jpg: 1.5825181886564592
output/comparekeira-knightleyR222_16.jpg: 1.6072770481127718
output/comparekeira-knightleyR222_17.jpg: 1.6555566333668637
output/comparekeira-knightleyR222_18.jpg: 1.7807552607869943
output/comparekeira-knightleyR222_19.jpg: 1.5039625301583528
output/comparekeira-knightleyR222_20.jpg: 1.7427614743375472
Fittest: test-images/keira_knightley2.jpg 0.5258493569646716
output/comparekeira-knightleyR223_1.jpg: 1.5809837028205143
output/comparekeira-knightleyR223_2.jpg: 1.5788784709738675
output/comparekeira-knightleyR223_3.jpg: 1.695093820742561
output/comparekeira-knightleyR223_4.jpg: 1.5591022974405164
output/comparekeira-knightleyR223_5.jpg: 1.6778321700023104
output/comparekeira-knightleyR

output/comparekeira-knightleyR229_1.jpg: 1.6528470750420798
output/comparekeira-knightleyR229_2.jpg: 1.5910643228036057
output/comparekeira-knightleyR229_3.jpg: 1.7010766452858141
output/comparekeira-knightleyR229_4.jpg: 1.6899584933186018
output/comparekeira-knightleyR229_5.jpg: 1.5308436015740072
output/comparekeira-knightleyR229_6.jpg: 1.6699471617290609
output/comparekeira-knightleyR229_7.jpg: 1.6570270595355907
output/comparekeira-knightleyR229_8.jpg: 1.5316612267787888
output/comparekeira-knightleyR229_9.jpg: 1.640347768363236
output/comparekeira-knightleyR229_10.jpg: 1.634788759965307
output/comparekeira-knightleyR229_11.jpg: 1.5650063541052417
output/comparekeira-knightleyR229_12.jpg: 1.7739629523509732
output/comparekeira-knightleyR229_13.jpg: 1.7481416692479692
output/comparekeira-knightleyR229_14.jpg: 1.5861175709322168
output/comparekeira-knightleyR229_15.jpg: 1.7004411212309123
output/comparekeira-knightleyR229_16.jpg: 1.7165184123836221
output/comparekeira-knightleyR229_1

output/comparekeira-knightleyR235_11.jpg: 1.6543745979776698
output/comparekeira-knightleyR235_12.jpg: 1.5907709677346547
output/comparekeira-knightleyR235_13.jpg: 1.752406421018188
output/comparekeira-knightleyR235_14.jpg: 1.6150836974524911
output/comparekeira-knightleyR235_15.jpg: 1.633173738902095
output/comparekeira-knightleyR235_16.jpg: 1.7426062375055806
output/comparekeira-knightleyR235_17.jpg: 1.6328567621080667
output/comparekeira-knightleyR235_18.jpg: 1.6372419165107985
output/comparekeira-knightleyR235_19.jpg: 1.7472806610428115
output/comparekeira-knightleyR235_20.jpg: 1.6952758460161532
Fittest: test-images/keira_knightley2.jpg 0.5258493569646716
output/comparekeira-knightleyR236_1.jpg: 1.568799849446831
output/comparekeira-knightleyR236_2.jpg: 1.717236231733827
output/comparekeira-knightleyR236_3.jpg: 1.6105951129531948
output/comparekeira-knightleyR236_4.jpg: 1.6134590299821308
output/comparekeira-knightleyR236_5.jpg: 1.6174434469040224
output/comparekeira-knightleyR236

output/comparekeira-knightleyR242_1.jpg: 1.6344209872395705
output/comparekeira-knightleyR242_2.jpg: 1.7911115811100735
output/comparekeira-knightleyR242_3.jpg: 1.6144849920633835
output/comparekeira-knightleyR242_4.jpg: 1.622522533659785
output/comparekeira-knightleyR242_5.jpg: 1.6808050695886734
output/comparekeira-knightleyR242_6.jpg: 1.7741374853260075
output/comparekeira-knightleyR242_7.jpg: 1.6991485552506962
output/comparekeira-knightleyR242_8.jpg: 1.62734783683587
output/comparekeira-knightleyR242_9.jpg: 1.604593482341665
output/comparekeira-knightleyR242_10.jpg: 1.6407193470830979
output/comparekeira-knightleyR242_11.jpg: 1.6636689276989682
output/comparekeira-knightleyR242_12.jpg: 1.612638803628541
output/comparekeira-knightleyR242_13.jpg: 1.7334682724061756
output/comparekeira-knightleyR242_14.jpg: 1.5991448130675163
output/comparekeira-knightleyR242_15.jpg: 1.6608157614620476
output/comparekeira-knightleyR242_16.jpg: 1.7308463972012866
output/comparekeira-knightleyR242_17.j

output/comparekeira-knightleyR248_11.jpg: 1.757829352730616
output/comparekeira-knightleyR248_12.jpg: 1.7173755427249804
output/comparekeira-knightleyR248_13.jpg: 1.6412632081582355
output/comparekeira-knightleyR248_14.jpg: 1.5421935769762376
output/comparekeira-knightleyR248_15.jpg: 1.641916899367698
output/comparekeira-knightleyR248_16.jpg: 1.5572089998159018
output/comparekeira-knightleyR248_17.jpg: 1.6660178769232172
output/comparekeira-knightleyR248_18.jpg: 1.6234925017338646
output/comparekeira-knightleyR248_19.jpg: 1.5981993618649877
output/comparekeira-knightleyR248_20.jpg: 1.5981449620597872
Fittest: test-images/keira_knightley2.jpg 0.5258493569646716
output/comparekeira-knightleyR249_1.jpg: 1.6879758691044309
output/comparekeira-knightleyR249_2.jpg: 1.6666249032996516
output/comparekeira-knightleyR249_3.jpg: 1.5951163443053265
output/comparekeira-knightleyR249_4.jpg: 1.6321495396300745
output/comparekeira-knightleyR249_5.jpg: 1.6330529504935802
output/comparekeira-knightleyR2

In [11]:
evolve('test-images/keira_knightley2.jpg', 'test-images/kristin_chenoweth.jpg','keira-knightley','R')

Start: 1.8266409289514702
output/comparekeira-knightleyR0_1.jpg: 1.9806772398420716
output/comparekeira-knightleyR0_2.jpg: 1.8892515924641626
output/comparekeira-knightleyR0_3.jpg: 1.9286723180853589
output/comparekeira-knightleyR0_4.jpg: 1.9920303640859152
output/comparekeira-knightleyR0_5.jpg: 1.9089999416574928
output/comparekeira-knightleyR0_6.jpg: 1.9022002850054787
output/comparekeira-knightleyR0_7.jpg: 1.9140305484100577
output/comparekeira-knightleyR0_8.jpg: 1.8806176382292843
output/comparekeira-knightleyR0_9.jpg: 1.7922047927610807
output/comparekeira-knightleyR0_10.jpg: 1.9137925632712753
output/comparekeira-knightleyR0_11.jpg: 1.931644908917304
output/comparekeira-knightleyR0_12.jpg: 1.8729007126814232
output/comparekeira-knightleyR0_13.jpg: 1.929252643534843
output/comparekeira-knightleyR0_14.jpg: 2.021016200776295
output/comparekeira-knightleyR0_15.jpg: 1.9634516732623264
output/comparekeira-knightleyR0_16.jpg: 1.873975382677151
output/comparekeira-knightleyR0_17.jpg: 1.9

output/comparekeira-knightleyR6_15.jpg: 1.9429798042843613
output/comparekeira-knightleyR6_16.jpg: 1.9932979677156282
output/comparekeira-knightleyR6_17.jpg: 1.970914012160984
output/comparekeira-knightleyR6_18.jpg: 1.9365250691799853
output/comparekeira-knightleyR6_19.jpg: 1.917060196231842
output/comparekeira-knightleyR6_20.jpg: 1.9953263165032262
Fittest: output/comparekeira-knightleyR6_1.jpg 1.7056159230583736
output/comparekeira-knightleyR7_1.jpg: 1.932773620474881
output/comparekeira-knightleyR7_2.jpg: 1.8306364122617227
output/comparekeira-knightleyR7_3.jpg: 1.8807570310032347
output/comparekeira-knightleyR7_4.jpg: 1.9133024629861373
output/comparekeira-knightleyR7_5.jpg: 1.8934062701680543
output/comparekeira-knightleyR7_6.jpg: 1.8898401345156606
output/comparekeira-knightleyR7_7.jpg: 1.9497840880693795
output/comparekeira-knightleyR7_8.jpg: 1.967357168627825
output/comparekeira-knightleyR7_9.jpg: 1.9356780747987699
output/comparekeira-knightleyR7_10.jpg: 1.7999735253382556
out

output/comparekeira-knightleyR13_7.jpg: 1.8920060886008403
output/comparekeira-knightleyR13_8.jpg: 1.8880533690916668
output/comparekeira-knightleyR13_9.jpg: 1.7721216741138741
output/comparekeira-knightleyR13_10.jpg: 1.9751562075942788
output/comparekeira-knightleyR13_11.jpg: 2.004592358130817
output/comparekeira-knightleyR13_12.jpg: 1.827373407327483
output/comparekeira-knightleyR13_13.jpg: 1.7196041524156995
output/comparekeira-knightleyR13_14.jpg: 1.874184626100392
output/comparekeira-knightleyR13_15.jpg: 1.9465149189166606
output/comparekeira-knightleyR13_16.jpg: 1.6378948201714822
output/comparekeira-knightleyR13_17.jpg: 1.8569819779859609
output/comparekeira-knightleyR13_18.jpg: 1.9413935072684758
output/comparekeira-knightleyR13_19.jpg: 1.8667308949654422
output/comparekeira-knightleyR13_20.jpg: 1.878116947050533
Fittest: output/comparekeira-knightleyR13_16.jpg 1.6378948201714822
output/comparekeira-knightleyR14_1.jpg: 1.9731117188242184
output/comparekeira-knightleyR14_2.jpg: 

output/comparekeira-knightleyR19_19.jpg: 1.710343803453033
output/comparekeira-knightleyR19_20.jpg: 1.8412794156524768
Fittest: output/comparekeira-knightleyR14_3.jpg 1.6034853409616405
output/comparekeira-knightleyR20_1.jpg: 1.971880441202942
output/comparekeira-knightleyR20_2.jpg: 1.9695222709912812
output/comparekeira-knightleyR20_3.jpg: 1.870238224953801
output/comparekeira-knightleyR20_4.jpg: 1.7123970740893428
output/comparekeira-knightleyR20_5.jpg: 1.898718211491839
output/comparekeira-knightleyR20_6.jpg: 1.714738988276361
output/comparekeira-knightleyR20_7.jpg: 1.9404046951467178
output/comparekeira-knightleyR20_8.jpg: 1.9446907893418335
output/comparekeira-knightleyR20_9.jpg: 1.6616939001494913
output/comparekeira-knightleyR20_10.jpg: 1.7059224415487724
output/comparekeira-knightleyR20_11.jpg: 2.0192979371482465
output/comparekeira-knightleyR20_12.jpg: 1.8903261030581389
output/comparekeira-knightleyR20_13.jpg: 1.8567690500330865
output/comparekeira-knightleyR20_14.jpg: 1.9692

output/comparekeira-knightleyR26_10.jpg: 1.8898141245214584
output/comparekeira-knightleyR26_11.jpg: 1.6904467227813793
output/comparekeira-knightleyR26_12.jpg: 1.8422321437593623
output/comparekeira-knightleyR26_13.jpg: 1.7729823525397417
output/comparekeira-knightleyR26_14.jpg: 1.7795240177272857
output/comparekeira-knightleyR26_15.jpg: 1.9110482284507666
output/comparekeira-knightleyR26_16.jpg: 1.8671595949702966
output/comparekeira-knightleyR26_17.jpg: 1.8768097741387164
output/comparekeira-knightleyR26_18.jpg: 1.7677248770964153
output/comparekeira-knightleyR26_19.jpg: 1.7439880148447602
output/comparekeira-knightleyR26_20.jpg: 1.9413963187411736
Fittest: output/comparekeira-knightleyR22_13.jpg 1.5938639582124225
output/comparekeira-knightleyR27_1.jpg: 1.8581207443948444
output/comparekeira-knightleyR27_2.jpg: 1.7914597084731927
output/comparekeira-knightleyR27_3.jpg: 1.8424959508336096
output/comparekeira-knightleyR27_4.jpg: 1.795725347598153
output/comparekeira-knightleyR27_5.jp

...

output/comparekeira-knightleyR222_1.jpg: 1.7105342356330016
output/comparekeira-knightleyR222_2.jpg: 1.906881814165355
output/comparekeira-knightleyR222_3.jpg: 1.886711998295194
output/comparekeira-knightleyR222_4.jpg: 1.8654692555221295
output/comparekeira-knightleyR222_5.jpg: 1.7718345900520913
output/comparekeira-knightleyR222_6.jpg: 1.693944767130434
output/comparekeira-knightleyR222_7.jpg: 1.8849440574052836
output/comparekeira-knightleyR222_8.jpg: 1.7649308632208773
output/comparekeira-knightleyR222_9.jpg: 1.8591805014634144
output/comparekeira-knightleyR222_10.jpg: 1.6884908788560269
output/comparekeira-knightleyR222_11.jpg: 1.627507983883528
output/comparekeira-knightleyR222_12.jpg: 1.7653600098172393
output/comparekeira-knightleyR222_13.jpg: 1.8402077971062993
output/comparekeira-knightleyR222_14.jpg: 1.691437552786836
output/comparekeira-knightleyR222_15.jpg: 1.9243541587870396
output/comparekeira-knightleyR222_16.jpg: 1.9137066833738379
output/comparekeira-knightleyR222_17.j

output/comparekeira-knightleyR228_11.jpg: 1.8593951328365836
output/comparekeira-knightleyR228_12.jpg: 1.8984200790027639
output/comparekeira-knightleyR228_13.jpg: 1.8066778623548896
output/comparekeira-knightleyR228_14.jpg: 1.9492972282961265
output/comparekeira-knightleyR228_15.jpg: 1.8525279983038074
output/comparekeira-knightleyR228_16.jpg: 1.8803133201625917
output/comparekeira-knightleyR228_17.jpg: 1.968575075863319
output/comparekeira-knightleyR228_18.jpg: 1.8755765090510699
output/comparekeira-knightleyR228_19.jpg: 1.7856382684407643
output/comparekeira-knightleyR228_20.jpg: 1.7112044261963884
Fittest: output/comparekeira-knightleyR110_7.jpg 1.489636925622166
output/comparekeira-knightleyR229_1.jpg: 1.8644119229425935
output/comparekeira-knightleyR229_2.jpg: 1.8130007649017184
output/comparekeira-knightleyR229_3.jpg: 1.7296055544612716
output/comparekeira-knightleyR229_4.jpg: 1.904268457924958
output/comparekeira-knightleyR229_5.jpg: 1.7093058629070044
output/comparekeira-knigh

output/comparekeira-knightleyR235_1.jpg: 1.6713599188791193
output/comparekeira-knightleyR235_2.jpg: 1.6700408892626863
output/comparekeira-knightleyR235_3.jpg: 1.8529139595447992
output/comparekeira-knightleyR235_4.jpg: 1.8352442426622342
output/comparekeira-knightleyR235_5.jpg: 1.8930300100524393
output/comparekeira-knightleyR235_6.jpg: 1.880875324941838
output/comparekeira-knightleyR235_7.jpg: 1.8250030979584086
output/comparekeira-knightleyR235_8.jpg: 1.8635479790367127
output/comparekeira-knightleyR235_9.jpg: 1.865460175907882
output/comparekeira-knightleyR235_10.jpg: 1.8966940541668242
output/comparekeira-knightleyR235_11.jpg: 1.6163660412538343
output/comparekeira-knightleyR235_12.jpg: 1.9489932692691645
output/comparekeira-knightleyR235_13.jpg: 1.7362962327892242
output/comparekeira-knightleyR235_14.jpg: 1.7406352625658026
output/comparekeira-knightleyR235_15.jpg: 1.920589267378177
output/comparekeira-knightleyR235_16.jpg: 1.750251457222714
output/comparekeira-knightleyR235_17.

output/comparekeira-knightleyR241_11.jpg: 1.8980479533190335
output/comparekeira-knightleyR241_12.jpg: 1.7396087283104975
output/comparekeira-knightleyR241_13.jpg: 1.6360323528251266
output/comparekeira-knightleyR241_14.jpg: 1.8820523427101834
output/comparekeira-knightleyR241_15.jpg: 1.855659507383432
output/comparekeira-knightleyR241_16.jpg: 1.9104096199050913
output/comparekeira-knightleyR241_17.jpg: 1.87408493467826
output/comparekeira-knightleyR241_18.jpg: 1.7016780471907524
output/comparekeira-knightleyR241_19.jpg: 1.7316378552570357
output/comparekeira-knightleyR241_20.jpg: 1.80747047059731
Fittest: output/comparekeira-knightleyR110_7.jpg 1.489636925622166
output/comparekeira-knightleyR242_1.jpg: 1.8842482998195391
output/comparekeira-knightleyR242_2.jpg: 1.84378407209771
output/comparekeira-knightleyR242_3.jpg: 1.8490019756216447
output/comparekeira-knightleyR242_4.jpg: 1.9203583282723682
output/comparekeira-knightleyR242_5.jpg: 1.8929058290539504
output/comparekeira-knightleyR

output/comparekeira-knightleyR248_1.jpg: 1.7773031628707314
output/comparekeira-knightleyR248_2.jpg: 1.7910480137419424
output/comparekeira-knightleyR248_3.jpg: 1.766019443787463
output/comparekeira-knightleyR248_4.jpg: 1.871474625845108
output/comparekeira-knightleyR248_5.jpg: 1.7171163677651862
output/comparekeira-knightleyR248_6.jpg: 1.6456283764323927
output/comparekeira-knightleyR248_7.jpg: 1.8857372035375732
output/comparekeira-knightleyR248_8.jpg: 1.8586232980523956
output/comparekeira-knightleyR248_9.jpg: 1.7180470080577275
output/comparekeira-knightleyR248_10.jpg: 1.867862351412976
output/comparekeira-knightleyR248_11.jpg: 1.9148426965342484
output/comparekeira-knightleyR248_12.jpg: 1.9509430293823997
output/comparekeira-knightleyR248_13.jpg: 1.7631670402010813
output/comparekeira-knightleyR248_14.jpg: 1.9368592556402746
output/comparekeira-knightleyR248_15.jpg: 1.848230679349919
output/comparekeira-knightleyR248_16.jpg: 1.6728099264951783
output/comparekeira-knightleyR248_17.

In [12]:
evolve('test-images/kristin_chenoweth.jpg', 'test-images/keira_knightley2.jpg', 'kristin-chenoweth','A')

Start: 1.8266409289514702
output/comparekristin-chenowethA0_1.jpg: 1.7196235962742883
output/comparekristin-chenowethA0_2.jpg: 1.6430634551341412
output/comparekristin-chenowethA0_3.jpg: 2.0204717506018617
output/comparekristin-chenowethA0_4.jpg: 1.6201231296352985
output/comparekristin-chenowethA0_5.jpg: 1.7506768615159867
output/comparekristin-chenowethA0_6.jpg: 1.9733006812730576
output/comparekristin-chenowethA0_7.jpg: 2.1159441538053416
output/comparekristin-chenowethA0_8.jpg: 2.0670742456171856
output/comparekristin-chenowethA0_9.jpg: 1.9608838671704565
output/comparekristin-chenowethA0_10.jpg: 1.6334528023675827
output/comparekristin-chenowethA0_11.jpg: 1.734206643809479
output/comparekristin-chenowethA0_12.jpg: 1.6534662812487713
output/comparekristin-chenowethA0_13.jpg: 1.6363073725308088
output/comparekristin-chenowethA0_14.jpg: 1.9752564806613746
output/comparekristin-chenowethA0_15.jpg: 1.6449934876644188
output/comparekristin-chenowethA0_16.jpg: 1.6505327066761728
output/c

output/comparekristin-chenowethA6_10.jpg: 1.6680546667486638
output/comparekristin-chenowethA6_11.jpg: 1.6678296429002586
output/comparekristin-chenowethA6_12.jpg: 1.6411455749100137
output/comparekristin-chenowethA6_13.jpg: 1.6477559386370921
output/comparekristin-chenowethA6_14.jpg: 1.7064485757026377
output/comparekristin-chenowethA6_15.jpg: 1.7052895943708504
output/comparekristin-chenowethA6_16.jpg: 1.6373491796313608
output/comparekristin-chenowethA6_17.jpg: 1.7116053402883808
output/comparekristin-chenowethA6_18.jpg: 1.7114784493760413
output/comparekristin-chenowethA6_19.jpg: 1.7083367192538705
output/comparekristin-chenowethA6_20.jpg: 1.674602767064711
Fittest: output/comparekristin-chenowethA2_19.jpg 1.5591613403110354
output/comparekristin-chenowethA7_1.jpg: 1.6298802244637018
output/comparekristin-chenowethA7_2.jpg: 1.6245955989808905
output/comparekristin-chenowethA7_3.jpg: 1.67184445507568
output/comparekristin-chenowethA7_4.jpg: 1.6683777612926107
output/comparekristin-c

output/comparekristin-chenowethA12_19.jpg: 1.6773384656361703
output/comparekristin-chenowethA12_20.jpg: 1.6963229909590969
Fittest: output/comparekristin-chenowethA2_19.jpg 1.5591613403110354
output/comparekristin-chenowethA13_1.jpg: 1.6111263375378218
output/comparekristin-chenowethA13_2.jpg: 1.6432960348752175
output/comparekristin-chenowethA13_3.jpg: 1.6393683465382707
output/comparekristin-chenowethA13_4.jpg: 1.6770786606052064
output/comparekristin-chenowethA13_5.jpg: 1.6471297049952949
output/comparekristin-chenowethA13_6.jpg: 1.6442554573285875
output/comparekristin-chenowethA13_7.jpg: 1.623200428516608
output/comparekristin-chenowethA13_8.jpg: 1.7337232677743184
output/comparekristin-chenowethA13_9.jpg: 1.6345266380645147
output/comparekristin-chenowethA13_10.jpg: 1.751437396414988
output/comparekristin-chenowethA13_11.jpg: 1.6464969509039893
output/comparekristin-chenowethA13_12.jpg: 1.6391497902364742
output/comparekristin-chenowethA13_13.jpg: 1.6027588759511873
output/compa

output/comparekristin-chenowethA19_5.jpg: 1.649402822012409
output/comparekristin-chenowethA19_6.jpg: 1.7064587160825373
output/comparekristin-chenowethA19_7.jpg: 1.641257901749737
output/comparekristin-chenowethA19_8.jpg: 1.7132530843541953
output/comparekristin-chenowethA19_9.jpg: 1.6343011443200854
output/comparekristin-chenowethA19_10.jpg: 1.709696217050582
output/comparekristin-chenowethA19_11.jpg: 1.6709454000537516
output/comparekristin-chenowethA19_12.jpg: 1.715866531293848
output/comparekristin-chenowethA19_13.jpg: 1.6419358391146992
output/comparekristin-chenowethA19_14.jpg: 1.6327893870030485
output/comparekristin-chenowethA19_15.jpg: 1.634607853783502
output/comparekristin-chenowethA19_16.jpg: 1.7075401427876917
output/comparekristin-chenowethA19_17.jpg: 1.6498013674520007
output/comparekristin-chenowethA19_18.jpg: 1.708875302924312
output/comparekristin-chenowethA19_19.jpg: 1.6321821119078574
output/comparekristin-chenowethA19_20.jpg: 1.7050342122412294
Fittest: output/com

output/comparekristin-chenowethA25_12.jpg: 1.6331589006421283
output/comparekristin-chenowethA25_13.jpg: 1.65561802150329
output/comparekristin-chenowethA25_14.jpg: 1.6493755560642378
output/comparekristin-chenowethA25_15.jpg: 1.646116222163499
output/comparekristin-chenowethA25_16.jpg: 1.6405650860849461
output/comparekristin-chenowethA25_17.jpg: 1.6483875267615593
output/comparekristin-chenowethA25_18.jpg: 1.6680216254110274
output/comparekristin-chenowethA25_19.jpg: 1.6730335260397258
output/comparekristin-chenowethA25_20.jpg: 2.042563061791231
Fittest: output/comparekristin-chenowethA2_19.jpg 1.5591613403110354
output/comparekristin-chenowethA26_1.jpg: 1.8492295714233815
output/comparekristin-chenowethA26_2.jpg: 1.6384139343039337
output/comparekristin-chenowethA26_3.jpg: 2.042206444924029
output/comparekristin-chenowethA26_4.jpg: 1.6661827124668793
output/comparekristin-chenowethA26_5.jpg: 1.6342039924529537
output/comparekristin-chenowethA26_6.jpg: 1.9077184314671003
output/compa

...

output/comparekristin-chenowethA220_6.jpg: 1.6489557758576832
output/comparekristin-chenowethA220_7.jpg: 1.546552254015261
output/comparekristin-chenowethA220_8.jpg: 1.7039287346556615
output/comparekristin-chenowethA220_9.jpg: 1.6975992834924631
output/comparekristin-chenowethA220_10.jpg: 1.7114909503538756
output/comparekristin-chenowethA220_11.jpg: 1.6427664378253564
output/comparekristin-chenowethA220_12.jpg: 1.6628615275519523
output/comparekristin-chenowethA220_13.jpg: 1.6709243903813267
output/comparekristin-chenowethA220_14.jpg: 1.6384901964982734
output/comparekristin-chenowethA220_15.jpg: 1.6966740476548992
output/comparekristin-chenowethA220_16.jpg: 1.662823686866413
output/comparekristin-chenowethA220_17.jpg: 1.6146152993485217
output/comparekristin-chenowethA220_18.jpg: 1.7225988747714114
output/comparekristin-chenowethA220_19.jpg: 1.6655827777403265
output/comparekristin-chenowethA220_20.jpg: 1.8549423848042466
Fittest: output/comparekristin-chenowethA195_6.jpg 1.47931131

output/comparekristin-chenowethA226_11.jpg: 1.9344292680608486
output/comparekristin-chenowethA226_12.jpg: 1.7094878424373265
output/comparekristin-chenowethA226_13.jpg: 1.6651113475801627
output/comparekristin-chenowethA226_14.jpg: 1.69751415249709
output/comparekristin-chenowethA226_15.jpg: 1.7081024698507095
output/comparekristin-chenowethA226_16.jpg: 1.7085628689439452
output/comparekristin-chenowethA226_17.jpg: 1.64524668802901
output/comparekristin-chenowethA226_18.jpg: 1.6983336165583538
output/comparekristin-chenowethA226_19.jpg: 1.6335196539649122
output/comparekristin-chenowethA226_20.jpg: 1.7085206946972258
Fittest: output/comparekristin-chenowethA195_6.jpg 1.4793113140869298
output/comparekristin-chenowethA227_1.jpg: 1.6281352038679453
output/comparekristin-chenowethA227_2.jpg: 1.686421496697017
output/comparekristin-chenowethA227_3.jpg: 1.6442521949575886
output/comparekristin-chenowethA227_4.jpg: 1.607209435283536
output/comparekristin-chenowethA227_5.jpg: 1.7015696799810

output/comparekristin-chenowethA232_16.jpg: 1.6174498228474392
output/comparekristin-chenowethA232_17.jpg: 1.625640064741261
output/comparekristin-chenowethA232_18.jpg: 1.6506262591213834
output/comparekristin-chenowethA232_19.jpg: 1.6689689462466402
output/comparekristin-chenowethA232_20.jpg: 1.704632876534581
Fittest: output/comparekristin-chenowethA195_6.jpg 1.4793113140869298
output/comparekristin-chenowethA233_1.jpg: 1.6988915887655587
output/comparekristin-chenowethA233_2.jpg: 1.7325599476186242
output/comparekristin-chenowethA233_3.jpg: 1.648116280475903
output/comparekristin-chenowethA233_4.jpg: 1.6993675423286398
output/comparekristin-chenowethA233_5.jpg: 1.6970729376142981
output/comparekristin-chenowethA233_6.jpg: 1.6468620609714386
output/comparekristin-chenowethA233_7.jpg: 1.5973937535513782
output/comparekristin-chenowethA233_8.jpg: 1.6312778112746569
output/comparekristin-chenowethA233_9.jpg: 1.6710377355182549
output/comparekristin-chenowethA233_10.jpg: 1.66528347291453

output/comparekristin-chenowethA239_1.jpg: 1.772329176885128
output/comparekristin-chenowethA239_2.jpg: 2.0429228529808006
output/comparekristin-chenowethA239_3.jpg: 1.627436331399413
output/comparekristin-chenowethA239_4.jpg: 1.6794121244750335
output/comparekristin-chenowethA239_5.jpg: 1.6647122008236375
output/comparekristin-chenowethA239_6.jpg: 1.635961106250626
output/comparekristin-chenowethA239_7.jpg: 1.9955885761718524
output/comparekristin-chenowethA239_8.jpg: 1.9906430066627323
output/comparekristin-chenowethA239_9.jpg: 1.6033411234793722
output/comparekristin-chenowethA239_10.jpg: 1.7086499669899786
output/comparekristin-chenowethA239_11.jpg: 1.639033196880388
output/comparekristin-chenowethA239_12.jpg: 1.7046516405510828
output/comparekristin-chenowethA239_13.jpg: 1.6622416938065567
output/comparekristin-chenowethA239_14.jpg: 1.73058904250244
output/comparekristin-chenowethA239_15.jpg: 1.6709592943142375
output/comparekristin-chenowethA239_16.jpg: 1.6461431347720263
output/

output/comparekristin-chenowethA245_6.jpg: 1.6650713822475163
output/comparekristin-chenowethA245_7.jpg: 1.7173894926483286
output/comparekristin-chenowethA245_8.jpg: 1.6428267713505533
output/comparekristin-chenowethA245_9.jpg: 1.6894094486192772
output/comparekristin-chenowethA245_10.jpg: 1.7277693518270896
output/comparekristin-chenowethA245_11.jpg: 2.048693471206956
output/comparekristin-chenowethA245_12.jpg: 1.6755520921415537
output/comparekristin-chenowethA245_13.jpg: 1.6362902431542468
output/comparekristin-chenowethA245_14.jpg: 1.6409038636004623
output/comparekristin-chenowethA245_15.jpg: 1.6744836797765776
output/comparekristin-chenowethA245_16.jpg: 1.6992154468445915
output/comparekristin-chenowethA245_17.jpg: 1.6398134040754768
output/comparekristin-chenowethA245_18.jpg: 1.6229408493122057
output/comparekristin-chenowethA245_19.jpg: 1.702661114549411
output/comparekristin-chenowethA245_20.jpg: 1.6646973219258228
Fittest: output/comparekristin-chenowethA195_6.jpg 1.47931131

In [13]:
evolve('test-images/matthew_perry.jpg', 'test-images/colin_firth.jpg', 'matthew-perry','A')

Start: 1.328649333500185
output/comparematthew-perryA0_1.jpg: 1.347471055422397
output/comparematthew-perryA0_2.jpg: 1.291904207140007
output/comparematthew-perryA0_3.jpg: 1.279476382637692
output/comparematthew-perryA0_4.jpg: 1.3313708570807676
output/comparematthew-perryA0_5.jpg: 1.2999634438700973
output/comparematthew-perryA0_6.jpg: 1.3620012427199182
output/comparematthew-perryA0_7.jpg: 1.308031675085326
output/comparematthew-perryA0_8.jpg: 1.2964537390095148
output/comparematthew-perryA0_9.jpg: 1.2741781339011928
output/comparematthew-perryA0_10.jpg: 1.2933960324681697
output/comparematthew-perryA0_11.jpg: 1.2951610467296675
output/comparematthew-perryA0_12.jpg: 1.3013139237431202
output/comparematthew-perryA0_13.jpg: 1.3121623179366364
output/comparematthew-perryA0_14.jpg: 1.3273508967062906
output/comparematthew-perryA0_15.jpg: 1.3049948950618506
output/comparematthew-perryA0_16.jpg: 1.3125183697499805
output/comparematthew-perryA0_17.jpg: 1.275527127654426
output/comparematthe

output/comparematthew-perryA6_20.jpg: 1.3506482180844335
Fittest: output/comparematthew-perryA0_9.jpg 1.2741781339011928
output/comparematthew-perryA7_1.jpg: 1.3308992632480434
output/comparematthew-perryA7_2.jpg: 1.313091143106086
output/comparematthew-perryA7_3.jpg: 1.3423858695993625
output/comparematthew-perryA7_4.jpg: 1.350023996947273
output/comparematthew-perryA7_5.jpg: 1.3229304123682937
output/comparematthew-perryA7_6.jpg: 1.3170781620218053
output/comparematthew-perryA7_7.jpg: 1.2985280298515895
output/comparematthew-perryA7_8.jpg: 1.3422941216001218
output/comparematthew-perryA7_9.jpg: 1.3355835823865951
output/comparematthew-perryA7_10.jpg: 1.3070742116999918
output/comparematthew-perryA7_11.jpg: 1.337220937961923
output/comparematthew-perryA7_12.jpg: 1.3123465076631946
output/comparematthew-perryA7_13.jpg: 1.265383970212183
output/comparematthew-perryA7_14.jpg: 1.3409305141735732
output/comparematthew-perryA7_15.jpg: 1.3409625294882754
output/comparematthew-perryA7_16.jpg:

output/comparematthew-perryA13_17.jpg: 1.2883332817785194
output/comparematthew-perryA13_18.jpg: 1.314250995324718
output/comparematthew-perryA13_19.jpg: 1.2842876670793233
output/comparematthew-perryA13_20.jpg: 1.315423795443335
Fittest: output/comparematthew-perryA13_4.jpg 1.258646234340692
output/comparematthew-perryA14_1.jpg: 1.3157444640792597
output/comparematthew-perryA14_2.jpg: 1.2961124780071898
output/comparematthew-perryA14_3.jpg: 1.287798610134641
output/comparematthew-perryA14_4.jpg: 1.341727260012421
output/comparematthew-perryA14_5.jpg: 1.3037321188003712
output/comparematthew-perryA14_6.jpg: 1.3154709453749913
output/comparematthew-perryA14_7.jpg: 1.2975744812914995
output/comparematthew-perryA14_8.jpg: 1.2846063972715998
output/comparematthew-perryA14_9.jpg: 1.2497379283533079
output/comparematthew-perryA14_10.jpg: 1.3167823447205242
output/comparematthew-perryA14_11.jpg: 1.2760083090022256
output/comparematthew-perryA14_12.jpg: 1.2701778720767152
output/comparematthew

output/comparematthew-perryA20_13.jpg: 1.2750297252757532
output/comparematthew-perryA20_14.jpg: 1.2866234617735797
output/comparematthew-perryA20_15.jpg: 1.2728477229598898
output/comparematthew-perryA20_16.jpg: 1.2699730187174403
output/comparematthew-perryA20_17.jpg: 1.3485381195520503
output/comparematthew-perryA20_18.jpg: 1.3187086643698085
output/comparematthew-perryA20_19.jpg: 1.2802169338476217
output/comparematthew-perryA20_20.jpg: 1.3145767736484646
Fittest: output/comparematthew-perryA18_4.jpg 1.2437094361901977
output/comparematthew-perryA21_1.jpg: 1.2678232828774394
output/comparematthew-perryA21_2.jpg: 1.2866191049146094
output/comparematthew-perryA21_3.jpg: 1.3117999696389486
output/comparematthew-perryA21_4.jpg: 1.2759031822999285
output/comparematthew-perryA21_5.jpg: 1.2770150938129448
output/comparematthew-perryA21_6.jpg: 1.2756759198053587
output/comparematthew-perryA21_7.jpg: 1.281522008444075
output/comparematthew-perryA21_8.jpg: 1.26018660062347
output/comparematt

output/comparematthew-perryA27_8.jpg: 1.278053258064352
output/comparematthew-perryA27_9.jpg: 1.2761893988638275
output/comparematthew-perryA27_10.jpg: 1.3038204623252783
output/comparematthew-perryA27_11.jpg: 1.279503245367382
output/comparematthew-perryA27_12.jpg: 1.3021378708817142
output/comparematthew-perryA27_13.jpg: 1.3032097350868617
output/comparematthew-perryA27_14.jpg: 1.3280234570224514
output/comparematthew-perryA27_15.jpg: 1.3051329293803624
output/comparematthew-perryA27_16.jpg: 1.350822058956946
output/comparematthew-perryA27_17.jpg: 1.2571627377999
output/comparematthew-perryA27_18.jpg: 1.2710453725675832
output/comparematthew-perryA27_19.jpg: 1.293487402796695
output/comparematthew-perryA27_20.jpg: 1.2940117601836194
Fittest: output/comparematthew-perryA18_4.jpg 1.2437094361901977
output/comparematthew-perryA28_1.jpg: 1.2951594226948107
output/comparematthew-perryA28_2.jpg: 1.297577769959092
output/comparematthew-perryA28_3.jpg: 1.2921196978160527
output/comparematthe

...

output/comparematthew-perryA222_1.jpg: 1.2925562308413452
output/comparematthew-perryA222_2.jpg: 1.2880837581082947
output/comparematthew-perryA222_3.jpg: 1.2938368575739885
output/comparematthew-perryA222_4.jpg: 1.299001111071877
output/comparematthew-perryA222_5.jpg: 1.258922373160074
output/comparematthew-perryA222_6.jpg: 1.2387955665040273
output/comparematthew-perryA222_7.jpg: 1.293890536784093
output/comparematthew-perryA222_8.jpg: 1.2938407962999938
output/comparematthew-perryA222_9.jpg: 1.3039367279293657
output/comparematthew-perryA222_10.jpg: 1.260306430893626
output/comparematthew-perryA222_11.jpg: 1.280454669160589
output/comparematthew-perryA222_12.jpg: 1.2377039319016347
output/comparematthew-perryA222_13.jpg: 1.2984384930024995
output/comparematthew-perryA222_14.jpg: 1.3465715983241333
output/comparematthew-perryA222_15.jpg: 1.2799368257106143
output/comparematthew-perryA222_16.jpg: 1.2935090402583709
output/comparematthew-perryA222_17.jpg: 1.2701295657959215
output/comp

output/comparematthew-perryA228_15.jpg: 1.2689905242845463
output/comparematthew-perryA228_16.jpg: 1.2994212566742824
output/comparematthew-perryA228_17.jpg: 1.3365885660613372
output/comparematthew-perryA228_18.jpg: 1.2960622456592068
output/comparematthew-perryA228_19.jpg: 1.3052891641344715
output/comparematthew-perryA228_20.jpg: 1.3383795219797885
Fittest: output/comparematthew-perryA178_16.jpg 1.224866627502508
output/comparematthew-perryA229_1.jpg: 1.2729188557058988
output/comparematthew-perryA229_2.jpg: 1.3032046300990687
output/comparematthew-perryA229_3.jpg: 1.29479830956484
output/comparematthew-perryA229_4.jpg: 1.3056610109379048
output/comparematthew-perryA229_5.jpg: 1.2888644392045427
output/comparematthew-perryA229_6.jpg: 1.334219225620712
output/comparematthew-perryA229_7.jpg: 1.2794710453265843
output/comparematthew-perryA229_8.jpg: 1.332626778428804
output/comparematthew-perryA229_9.jpg: 1.3227447006531956
output/comparematthew-perryA229_10.jpg: 1.2572426615704322
out

output/comparematthew-perryA235_8.jpg: 1.2831004213720565
output/comparematthew-perryA235_9.jpg: 1.3034057616855579
output/comparematthew-perryA235_10.jpg: 1.30983193978539
output/comparematthew-perryA235_11.jpg: 1.293339666051164
output/comparematthew-perryA235_12.jpg: 1.2839341354949756
output/comparematthew-perryA235_13.jpg: 1.2999266270271026
output/comparematthew-perryA235_14.jpg: 1.2682864318906528
output/comparematthew-perryA235_15.jpg: 1.3431567015730983
output/comparematthew-perryA235_16.jpg: 1.2949763594018637
output/comparematthew-perryA235_17.jpg: 1.267641923038809
output/comparematthew-perryA235_18.jpg: 1.269277283809112
output/comparematthew-perryA235_19.jpg: 1.2984872706895447
output/comparematthew-perryA235_20.jpg: 1.3026000389388876
Fittest: output/comparematthew-perryA178_16.jpg 1.224866627502508
output/comparematthew-perryA236_1.jpg: 1.2910236742447418
output/comparematthew-perryA236_2.jpg: 1.2895767002795848
output/comparematthew-perryA236_3.jpg: 1.257346380784678
o

output/comparematthew-perryA242_1.jpg: 1.3239646890928625
output/comparematthew-perryA242_2.jpg: 1.2768433360869582
output/comparematthew-perryA242_3.jpg: 1.333471217586247
output/comparematthew-perryA242_4.jpg: 1.2961755141695628
output/comparematthew-perryA242_5.jpg: 1.316500662612247
output/comparematthew-perryA242_6.jpg: 1.2779514232461644
output/comparematthew-perryA242_7.jpg: 1.2556719154151226
output/comparematthew-perryA242_8.jpg: 1.2972710832308896
output/comparematthew-perryA242_9.jpg: 1.2725019751468787
output/comparematthew-perryA242_10.jpg: 1.2870947386640652
output/comparematthew-perryA242_11.jpg: 1.280203800466809
output/comparematthew-perryA242_12.jpg: 1.3027105068074687
output/comparematthew-perryA242_13.jpg: 1.2677429039726187
output/comparematthew-perryA242_14.jpg: 1.270097441637925
output/comparematthew-perryA242_15.jpg: 1.2730104419459622
output/comparematthew-perryA242_16.jpg: 1.293065058704269
output/comparematthew-perryA242_17.jpg: 1.2853132205804672
output/comp

output/comparematthew-perryA248_15.jpg: 1.2738935005527523
output/comparematthew-perryA248_16.jpg: 1.294308638049665
output/comparematthew-perryA248_17.jpg: 1.275510894570326
output/comparematthew-perryA248_18.jpg: 1.3170147583208542
output/comparematthew-perryA248_19.jpg: 1.2813790682038908
output/comparematthew-perryA248_20.jpg: 1.2582711449204322
Fittest: output/comparematthew-perryA178_16.jpg 1.224866627502508
output/comparematthew-perryA249_1.jpg: 1.3334231449528755
output/comparematthew-perryA249_2.jpg: 1.3321566745596316
output/comparematthew-perryA249_3.jpg: 1.3341307744464022
output/comparematthew-perryA249_4.jpg: 1.2627393691747781
output/comparematthew-perryA249_5.jpg: 1.2987125988840795
output/comparematthew-perryA249_6.jpg: 1.2996671766420262
output/comparematthew-perryA249_7.jpg: 1.2690198660066307
output/comparematthew-perryA249_8.jpg: 1.3313579647501617
output/comparematthew-perryA249_9.jpg: 1.2620116614958317
output/comparematthew-perryA249_10.jpg: 1.2659977461951906
o

In [14]:
evolve('test-images/colin_firth.jpg', 'test-images/matthew_perry.jpg', 'colin-firth','A')

Start: 1.328649333500185
output/comparecolin-firthA0_1.jpg: 1.3767503994780959
output/comparecolin-firthA0_2.jpg: 1.3797134674562335
output/comparecolin-firthA0_3.jpg: 1.682096165640859
output/comparecolin-firthA0_4.jpg: 1.349057109562501
output/comparecolin-firthA0_5.jpg: 1.4632222172133154
output/comparecolin-firthA0_6.jpg: 1.467541361784421
output/comparecolin-firthA0_7.jpg: 1.3943573007777894
output/comparecolin-firthA0_8.jpg: 1.412639760016366
output/comparecolin-firthA0_9.jpg: 1.4037569261685634
output/comparecolin-firthA0_10.jpg: 1.6227754812628494
output/comparecolin-firthA0_11.jpg: 1.3140546631565488
output/comparecolin-firthA0_12.jpg: 1.577894425935201
output/comparecolin-firthA0_13.jpg: 1.2931714259045164
output/comparecolin-firthA0_14.jpg: 1.3234199199740937
output/comparecolin-firthA0_15.jpg: 1.4122165513521083
output/comparecolin-firthA0_16.jpg: 1.3617164888557025
output/comparecolin-firthA0_17.jpg: 1.3599389657959309
output/comparecolin-firthA0_18.jpg: 1.4095209966320543

output/comparecolin-firthA7_4.jpg: 1.5821694026549258
output/comparecolin-firthA7_5.jpg: 1.3299163659061715
output/comparecolin-firthA7_6.jpg: 1.2970537297414273
output/comparecolin-firthA7_7.jpg: 1.4950058314280945
output/comparecolin-firthA7_8.jpg: 1.2983650821671213
output/comparecolin-firthA7_9.jpg: 1.399162618626829
output/comparecolin-firthA7_10.jpg: 1.4563827702173189
output/comparecolin-firthA7_11.jpg: 1.4128684003504524
output/comparecolin-firthA7_12.jpg: 1.4489291886763038
output/comparecolin-firthA7_13.jpg: 1.294200625834823
output/comparecolin-firthA7_14.jpg: 1.2919145427185035
output/comparecolin-firthA7_15.jpg: 1.5088475808383337
output/comparecolin-firthA7_16.jpg: 1.408636502259166
output/comparecolin-firthA7_17.jpg: 1.4044152522294875
output/comparecolin-firthA7_18.jpg: 1.361266839050499
output/comparecolin-firthA7_19.jpg: 1.3473996987221482
output/comparecolin-firthA7_20.jpg: 1.5205145275420153
Fittest: output/comparecolin-firthA6_3.jpg 1.1476847840030735
output/compar

output/comparecolin-firthA14_6.jpg: 1.3174835820195334
output/comparecolin-firthA14_7.jpg: 1.2833633837069813
output/comparecolin-firthA14_8.jpg: 1.2938705732601408
output/comparecolin-firthA14_9.jpg: 1.4563635323855708
output/comparecolin-firthA14_10.jpg: 1.3110992550341691
output/comparecolin-firthA14_11.jpg: 1.5289184288967803
output/comparecolin-firthA14_12.jpg: 1.3839270747685144
output/comparecolin-firthA14_13.jpg: 1.3708492762966802
output/comparecolin-firthA14_14.jpg: 1.5227682190662408
output/comparecolin-firthA14_15.jpg: 1.4583079246666428
output/comparecolin-firthA14_16.jpg: 1.3475008386112202
output/comparecolin-firthA14_17.jpg: 1.58095836493009
output/comparecolin-firthA14_18.jpg: 1.3449915731046487
output/comparecolin-firthA14_19.jpg: 1.293822712030649
output/comparecolin-firthA14_20.jpg: 1.4909594226577905
Fittest: output/comparecolin-firthA6_3.jpg 1.1476847840030735
output/comparecolin-firthA15_1.jpg: 1.4764364349673604
output/comparecolin-firthA15_2.jpg: 1.303563517487

output/comparecolin-firthA21_7.jpg: 1.383741946907266
output/comparecolin-firthA21_8.jpg: 1.410710400000931
output/comparecolin-firthA21_9.jpg: 1.4625126712698864
output/comparecolin-firthA21_10.jpg: 1.429233653963395
output/comparecolin-firthA21_11.jpg: 1.3591895399864597
output/comparecolin-firthA21_12.jpg: 1.4119729186237095
output/comparecolin-firthA21_13.jpg: 1.4162658719518446
output/comparecolin-firthA21_14.jpg: 1.394031619665952
output/comparecolin-firthA21_15.jpg: 1.4496255145893326
output/comparecolin-firthA21_16.jpg: 1.4016706394334606
output/comparecolin-firthA21_17.jpg: 1.3798207324110012
output/comparecolin-firthA21_18.jpg: 1.4470865980920518
output/comparecolin-firthA21_19.jpg: 1.4657145833186254
output/comparecolin-firthA21_20.jpg: 1.3502985558236649
Fittest: output/comparecolin-firthA6_3.jpg 1.1476847840030735
output/comparecolin-firthA22_1.jpg: 1.3060456585823106
output/comparecolin-firthA22_2.jpg: 1.4205089852536312
output/comparecolin-firthA22_3.jpg: 1.5304533120786

output/comparecolin-firthA28_8.jpg: 1.6730262213061557
output/comparecolin-firthA28_9.jpg: 1.4115518194490273
output/comparecolin-firthA28_10.jpg: 1.467952335386256
output/comparecolin-firthA28_11.jpg: 1.4266993608984957
output/comparecolin-firthA28_12.jpg: 1.4668368281739155
output/comparecolin-firthA28_13.jpg: 1.4652576329382732
output/comparecolin-firthA28_14.jpg: 1.45729689228187
output/comparecolin-firthA28_15.jpg: 1.4463595790270616
output/comparecolin-firthA28_16.jpg: 1.382461962890899
output/comparecolin-firthA28_17.jpg: 1.2569663478213906
output/comparecolin-firthA28_18.jpg: 1.4750440718102846
output/comparecolin-firthA28_19.jpg: 1.3698514559489245
output/comparecolin-firthA28_20.jpg: 1.5034721348256648
Fittest: output/comparecolin-firthA6_3.jpg 1.1476847840030735
output/comparecolin-firthA29_1.jpg: 1.498844422670148
output/comparecolin-firthA29_2.jpg: 1.2505209548730731
output/comparecolin-firthA29_3.jpg: 1.65045578355475
output/comparecolin-firthA29_4.jpg: 1.3176816199294383

...

output/comparecolin-firthA216_4.jpg: 1.0920039948320295
output/comparecolin-firthA216_5.jpg: 1.352193683951798
output/comparecolin-firthA216_6.jpg: 1.5362007693460131
output/comparecolin-firthA216_7.jpg: 1.3465932110605126
output/comparecolin-firthA216_8.jpg: 1.4136108688731144
output/comparecolin-firthA216_9.jpg: 1.2803576395933245
output/comparecolin-firthA216_10.jpg: 1.5316364781236957
output/comparecolin-firthA216_11.jpg: 1.3685389690216279
output/comparecolin-firthA216_12.jpg: 1.3796883878476587
output/comparecolin-firthA216_13.jpg: 1.540684178527088
output/comparecolin-firthA216_14.jpg: 1.4428976953987447
output/comparecolin-firthA216_15.jpg: 1.2690060619018322
output/comparecolin-firthA216_16.jpg: 1.3221786868783898
output/comparecolin-firthA216_17.jpg: 1.486708168745573
output/comparecolin-firthA216_18.jpg: 1.3362957739768628
output/comparecolin-firthA216_19.jpg: 1.5553593346401686
output/comparecolin-firthA216_20.jpg: 1.5145261660247895
Fittest: output/comparecolin-firthA169_1

output/comparecolin-firthA223_2.jpg: 1.4666932869419629
output/comparecolin-firthA223_3.jpg: 1.5727005584981628
output/comparecolin-firthA223_4.jpg: 1.325925616874421
output/comparecolin-firthA223_5.jpg: 1.4395357615613125
output/comparecolin-firthA223_6.jpg: 1.3157083986127418
output/comparecolin-firthA223_7.jpg: 1.3394600760578816
output/comparecolin-firthA223_8.jpg: 1.4113643176269286
output/comparecolin-firthA223_9.jpg: 1.4875693505772491
output/comparecolin-firthA223_10.jpg: 1.4412641380655122
output/comparecolin-firthA223_11.jpg: 1.4885617009457164
output/comparecolin-firthA223_12.jpg: 1.4011510714060518
output/comparecolin-firthA223_13.jpg: 1.404235884290219
output/comparecolin-firthA223_14.jpg: 1.36390492794371
output/comparecolin-firthA223_15.jpg: 1.4570255329981552
output/comparecolin-firthA223_16.jpg: 1.2937961568029706
output/comparecolin-firthA223_17.jpg: 1.3428723690827202
output/comparecolin-firthA223_18.jpg: 1.406337380072314
output/comparecolin-firthA223_19.jpg: 1.4558

output/comparecolin-firthA230_1.jpg: 1.3763931372969118
output/comparecolin-firthA230_2.jpg: 1.4952925248186195
output/comparecolin-firthA230_3.jpg: 1.287411776601228
output/comparecolin-firthA230_4.jpg: 1.2608130048772945
output/comparecolin-firthA230_5.jpg: 1.4099064536020416
output/comparecolin-firthA230_6.jpg: 1.35053910054257
output/comparecolin-firthA230_7.jpg: 1.4163785068890082
output/comparecolin-firthA230_8.jpg: 1.3396410300955433
output/comparecolin-firthA230_9.jpg: 1.4530962639101428
output/comparecolin-firthA230_10.jpg: 1.5009282141230822
output/comparecolin-firthA230_11.jpg: 1.2984848757522687
output/comparecolin-firthA230_12.jpg: 1.0398425378277625
output/comparecolin-firthA230_13.jpg: 1.415848148411604
output/comparecolin-firthA230_14.jpg: 1.4083847025173333
output/comparecolin-firthA230_15.jpg: 1.4805014372117562
output/comparecolin-firthA230_16.jpg: 1.4515076380662806
output/comparecolin-firthA230_17.jpg: 1.2610485577846064
output/comparecolin-firthA230_18.jpg: 1.3085

output/comparecolin-firthA236_20.jpg: 1.346359902173736
Fittest: output/comparecolin-firthA169_18.jpg 0.9641072720104851
output/comparecolin-firthA237_1.jpg: 1.340880382672026
output/comparecolin-firthA237_2.jpg: 1.45425435175062
output/comparecolin-firthA237_3.jpg: 1.4174208716893797
output/comparecolin-firthA237_4.jpg: 1.4248046778506667
output/comparecolin-firthA237_5.jpg: 1.4562698299724013
output/comparecolin-firthA237_6.jpg: 1.5132869911244327
output/comparecolin-firthA237_7.jpg: 1.3534163429286181
output/comparecolin-firthA237_8.jpg: 1.2289019350869284
output/comparecolin-firthA237_9.jpg: 1.4993145863555897
output/comparecolin-firthA237_10.jpg: 1.459019524147491
output/comparecolin-firthA237_11.jpg: 1.4273743666978296
output/comparecolin-firthA237_12.jpg: 1.584493018504085
output/comparecolin-firthA237_13.jpg: 1.4732432476257435
output/comparecolin-firthA237_14.jpg: 1.2483891825487219
output/comparecolin-firthA237_15.jpg: 1.3552063688516451
output/comparecolin-firthA237_16.jpg: 

output/comparecolin-firthA243_18.jpg: 1.2613309794624996
output/comparecolin-firthA243_19.jpg: 1.5256989097678768
output/comparecolin-firthA243_20.jpg: 1.2936872432616577
Fittest: output/comparecolin-firthA169_18.jpg 0.9641072720104851
output/comparecolin-firthA244_1.jpg: 1.337120295575533
output/comparecolin-firthA244_2.jpg: 1.629419042778454
output/comparecolin-firthA244_3.jpg: 1.3202054028734889
output/comparecolin-firthA244_4.jpg: 1.3535583369926851
output/comparecolin-firthA244_5.jpg: 1.3703889968420495
output/comparecolin-firthA244_6.jpg: 1.5206277275137037
output/comparecolin-firthA244_7.jpg: 1.3982982665843822
output/comparecolin-firthA244_8.jpg: 1.5092214653710507
output/comparecolin-firthA244_9.jpg: 1.4004700504508185
output/comparecolin-firthA244_10.jpg: 1.334967440301067
output/comparecolin-firthA244_11.jpg: 1.4897665346261397
output/comparecolin-firthA244_12.jpg: 1.5388728660860644
output/comparecolin-firthA244_13.jpg: 1.388949444004469
output/comparecolin-firthA244_14.jpg

In [15]:
evolve('test-images/kristin_chenoweth.jpg', 'test-images/colin_firth.jpg', 'kristin-chenoweth','B')

Start: 2.067845383707371
output/comparekristin-chenowethB0_1.jpg: 2.1217349274164965
output/comparekristin-chenowethB0_2.jpg: 2.0163145301401335
output/comparekristin-chenowethB0_3.jpg: 2.154818918381883
output/comparekristin-chenowethB0_4.jpg: 1.9829296893394686
output/comparekristin-chenowethB0_5.jpg: 1.9681846161950314
output/comparekristin-chenowethB0_6.jpg: 1.967272022328217
output/comparekristin-chenowethB0_7.jpg: 2.0688477354268318
output/comparekristin-chenowethB0_8.jpg: 1.9012770651935842
output/comparekristin-chenowethB0_9.jpg: 2.0302937478134884
output/comparekristin-chenowethB0_10.jpg: 1.9315292322241637
output/comparekristin-chenowethB0_11.jpg: 2.0017462890121718
output/comparekristin-chenowethB0_12.jpg: 2.0608326255037364
output/comparekristin-chenowethB0_13.jpg: 1.97978515332344
output/comparekristin-chenowethB0_14.jpg: 1.893981731480784
output/comparekristin-chenowethB0_15.jpg: 1.94045871875241
output/comparekristin-chenowethB0_16.jpg: 1.9475987779914672
output/comparek

output/comparekristin-chenowethB6_10.jpg: 2.0570129333804426
output/comparekristin-chenowethB6_11.jpg: 1.9769463999612547
output/comparekristin-chenowethB6_12.jpg: 1.9824747370463358
output/comparekristin-chenowethB6_13.jpg: 1.9098300510233295
output/comparekristin-chenowethB6_14.jpg: 1.9948021168162384
output/comparekristin-chenowethB6_15.jpg: 2.0896138331510974
output/comparekristin-chenowethB6_16.jpg: 2.0526640282858337
output/comparekristin-chenowethB6_17.jpg: 2.113016083830828
output/comparekristin-chenowethB6_18.jpg: 1.9257662036654357
output/comparekristin-chenowethB6_19.jpg: 2.1586254032717545
output/comparekristin-chenowethB6_20.jpg: 1.9036533840869703
Fittest: output/comparekristin-chenowethB4_19.jpg 1.7681074260263503
output/comparekristin-chenowethB7_1.jpg: 1.9261475944250126
output/comparekristin-chenowethB7_2.jpg: 1.973547526205819
output/comparekristin-chenowethB7_3.jpg: 1.7548072220202393
output/comparekristin-chenowethB7_4.jpg: 1.9043082478343143
output/comparekristin-

output/comparekristin-chenowethB12_19.jpg: 2.0115273756592815
output/comparekristin-chenowethB12_20.jpg: 2.12327300701729
Fittest: output/comparekristin-chenowethB7_3.jpg 1.7548072220202393
output/comparekristin-chenowethB13_1.jpg: 1.928816015816302
output/comparekristin-chenowethB13_2.jpg: 2.0490765198646557
output/comparekristin-chenowethB13_3.jpg: 1.8183400927667752
output/comparekristin-chenowethB13_4.jpg: 1.9226085503345594
output/comparekristin-chenowethB13_5.jpg: 1.928542675107885
output/comparekristin-chenowethB13_6.jpg: 1.9242455616864893
output/comparekristin-chenowethB13_7.jpg: 1.8919900687553297
output/comparekristin-chenowethB13_8.jpg: 1.9232130706790636
output/comparekristin-chenowethB13_9.jpg: 1.9252648280363553
output/comparekristin-chenowethB13_10.jpg: 2.0593104452013717
output/comparekristin-chenowethB13_11.jpg: 1.9885922392814173
output/comparekristin-chenowethB13_12.jpg: 1.802870859791491
output/comparekristin-chenowethB13_13.jpg: 1.8978717484085104
output/comparekr

output/comparekristin-chenowethB19_5.jpg: 1.9057001902669695
output/comparekristin-chenowethB19_6.jpg: 2.0389991028619603
output/comparekristin-chenowethB19_7.jpg: 1.8934523635053022
output/comparekristin-chenowethB19_8.jpg: 1.8401742568221944
output/comparekristin-chenowethB19_9.jpg: 1.9434367019949947
output/comparekristin-chenowethB19_10.jpg: 2.115045777700961
output/comparekristin-chenowethB19_11.jpg: 1.9308538566295652
output/comparekristin-chenowethB19_12.jpg: 1.947432809217411
output/comparekristin-chenowethB19_13.jpg: 1.8562438124374336
output/comparekristin-chenowethB19_14.jpg: 2.158627457476399
output/comparekristin-chenowethB19_15.jpg: 1.8860061144878077
output/comparekristin-chenowethB19_16.jpg: 1.9901086114363005
output/comparekristin-chenowethB19_17.jpg: 1.9228265797065984
output/comparekristin-chenowethB19_18.jpg: 1.9427695792817987
output/comparekristin-chenowethB19_19.jpg: 1.8302281086079233
output/comparekristin-chenowethB19_20.jpg: 1.9277931781942823
Fittest: output/

output/comparekristin-chenowethB25_13.jpg: 1.9985394387126874
output/comparekristin-chenowethB25_14.jpg: 1.9095760713205996
output/comparekristin-chenowethB25_15.jpg: 1.922890501901633
output/comparekristin-chenowethB25_16.jpg: 1.985615143188387
output/comparekristin-chenowethB25_17.jpg: 2.009270158410544
output/comparekristin-chenowethB25_18.jpg: 1.928821526979233
output/comparekristin-chenowethB25_19.jpg: 2.007749611428373
output/comparekristin-chenowethB25_20.jpg: 1.990423733761335
Fittest: output/comparekristin-chenowethB7_3.jpg 1.7548072220202393
output/comparekristin-chenowethB26_1.jpg: 1.9702181244597288
output/comparekristin-chenowethB26_2.jpg: 2.0099782416768757
output/comparekristin-chenowethB26_3.jpg: 1.8382062489500561
output/comparekristin-chenowethB26_4.jpg: 1.8865839133290816
output/comparekristin-chenowethB26_5.jpg: 1.9641721159028471
output/comparekristin-chenowethB26_6.jpg: 1.9283644135192721
output/comparekristin-chenowethB26_7.jpg: 1.8619942616608327
output/comparek

...

output/comparekristin-chenowethB220_17.jpg: 1.8977746373249738
output/comparekristin-chenowethB220_18.jpg: 1.9198230629765685
output/comparekristin-chenowethB220_19.jpg: 1.8820171703235578
output/comparekristin-chenowethB220_20.jpg: 1.9057035812046668
Fittest: output/comparekristin-chenowethB169_4.jpg 1.7294218539518462
output/comparekristin-chenowethB221_1.jpg: 1.8891328815923112
output/comparekristin-chenowethB221_2.jpg: 1.895343157271634
output/comparekristin-chenowethB221_3.jpg: 1.7846613332879218
output/comparekristin-chenowethB221_4.jpg: 1.9324797390200557
output/comparekristin-chenowethB221_5.jpg: 1.8921412971274258
output/comparekristin-chenowethB221_6.jpg: 1.942299812309928
output/comparekristin-chenowethB221_7.jpg: 1.981469879031754
output/comparekristin-chenowethB221_8.jpg: 1.8740447356201237
output/comparekristin-chenowethB221_9.jpg: 1.832700755375083
output/comparekristin-chenowethB221_10.jpg: 2.020835704632962
output/comparekristin-chenowethB221_11.jpg: 1.9254002730435456

output/comparekristin-chenowethB227_1.jpg: 2.148459720498929
output/comparekristin-chenowethB227_2.jpg: 1.8656181897845305
output/comparekristin-chenowethB227_3.jpg: 2.0979976523085337
output/comparekristin-chenowethB227_4.jpg: 1.9546479243261792
output/comparekristin-chenowethB227_5.jpg: 1.8555111528230546
output/comparekristin-chenowethB227_6.jpg: 1.9017390472687876
output/comparekristin-chenowethB227_7.jpg: 1.8898016906423494
output/comparekristin-chenowethB227_8.jpg: 1.8938938034175514
output/comparekristin-chenowethB227_9.jpg: 1.8975646033980946
output/comparekristin-chenowethB227_10.jpg: 2.158973851997866
output/comparekristin-chenowethB227_11.jpg: 1.931654095255298
output/comparekristin-chenowethB227_12.jpg: 1.8914606419961426
output/comparekristin-chenowethB227_13.jpg: 1.8815557903803186
output/comparekristin-chenowethB227_14.jpg: 1.7874434306144327
output/comparekristin-chenowethB227_15.jpg: 1.9313711498770028
output/comparekristin-chenowethB227_16.jpg: 1.9021988101502334
outp

output/comparekristin-chenowethB233_6.jpg: 1.957929600073684
output/comparekristin-chenowethB233_7.jpg: 1.9743702985310332
output/comparekristin-chenowethB233_8.jpg: 1.8906450626801314
output/comparekristin-chenowethB233_9.jpg: 1.869200139835645
output/comparekristin-chenowethB233_10.jpg: 1.8161467071490516
output/comparekristin-chenowethB233_11.jpg: 1.988810277418446
output/comparekristin-chenowethB233_12.jpg: 1.9650778147959242
output/comparekristin-chenowethB233_13.jpg: 1.8797859068642704
output/comparekristin-chenowethB233_14.jpg: 1.9922253614908443
output/comparekristin-chenowethB233_15.jpg: 1.8030641122695583
output/comparekristin-chenowethB233_16.jpg: 1.8898481435850074
output/comparekristin-chenowethB233_17.jpg: 2.028618154642415
output/comparekristin-chenowethB233_18.jpg: 1.9875431990642722
output/comparekristin-chenowethB233_19.jpg: 1.7720974844084618
output/comparekristin-chenowethB233_20.jpg: 2.120360392690576
Fittest: output/comparekristin-chenowethB169_4.jpg 1.72942185395

output/comparekristin-chenowethB239_11.jpg: 2.1201046894270457
output/comparekristin-chenowethB239_12.jpg: 1.8153465270734814
output/comparekristin-chenowethB239_13.jpg: 1.9780701609507183
output/comparekristin-chenowethB239_14.jpg: 1.8325990975517463
output/comparekristin-chenowethB239_15.jpg: 1.9477870688393153
output/comparekristin-chenowethB239_16.jpg: 1.9730424417302612
output/comparekristin-chenowethB239_17.jpg: 1.9389058743488405
output/comparekristin-chenowethB239_18.jpg: 1.9767881027836638
output/comparekristin-chenowethB239_19.jpg: 1.903425805400937
output/comparekristin-chenowethB239_20.jpg: 1.9056782097094702
Fittest: output/comparekristin-chenowethB169_4.jpg 1.7294218539518462
output/comparekristin-chenowethB240_1.jpg: 1.8190115414425212
output/comparekristin-chenowethB240_2.jpg: 1.881814035156701
output/comparekristin-chenowethB240_3.jpg: 2.0525158632440244
output/comparekristin-chenowethB240_4.jpg: 1.88405648853097
output/comparekristin-chenowethB240_5.jpg: 1.87187719061

output/comparekristin-chenowethB245_16.jpg: 1.954990189659486
output/comparekristin-chenowethB245_17.jpg: 1.9548033277410437
output/comparekristin-chenowethB245_18.jpg: 1.9749421698910647
output/comparekristin-chenowethB245_19.jpg: 1.9034514695578735
output/comparekristin-chenowethB245_20.jpg: 1.7901849493361768
Fittest: output/comparekristin-chenowethB169_4.jpg 1.7294218539518462
output/comparekristin-chenowethB246_1.jpg: 1.9321685191090978
output/comparekristin-chenowethB246_2.jpg: 1.9302312130828463
output/comparekristin-chenowethB246_3.jpg: 2.1168975223888866
output/comparekristin-chenowethB246_4.jpg: 1.9258054528228425
output/comparekristin-chenowethB246_5.jpg: 1.8810229666044807
output/comparekristin-chenowethB246_6.jpg: 2.037722644570569
output/comparekristin-chenowethB246_7.jpg: 1.8934264757438743
output/comparekristin-chenowethB246_8.jpg: 1.891173721929715
output/comparekristin-chenowethB246_9.jpg: 1.8797426327529134
output/comparekristin-chenowethB246_10.jpg: 1.84246122547971

In [11]:
evolve('test-images/colin_firth.jpg', 'test-images/kristin_chenoweth.jpg', 'colin-firth','R')

Start: 2.067845383707371
output/comparecolin-firthR0_1.jpg: 1.8976404267128713
output/comparecolin-firthR0_2.jpg: 2.047638214654034
output/comparecolin-firthR0_3.jpg: 1.9537374017712787
output/comparecolin-firthR0_4.jpg: 1.988163653380393
output/comparecolin-firthR0_5.jpg: 1.8000672269225375
output/comparecolin-firthR0_6.jpg: 2.053507196012083
output/comparecolin-firthR0_7.jpg: 1.9666795777273505
output/comparecolin-firthR0_8.jpg: 1.9023041380680705
output/comparecolin-firthR0_9.jpg: 1.741438612484546
output/comparecolin-firthR0_10.jpg: 2.0442710547483847
output/comparecolin-firthR0_11.jpg: 1.863744602994235
output/comparecolin-firthR0_12.jpg: 2.034898358096425
output/comparecolin-firthR0_13.jpg: 1.7259410097852728
output/comparecolin-firthR0_14.jpg: 2.0355647670862993
output/comparecolin-firthR0_15.jpg: 1.7913309116738105
output/comparecolin-firthR0_16.jpg: 1.801933302688718
output/comparecolin-firthR0_17.jpg: 1.8338532941902543
output/comparecolin-firthR0_18.jpg: 1.9389712383652198
o

output/comparecolin-firthR7_4.jpg: 1.924917058378897
output/comparecolin-firthR7_5.jpg: 1.957934151419539
output/comparecolin-firthR7_6.jpg: 1.8177560015071688
output/comparecolin-firthR7_7.jpg: 1.8021306166531088
output/comparecolin-firthR7_8.jpg: 1.9363736190339371
output/comparecolin-firthR7_9.jpg: 1.8791374566923564
output/comparecolin-firthR7_10.jpg: 1.778033479695198
output/comparecolin-firthR7_11.jpg: 1.8087821297332738
output/comparecolin-firthR7_12.jpg: 1.722893934122247
output/comparecolin-firthR7_13.jpg: 1.947933713434444
output/comparecolin-firthR7_14.jpg: 1.7874696292778611
output/comparecolin-firthR7_15.jpg: 1.8098708844528726
output/comparecolin-firthR7_16.jpg: 1.8947110690501459
output/comparecolin-firthR7_17.jpg: 1.711784745585879
output/comparecolin-firthR7_18.jpg: 2.0241756132760744
output/comparecolin-firthR7_19.jpg: 1.8583745525909656
output/comparecolin-firthR7_20.jpg: 1.887617686309377
Fittest: output/comparecolin-firthR6_17.jpg 1.670490776676738
output/compareco

output/comparecolin-firthR14_6.jpg: 1.9012622047221839
output/comparecolin-firthR14_7.jpg: 1.8970446524896203
output/comparecolin-firthR14_8.jpg: 1.649848268189766
output/comparecolin-firthR14_9.jpg: 1.9068326258332358
output/comparecolin-firthR14_10.jpg: 1.769827042217912
output/comparecolin-firthR14_11.jpg: 1.7085007008259896
output/comparecolin-firthR14_12.jpg: 1.8520547238990246
output/comparecolin-firthR14_13.jpg: 1.7133553414164335
output/comparecolin-firthR14_14.jpg: 1.8361361751052865
output/comparecolin-firthR14_15.jpg: 1.9426394517133634
output/comparecolin-firthR14_16.jpg: 1.8071051520702324
output/comparecolin-firthR14_17.jpg: 1.9358536171618421
output/comparecolin-firthR14_18.jpg: 1.8533331128918737
output/comparecolin-firthR14_19.jpg: 1.7896802148484365
output/comparecolin-firthR14_20.jpg: 1.726845307731014
Fittest: output/comparecolin-firthR8_20.jpg 1.565020782726001
output/comparecolin-firthR15_1.jpg: 1.6874034657622397
output/comparecolin-firthR15_2.jpg: 1.706369447949

output/comparecolin-firthR21_7.jpg: 1.909233729133085
output/comparecolin-firthR21_8.jpg: 1.9515972297672761
output/comparecolin-firthR21_9.jpg: 1.885568375396013
output/comparecolin-firthR21_10.jpg: 1.8155451396780546
output/comparecolin-firthR21_11.jpg: 1.829729932330364
output/comparecolin-firthR21_12.jpg: 1.6198729504690494
output/comparecolin-firthR21_13.jpg: 1.78643752076036
output/comparecolin-firthR21_14.jpg: 1.8310376802898247
output/comparecolin-firthR21_15.jpg: 1.8071521410550404
output/comparecolin-firthR21_16.jpg: 1.853467398984694
output/comparecolin-firthR21_17.jpg: 1.859712253162946
output/comparecolin-firthR21_18.jpg: 1.8812460666407538
output/comparecolin-firthR21_19.jpg: 1.9266916751507246
output/comparecolin-firthR21_20.jpg: 1.925650900720572
Fittest: output/comparecolin-firthR8_20.jpg 1.565020782726001
output/comparecolin-firthR22_1.jpg: 1.8963273635381401
output/comparecolin-firthR22_2.jpg: 1.8635296401655728
output/comparecolin-firthR22_3.jpg: 1.9866461659174548


output/comparecolin-firthR28_8.jpg: 1.7488417996269967
output/comparecolin-firthR28_9.jpg: 1.8781818283806135
output/comparecolin-firthR28_10.jpg: 1.828446281318138
output/comparecolin-firthR28_11.jpg: 1.8353869392488866
output/comparecolin-firthR28_12.jpg: 1.8092747024839908
output/comparecolin-firthR28_13.jpg: 1.8550700301845955
output/comparecolin-firthR28_14.jpg: 1.7575577803258353
output/comparecolin-firthR28_15.jpg: 1.8897282819048593
output/comparecolin-firthR28_16.jpg: 1.966475892877677
output/comparecolin-firthR28_17.jpg: 1.7845908435916185
output/comparecolin-firthR28_18.jpg: 1.7668395257782668
output/comparecolin-firthR28_19.jpg: 1.7530559640203909
output/comparecolin-firthR28_20.jpg: 1.9013460533402209
Fittest: output/comparecolin-firthR8_20.jpg 1.565020782726001
output/comparecolin-firthR29_1.jpg: 1.9048422216218865
output/comparecolin-firthR29_2.jpg: 1.874497613884146
output/comparecolin-firthR29_3.jpg: 1.7645852256485066
output/comparecolin-firthR29_4.jpg: 1.701994451647

...

output/comparecolin-firthR216_10.jpg: 1.6946381472413294
output/comparecolin-firthR216_11.jpg: 1.7643088651160275
output/comparecolin-firthR216_12.jpg: 1.8860634382497323
output/comparecolin-firthR216_13.jpg: 1.7898769804735633
output/comparecolin-firthR216_14.jpg: 1.7678247163538505
output/comparecolin-firthR216_15.jpg: 1.8043654656417434
output/comparecolin-firthR216_16.jpg: 1.8455092863508358
output/comparecolin-firthR216_17.jpg: 1.8532981901450323
output/comparecolin-firthR216_18.jpg: 2.073399631120883
output/comparecolin-firthR216_19.jpg: 1.7790354417302772
output/comparecolin-firthR216_20.jpg: 1.759504392119711
Fittest: output/comparecolin-firthR8_20.jpg 1.565020782726001
output/comparecolin-firthR217_1.jpg: 1.926188388542201
output/comparecolin-firthR217_2.jpg: 1.8557396204202208
output/comparecolin-firthR217_3.jpg: 1.7621836894871032
output/comparecolin-firthR217_4.jpg: 1.8027229876737596
output/comparecolin-firthR217_5.jpg: 1.6610998409339504
output/comparecolin-firthR217_6.jp

output/comparecolin-firthR223_8.jpg: 1.8352470527313676
output/comparecolin-firthR223_9.jpg: 1.8996875408910312
output/comparecolin-firthR223_10.jpg: 1.7938198682222435
output/comparecolin-firthR223_11.jpg: 1.721975976182595
output/comparecolin-firthR223_12.jpg: 1.8369182337319514
output/comparecolin-firthR223_13.jpg: 1.7580648366725227
output/comparecolin-firthR223_14.jpg: 1.843993155291416
output/comparecolin-firthR223_15.jpg: 1.9288628832773944
output/comparecolin-firthR223_16.jpg: 1.8423943060942425
output/comparecolin-firthR223_17.jpg: 1.7578165775887165
output/comparecolin-firthR223_18.jpg: 1.750385177951635
output/comparecolin-firthR223_19.jpg: 1.8078489333907408
output/comparecolin-firthR223_20.jpg: 1.9888012078243782
Fittest: output/comparecolin-firthR8_20.jpg 1.565020782726001
output/comparecolin-firthR224_1.jpg: 1.7271981818464819
output/comparecolin-firthR224_2.jpg: 1.7670182396969465
output/comparecolin-firthR224_3.jpg: 1.8897546867148922
output/comparecolin-firthR224_4.jp

output/comparecolin-firthR230_6.jpg: 1.8051853712679475
output/comparecolin-firthR230_7.jpg: 1.7597616419156858
output/comparecolin-firthR230_8.jpg: 1.8654002200967672
output/comparecolin-firthR230_9.jpg: 1.7856998075977504
output/comparecolin-firthR230_10.jpg: 1.7545035442940395
output/comparecolin-firthR230_11.jpg: 1.9537062709617077
output/comparecolin-firthR230_12.jpg: 1.7988456797086045
output/comparecolin-firthR230_13.jpg: 1.802714175302125
output/comparecolin-firthR230_14.jpg: 1.779492887091442
output/comparecolin-firthR230_15.jpg: 1.7971171445973289
output/comparecolin-firthR230_16.jpg: 1.9379770666650493
output/comparecolin-firthR230_17.jpg: 1.8884304930929465
output/comparecolin-firthR230_18.jpg: 1.8419807002909045
output/comparecolin-firthR230_19.jpg: 1.790464172079878
output/comparecolin-firthR230_20.jpg: 1.920344642199047
Fittest: output/comparecolin-firthR8_20.jpg 1.565020782726001
output/comparecolin-firthR231_1.jpg: 1.8375357849884806
output/comparecolin-firthR231_2.jpg

output/comparecolin-firthR237_4.jpg: 1.8779672967821692
output/comparecolin-firthR237_5.jpg: 1.7663267460477128
output/comparecolin-firthR237_6.jpg: 2.0144522057587366
output/comparecolin-firthR237_7.jpg: 1.6400152234074477
output/comparecolin-firthR237_8.jpg: 1.8390041059606208
output/comparecolin-firthR237_9.jpg: 1.9026623336635846
output/comparecolin-firthR237_10.jpg: 1.7170264653133773
output/comparecolin-firthR237_11.jpg: 1.7788910445748498
output/comparecolin-firthR237_12.jpg: 1.5810384657098508
output/comparecolin-firthR237_13.jpg: 1.7330607655661945
output/comparecolin-firthR237_14.jpg: 1.8486947684575563
output/comparecolin-firthR237_15.jpg: 1.9089630225709282
output/comparecolin-firthR237_16.jpg: 1.8776582397315418
output/comparecolin-firthR237_17.jpg: 1.9625093784128822
output/comparecolin-firthR237_18.jpg: 1.9432633187162467
output/comparecolin-firthR237_19.jpg: 1.7766995624355224
output/comparecolin-firthR237_20.jpg: 1.7334639520172472
Fittest: output/comparecolin-firthR8_

output/comparecolin-firthR244_2.jpg: 1.937829013981929
output/comparecolin-firthR244_3.jpg: 1.879350037854999
output/comparecolin-firthR244_4.jpg: 1.8556601174496414
output/comparecolin-firthR244_5.jpg: 1.8847119351630033
output/comparecolin-firthR244_6.jpg: 1.8185641103433579
output/comparecolin-firthR244_7.jpg: 1.7008692006912622
output/comparecolin-firthR244_8.jpg: 1.8378249726136688
output/comparecolin-firthR244_9.jpg: 1.7070894133124024
output/comparecolin-firthR244_10.jpg: 1.9336209406361933
output/comparecolin-firthR244_11.jpg: 1.7401807343545537
output/comparecolin-firthR244_12.jpg: 1.947288885864328
output/comparecolin-firthR244_13.jpg: 1.823215311136318
output/comparecolin-firthR244_14.jpg: 1.685822547201497
output/comparecolin-firthR244_15.jpg: 1.9165562707098345
output/comparecolin-firthR244_16.jpg: 1.8959400468087153
output/comparecolin-firthR244_17.jpg: 1.6640221645678164
output/comparecolin-firthR244_18.jpg: 1.7152994888556012
output/comparecolin-firthR244_19.jpg: 1.8940

In [6]:
evolve('test-images/tatyana_ali.jpg', 'test-images/samuel_jackson.jpg', 'tatyana-ali','A')

Start: 1.7517779051410356
output/comparetatyana-aliA0_1.jpg: 2.0110898146680762
output/comparetatyana-aliA0_2.jpg: 1.9711409511639437
output/comparetatyana-aliA0_3.jpg: 2.0149093046794846
output/comparetatyana-aliA0_4.jpg: 2.0463283617278307
output/comparetatyana-aliA0_5.jpg: 2.043033884166265
output/comparetatyana-aliA0_6.jpg: 2.059189817329799
output/comparetatyana-aliA0_7.jpg: 1.9324298826958968
output/comparetatyana-aliA0_8.jpg: 2.13745274893827
output/comparetatyana-aliA0_9.jpg: 2.0794605065238745
output/comparetatyana-aliA0_10.jpg: 2.0991049647737543
output/comparetatyana-aliA0_11.jpg: 1.9798878107710787
output/comparetatyana-aliA0_12.jpg: 1.9466544646214132
output/comparetatyana-aliA0_13.jpg: 2.076563337471005
output/comparetatyana-aliA0_14.jpg: 2.157627520910231
output/comparetatyana-aliA0_15.jpg: 2.0898755271049527
output/comparetatyana-aliA0_16.jpg: 1.9948613614708615
output/comparetatyana-aliA0_17.jpg: 2.092391449973899
output/comparetatyana-aliA0_18.jpg: 2.0601838210196926


output/comparetatyana-aliA7_5.jpg: 2.00254714588399
output/comparetatyana-aliA7_6.jpg: 1.8889085690733827
output/comparetatyana-aliA7_7.jpg: 2.1088669551513197
output/comparetatyana-aliA7_8.jpg: 1.845948425617336
output/comparetatyana-aliA7_9.jpg: 2.0702930754109405
output/comparetatyana-aliA7_10.jpg: 2.0298418876260875
output/comparetatyana-aliA7_11.jpg: 2.015833284414669
output/comparetatyana-aliA7_12.jpg: 2.069241691174817
output/comparetatyana-aliA7_13.jpg: 2.0834671281350796
output/comparetatyana-aliA7_14.jpg: 1.955098041708066
output/comparetatyana-aliA7_15.jpg: 2.064864502883
output/comparetatyana-aliA7_16.jpg: 1.9953028960561858
output/comparetatyana-aliA7_17.jpg: 1.9570482330469523
output/comparetatyana-aliA7_18.jpg: 2.0318071974184377
output/comparetatyana-aliA7_19.jpg: 2.072562832285651
output/comparetatyana-aliA7_20.jpg: 2.150618007930319
Fittest: test-images/tatyana_ali.jpg 1.7517779051410356
output/comparetatyana-aliA8_1.jpg: 2.024871003900264
output/comparetatyana-aliA8_

output/comparetatyana-aliA14_8.jpg: 2.053062517095052
output/comparetatyana-aliA14_9.jpg: 2.0448365093023755
output/comparetatyana-aliA14_10.jpg: 1.950038635532263
output/comparetatyana-aliA14_11.jpg: 1.9684456167693185
output/comparetatyana-aliA14_12.jpg: 2.018760349993907
output/comparetatyana-aliA14_13.jpg: 1.9768902642799155
output/comparetatyana-aliA14_14.jpg: 1.9727650798186467
output/comparetatyana-aliA14_15.jpg: 1.8784300962738039
output/comparetatyana-aliA14_16.jpg: 1.9926384085634974
output/comparetatyana-aliA14_17.jpg: 2.0997892036417207
output/comparetatyana-aliA14_18.jpg: 2.1007839071762198
output/comparetatyana-aliA14_19.jpg: 2.0414785054533455
output/comparetatyana-aliA14_20.jpg: 2.024444658297825
Fittest: test-images/tatyana_ali.jpg 1.7517779051410356
output/comparetatyana-aliA15_1.jpg: 2.0645431696396708
output/comparetatyana-aliA15_2.jpg: 1.9707711312930056
output/comparetatyana-aliA15_3.jpg: 2.0850204743895526
output/comparetatyana-aliA15_4.jpg: 2.0649548617555786
ou

output/comparetatyana-aliA21_10.jpg: 1.9940659525535516
output/comparetatyana-aliA21_11.jpg: 2.0393461669575466
output/comparetatyana-aliA21_12.jpg: 2.0037453094978375
output/comparetatyana-aliA21_13.jpg: 2.0605417012236806
output/comparetatyana-aliA21_14.jpg: 2.0772828104763006
output/comparetatyana-aliA21_15.jpg: 2.0645980488992417
output/comparetatyana-aliA21_16.jpg: 2.0190192980492894
output/comparetatyana-aliA21_17.jpg: 2.099607809808583
output/comparetatyana-aliA21_18.jpg: 1.8182375570759786
output/comparetatyana-aliA21_19.jpg: 2.0245787358797904
output/comparetatyana-aliA21_20.jpg: 1.9524236727352533
Fittest: output/comparetatyana-aliA18_15.jpg 1.716603882622013
output/comparetatyana-aliA22_1.jpg: 1.9684403822822352
output/comparetatyana-aliA22_2.jpg: 1.9520966660890655
output/comparetatyana-aliA22_3.jpg: 2.0856199076502273
output/comparetatyana-aliA22_4.jpg: 1.9406117837082326
output/comparetatyana-aliA22_5.jpg: 2.1496597885672166
output/comparetatyana-aliA22_6.jpg: 2.095792948

output/comparetatyana-aliA28_11.jpg: 1.9733587764522222
output/comparetatyana-aliA28_12.jpg: 2.0810957013313613
output/comparetatyana-aliA28_13.jpg: 2.0385971823321842
output/comparetatyana-aliA28_14.jpg: 2.0363599486669743
output/comparetatyana-aliA28_15.jpg: 2.0558978208909098
output/comparetatyana-aliA28_16.jpg: 2.049819828343397
output/comparetatyana-aliA28_17.jpg: 2.0054909308489828
output/comparetatyana-aliA28_18.jpg: 1.9649131941513036
output/comparetatyana-aliA28_19.jpg: 2.0045585210585624
output/comparetatyana-aliA28_20.jpg: 2.072663331806038
Fittest: output/comparetatyana-aliA18_15.jpg 1.716603882622013
output/comparetatyana-aliA29_1.jpg: 2.1884410262886322
output/comparetatyana-aliA29_2.jpg: 1.8819126223183131
output/comparetatyana-aliA29_3.jpg: 1.9485924130597465
output/comparetatyana-aliA29_4.jpg: 2.0017253524786813
output/comparetatyana-aliA29_5.jpg: 2.0284559089382617
output/comparetatyana-aliA29_6.jpg: 2.056301069524693
output/comparetatyana-aliA29_7.jpg: 1.943478523068

...

output/comparetatyana-aliA216_19.jpg: 1.8404364916533684
output/comparetatyana-aliA216_20.jpg: 1.9948558098517304
Fittest: output/comparetatyana-aliA116_6.jpg 1.5981706522168455
output/comparetatyana-aliA217_1.jpg: 1.9390744529316484
output/comparetatyana-aliA217_2.jpg: 2.036110307509731
output/comparetatyana-aliA217_3.jpg: 2.033991872306856
output/comparetatyana-aliA217_4.jpg: 1.9687016097750354
output/comparetatyana-aliA217_5.jpg: 1.984269479146072
output/comparetatyana-aliA217_6.jpg: 2.004508608424638
output/comparetatyana-aliA217_7.jpg: 1.9035151473248844
output/comparetatyana-aliA217_8.jpg: 2.02039582189172
output/comparetatyana-aliA217_9.jpg: 2.0706976156400425
output/comparetatyana-aliA217_10.jpg: 1.9998447560371655
output/comparetatyana-aliA217_11.jpg: 2.0175035081781774
output/comparetatyana-aliA217_12.jpg: 1.938033884891019
output/comparetatyana-aliA217_13.jpg: 1.933372431757263
output/comparetatyana-aliA217_14.jpg: 1.953765649795479
output/comparetatyana-aliA217_15.jpg: 2.03

output/comparetatyana-aliA223_17.jpg: 2.0033382020863897
output/comparetatyana-aliA223_18.jpg: 1.916644521180102
output/comparetatyana-aliA223_19.jpg: 1.9161854786088584
output/comparetatyana-aliA223_20.jpg: 2.0296182013311133
Fittest: output/comparetatyana-aliA116_6.jpg 1.5981706522168455
output/comparetatyana-aliA224_1.jpg: 2.0596756567986887
output/comparetatyana-aliA224_2.jpg: 1.9570513912663754
output/comparetatyana-aliA224_3.jpg: 2.0504056377205693
output/comparetatyana-aliA224_4.jpg: 2.045351647878221
output/comparetatyana-aliA224_5.jpg: 2.028184742205596
output/comparetatyana-aliA224_6.jpg: 2.005207443456464
output/comparetatyana-aliA224_7.jpg: 1.963376396886589
output/comparetatyana-aliA224_8.jpg: 2.06125553320487
output/comparetatyana-aliA224_9.jpg: 2.0801888473394596
output/comparetatyana-aliA224_10.jpg: 1.9674217587154812
output/comparetatyana-aliA224_11.jpg: 2.0666795134479115
output/comparetatyana-aliA224_12.jpg: 2.0235831236324353
output/comparetatyana-aliA224_13.jpg: 2.

output/comparetatyana-aliA230_15.jpg: 2.0569074947117416
output/comparetatyana-aliA230_16.jpg: 1.919633102409329
output/comparetatyana-aliA230_17.jpg: 2.036575208139724
output/comparetatyana-aliA230_18.jpg: 1.974181331176502
output/comparetatyana-aliA230_19.jpg: 2.058816862395279
output/comparetatyana-aliA230_20.jpg: 1.9578145889276728
Fittest: output/comparetatyana-aliA116_6.jpg 1.5981706522168455
output/comparetatyana-aliA231_1.jpg: 1.9760556172108044
output/comparetatyana-aliA231_2.jpg: 2.001640539626522
output/comparetatyana-aliA231_3.jpg: 1.993335841977688
output/comparetatyana-aliA231_4.jpg: 2.063913633430339
output/comparetatyana-aliA231_5.jpg: 1.9187589075438032
output/comparetatyana-aliA231_6.jpg: 2.0474299751772618
output/comparetatyana-aliA231_7.jpg: 2.085649244027758
output/comparetatyana-aliA231_8.jpg: 2.0360830237089855
output/comparetatyana-aliA231_9.jpg: 1.999855167935229
output/comparetatyana-aliA231_10.jpg: 1.9677658097676385
output/comparetatyana-aliA231_11.jpg: 2.07

output/comparetatyana-aliA237_13.jpg: 2.0922319304262778
output/comparetatyana-aliA237_14.jpg: 2.143391726478675
output/comparetatyana-aliA237_15.jpg: 1.992953316995461
output/comparetatyana-aliA237_16.jpg: 2.004352440959718
output/comparetatyana-aliA237_17.jpg: 2.0284134856296747
output/comparetatyana-aliA237_18.jpg: 1.836431014712733
output/comparetatyana-aliA237_19.jpg: 1.9856644419444802
output/comparetatyana-aliA237_20.jpg: 1.9441392853204276
Fittest: output/comparetatyana-aliA116_6.jpg 1.5981706522168455
output/comparetatyana-aliA238_1.jpg: 1.9788972598464394
output/comparetatyana-aliA238_2.jpg: 1.882745679601452
output/comparetatyana-aliA238_3.jpg: 1.949300461173929
output/comparetatyana-aliA238_4.jpg: 1.8242648279906675
output/comparetatyana-aliA238_5.jpg: 1.724506346443817
output/comparetatyana-aliA238_6.jpg: 2.050699677938895
output/comparetatyana-aliA238_7.jpg: 2.010643468345352
output/comparetatyana-aliA238_8.jpg: 1.914104129794046
output/comparetatyana-aliA238_9.jpg: 1.909

output/comparetatyana-aliA244_12.jpg: 2.01574893783443
output/comparetatyana-aliA244_13.jpg: 2.023928710932157
output/comparetatyana-aliA244_14.jpg: 2.039167301293282
output/comparetatyana-aliA244_15.jpg: 2.0848180314322935
output/comparetatyana-aliA244_16.jpg: 1.9640940103705202
output/comparetatyana-aliA244_17.jpg: 2.0456185176846793
output/comparetatyana-aliA244_18.jpg: 1.8833060486537052
output/comparetatyana-aliA244_19.jpg: 1.9584918891532703
output/comparetatyana-aliA244_20.jpg: 2.001240359085592
Fittest: output/comparetatyana-aliA116_6.jpg 1.5981706522168455
output/comparetatyana-aliA245_1.jpg: 1.943899699078499
output/comparetatyana-aliA245_2.jpg: 2.0104826093531196
output/comparetatyana-aliA245_3.jpg: 1.930076108427115
output/comparetatyana-aliA245_4.jpg: 1.950155811918239
output/comparetatyana-aliA245_5.jpg: 1.8243744384382534
output/comparetatyana-aliA245_6.jpg: 2.0698024016362457
output/comparetatyana-aliA245_7.jpg: 2.014016338434309
output/comparetatyana-aliA245_8.jpg: 1.8

In [10]:
evolve('test-images/samuel_jackson.jpg', 'test-images/tatyana_ali.jpg', 'samuel-l-jackson','C')

Start: 1.7517779051410356


Exception: Unable to find a face: output/comparesamuel-l-jacksonC0_1.jpg

Let's look at the image that fails:
![Samuel L. Jackson](https://github.com/erstrong/BigDataSystemsandIntelligenceAnalytics/blob/master/AdversarialFaceRecognition/examples/comparesamuel-l-jacksonA0_1.jpg?raw=true)
There is still a discernable face, but Samuel L. Jackson's dark skin tone, his glasses, and his hat are all likely contributing to why with the addition of noise the model can no longer find the gradient pattern of a face. If the model was not trained on many faces of black people, it could explain why this image is having the problem when none of the others do.

Continuing on to the other combinations:

In [12]:
evolve('test-images/colin_firth.jpg', 'test-images/george_lopez.jpg', 'colin-firth','C')

Start: 1.4893645550500847
output/comparecolin-firthC0_1.jpg: 1.8094400459350557
output/comparecolin-firthC0_2.jpg: 1.7522427206784705
output/comparecolin-firthC0_3.jpg: 2.061119122554846
output/comparecolin-firthC0_4.jpg: 1.8778317759210505
output/comparecolin-firthC0_5.jpg: 1.6439120527462578
output/comparecolin-firthC0_6.jpg: 1.6195744201337086
output/comparecolin-firthC0_7.jpg: 1.8572617351455702
output/comparecolin-firthC0_8.jpg: 1.7884535772058907
output/comparecolin-firthC0_9.jpg: 1.6713718861052347
output/comparecolin-firthC0_10.jpg: 1.7487032547469505
output/comparecolin-firthC0_11.jpg: 1.9512277758363616
output/comparecolin-firthC0_12.jpg: 1.6934268651034214
output/comparecolin-firthC0_13.jpg: 2.0598135007449363
output/comparecolin-firthC0_14.jpg: 2.1057964304541024
output/comparecolin-firthC0_15.jpg: 1.9336376804899793
output/comparecolin-firthC0_16.jpg: 1.599669410563502
output/comparecolin-firthC0_17.jpg: 1.8978524123714404
output/comparecolin-firthC0_18.jpg: 1.878657575578

output/comparecolin-firthC7_4.jpg: 1.8783522987717243
output/comparecolin-firthC7_5.jpg: 1.9138460814051577
output/comparecolin-firthC7_6.jpg: 1.8262771969963947
output/comparecolin-firthC7_7.jpg: 1.8224493789220269
output/comparecolin-firthC7_8.jpg: 1.7020707414857856
output/comparecolin-firthC7_9.jpg: 1.944809945022043
output/comparecolin-firthC7_10.jpg: 1.7542778079344896
output/comparecolin-firthC7_11.jpg: 1.9034708823407351
output/comparecolin-firthC7_12.jpg: 1.9337555592029223
output/comparecolin-firthC7_13.jpg: 1.8878271294619808
output/comparecolin-firthC7_14.jpg: 1.8635696190688311
output/comparecolin-firthC7_15.jpg: 1.949487692046934
output/comparecolin-firthC7_16.jpg: 1.857952524310719
output/comparecolin-firthC7_17.jpg: 1.9386913710513451
output/comparecolin-firthC7_18.jpg: 1.827323981140219
output/comparecolin-firthC7_19.jpg: 1.932743011489808
output/comparecolin-firthC7_20.jpg: 1.819129874026988
Fittest: output/comparecolin-firthC1_9.jpg 1.438012413919195
output/compareco

output/comparecolin-firthC14_6.jpg: 1.67533874907132
output/comparecolin-firthC14_7.jpg: 1.8988365284609934
output/comparecolin-firthC14_8.jpg: 1.625623797399571
output/comparecolin-firthC14_9.jpg: 1.8336434441296288
output/comparecolin-firthC14_10.jpg: 2.0217379580276225
output/comparecolin-firthC14_11.jpg: 1.7896745309835957
output/comparecolin-firthC14_12.jpg: 1.9198805955932032
output/comparecolin-firthC14_13.jpg: 1.8405156428834468
output/comparecolin-firthC14_14.jpg: 1.750643513949982
output/comparecolin-firthC14_15.jpg: 1.932974723272723
output/comparecolin-firthC14_16.jpg: 1.9301017204994873
output/comparecolin-firthC14_17.jpg: 1.8389639871641474
output/comparecolin-firthC14_18.jpg: 1.8858755791656683
output/comparecolin-firthC14_19.jpg: 1.8689908572790717
output/comparecolin-firthC14_20.jpg: 1.9470193998260061
Fittest: output/comparecolin-firthC1_9.jpg 1.438012413919195
output/comparecolin-firthC15_1.jpg: 1.6668006456219406
output/comparecolin-firthC15_2.jpg: 1.582473720329013

output/comparecolin-firthC21_7.jpg: 1.9224780819730924
output/comparecolin-firthC21_8.jpg: 1.8914125691398906
output/comparecolin-firthC21_9.jpg: 1.7689226130165192
output/comparecolin-firthC21_10.jpg: 1.745423082138434
output/comparecolin-firthC21_11.jpg: 1.693287831354276
output/comparecolin-firthC21_12.jpg: 1.7408742879700434
output/comparecolin-firthC21_13.jpg: 2.0124775416992273
output/comparecolin-firthC21_14.jpg: 1.7243178063121316
output/comparecolin-firthC21_15.jpg: 1.7867497977486462
output/comparecolin-firthC21_16.jpg: 1.8460639352895474
output/comparecolin-firthC21_17.jpg: 1.7562782251120215
output/comparecolin-firthC21_18.jpg: 2.0061647510236744
output/comparecolin-firthC21_19.jpg: 1.6755446466620205
output/comparecolin-firthC21_20.jpg: 1.8760007621959294
Fittest: output/comparecolin-firthC1_9.jpg 1.438012413919195
output/comparecolin-firthC22_1.jpg: 1.93626464083233
output/comparecolin-firthC22_2.jpg: 1.6611244145242892
output/comparecolin-firthC22_3.jpg: 1.58571851570479

output/comparecolin-firthC28_8.jpg: 1.4457941854590683
output/comparecolin-firthC28_9.jpg: 1.8392404025025142
output/comparecolin-firthC28_10.jpg: 1.7265086383213504
output/comparecolin-firthC28_11.jpg: 1.8847212784446643
output/comparecolin-firthC28_12.jpg: 1.8324839662389834
output/comparecolin-firthC28_13.jpg: 1.8185095783793395
output/comparecolin-firthC28_14.jpg: 1.8985160844807933
output/comparecolin-firthC28_15.jpg: 1.9387254765145343
output/comparecolin-firthC28_16.jpg: 1.9380460414925316
output/comparecolin-firthC28_17.jpg: 1.9398765012308763
output/comparecolin-firthC28_18.jpg: 1.8454425652655408
output/comparecolin-firthC28_19.jpg: 1.8548836179817791
output/comparecolin-firthC28_20.jpg: 1.982436150623514
Fittest: output/comparecolin-firthC1_9.jpg 1.438012413919195
output/comparecolin-firthC29_1.jpg: 1.8459818264744192
output/comparecolin-firthC29_2.jpg: 1.7522730654573697
output/comparecolin-firthC29_3.jpg: 1.9028504460519344
output/comparecolin-firthC29_4.jpg: 1.78827688553

...

output/comparecolin-firthC216_6.jpg: 1.8037743438556637
output/comparecolin-firthC216_7.jpg: 1.5460762948869644
output/comparecolin-firthC216_8.jpg: 1.6725002296413929
output/comparecolin-firthC216_9.jpg: 1.834087222638109
output/comparecolin-firthC216_10.jpg: 1.8891939580437047
output/comparecolin-firthC216_11.jpg: 1.8350547977933387
output/comparecolin-firthC216_12.jpg: 1.8721332047152432
output/comparecolin-firthC216_13.jpg: 1.8581483600248752
output/comparecolin-firthC216_14.jpg: 2.0024444543401794
output/comparecolin-firthC216_15.jpg: 1.7236473970130735
output/comparecolin-firthC216_16.jpg: 1.780779689858395
output/comparecolin-firthC216_17.jpg: 1.57042517954079
output/comparecolin-firthC216_18.jpg: 2.020950314482752
output/comparecolin-firthC216_19.jpg: 1.806462524187583
output/comparecolin-firthC216_20.jpg: 1.803821338153218
Fittest: output/comparecolin-firthC86_4.jpg 1.3003711804094247
output/comparecolin-firthC217_1.jpg: 1.872981404394581
output/comparecolin-firthC217_2.jpg: 1

output/comparecolin-firthC223_4.jpg: 1.7906546044496252
output/comparecolin-firthC223_5.jpg: 1.8434529671632274
output/comparecolin-firthC223_6.jpg: 1.748840717834896
output/comparecolin-firthC223_7.jpg: 1.7331477420088937
output/comparecolin-firthC223_8.jpg: 1.788985438349033
output/comparecolin-firthC223_9.jpg: 1.7769496409323833
output/comparecolin-firthC223_10.jpg: 1.886371714436483
output/comparecolin-firthC223_11.jpg: 1.741126532857739
output/comparecolin-firthC223_12.jpg: 1.8538480664743218
output/comparecolin-firthC223_13.jpg: 1.7358996854254718
output/comparecolin-firthC223_14.jpg: 1.9848473659426031
output/comparecolin-firthC223_15.jpg: 1.844919834822203
output/comparecolin-firthC223_16.jpg: 1.8964775787449812
output/comparecolin-firthC223_17.jpg: 1.708331813015711
output/comparecolin-firthC223_18.jpg: 1.6820695780972559
output/comparecolin-firthC223_19.jpg: 1.8312822463167733
output/comparecolin-firthC223_20.jpg: 1.7538624248145802
Fittest: output/comparecolin-firthC86_4.jpg

output/comparecolin-firthC230_2.jpg: 1.6689305261438707
output/comparecolin-firthC230_3.jpg: 1.9344593281548004
output/comparecolin-firthC230_4.jpg: 1.6708969878705429
output/comparecolin-firthC230_5.jpg: 1.9690823160476065
output/comparecolin-firthC230_6.jpg: 1.807824743259212
output/comparecolin-firthC230_7.jpg: 1.6153774682763775
output/comparecolin-firthC230_8.jpg: 1.6822955727445796
output/comparecolin-firthC230_9.jpg: 1.7873347032636657
output/comparecolin-firthC230_10.jpg: 1.6062155123673874
output/comparecolin-firthC230_11.jpg: 1.9411498107330376
output/comparecolin-firthC230_12.jpg: 1.930631293603625
output/comparecolin-firthC230_13.jpg: 1.7333221732646165
output/comparecolin-firthC230_14.jpg: 1.785186571220626
output/comparecolin-firthC230_15.jpg: 1.7848996609673609
output/comparecolin-firthC230_16.jpg: 1.8780312894307816
output/comparecolin-firthC230_17.jpg: 1.6433165538640804
output/comparecolin-firthC230_18.jpg: 1.8450472152497657
output/comparecolin-firthC230_19.jpg: 1.96

output/comparecolin-firthC237_1.jpg: 1.8820292007928514
output/comparecolin-firthC237_2.jpg: 1.7657743866696243
output/comparecolin-firthC237_3.jpg: 1.8398089902035863
output/comparecolin-firthC237_4.jpg: 1.7941726983405322
output/comparecolin-firthC237_5.jpg: 1.9448350382256918
output/comparecolin-firthC237_6.jpg: 1.724336355438707
output/comparecolin-firthC237_7.jpg: 1.811224562364539
output/comparecolin-firthC237_8.jpg: 1.8702261772057276
output/comparecolin-firthC237_9.jpg: 1.9721594636972317
output/comparecolin-firthC237_10.jpg: 1.882459296858904
output/comparecolin-firthC237_11.jpg: 1.738535143132286
output/comparecolin-firthC237_12.jpg: 1.7914292122133144
output/comparecolin-firthC237_13.jpg: 1.701335388032532
output/comparecolin-firthC237_14.jpg: 1.805805906165764
output/comparecolin-firthC237_15.jpg: 1.7525248844151295
output/comparecolin-firthC237_16.jpg: 1.8980191320684412
output/comparecolin-firthC237_17.jpg: 1.861828573542239
output/comparecolin-firthC237_18.jpg: 1.7384148

output/comparecolin-firthC243_20.jpg: 1.786421214397018
Fittest: output/comparecolin-firthC86_4.jpg 1.3003711804094247
output/comparecolin-firthC244_1.jpg: 1.6323845520808176
output/comparecolin-firthC244_2.jpg: 1.9790167314124574
output/comparecolin-firthC244_3.jpg: 1.7447943339448613
output/comparecolin-firthC244_4.jpg: 1.774271836194262
output/comparecolin-firthC244_5.jpg: 1.737471062819611
output/comparecolin-firthC244_6.jpg: 1.9857157782096477
output/comparecolin-firthC244_7.jpg: 1.7576516740511814
output/comparecolin-firthC244_8.jpg: 2.0168158844444797
output/comparecolin-firthC244_9.jpg: 1.803109571057881
output/comparecolin-firthC244_10.jpg: 2.0017569494338776
output/comparecolin-firthC244_11.jpg: 1.7036044087540971
output/comparecolin-firthC244_12.jpg: 1.8132352760696944
output/comparecolin-firthC244_13.jpg: 1.8557526839275595
output/comparecolin-firthC244_14.jpg: 1.8901261983960795
output/comparecolin-firthC244_15.jpg: 1.8394762767301533
output/comparecolin-firthC244_16.jpg: 

In [13]:
evolve('test-images/george_lopez.jpg', 'test-images/colin_firth.jpg', 'george-lopez','A')

Start: 1.4893645550500847
output/comparegeorge-lopezA0_1.jpg: 1.4786397063187937
output/comparegeorge-lopezA0_2.jpg: 1.484046186825314
output/comparegeorge-lopezA0_3.jpg: 1.4519099888459177
output/comparegeorge-lopezA0_4.jpg: 1.5101118036627312
output/comparegeorge-lopezA0_5.jpg: 1.4828011270610288
output/comparegeorge-lopezA0_6.jpg: 1.5025063192902675
output/comparegeorge-lopezA0_7.jpg: 1.4872449927518399
output/comparegeorge-lopezA0_8.jpg: 1.4314312575982475
output/comparegeorge-lopezA0_9.jpg: 1.5134420376525473
output/comparegeorge-lopezA0_10.jpg: 1.5288351244247216
output/comparegeorge-lopezA0_11.jpg: 1.5115304083251437
output/comparegeorge-lopezA0_12.jpg: 1.50355481999649
output/comparegeorge-lopezA0_13.jpg: 1.5063014315529606
output/comparegeorge-lopezA0_14.jpg: 1.4931601900081102
output/comparegeorge-lopezA0_15.jpg: 1.4821784230127193
output/comparegeorge-lopezA0_16.jpg: 1.2606827135106489
output/comparegeorge-lopezA0_17.jpg: 1.445738756442825
output/comparegeorge-lopezA0_18.jpg

output/comparegeorge-lopezA7_1.jpg: 1.470304008441012
output/comparegeorge-lopezA7_2.jpg: 1.4874867040655255
output/comparegeorge-lopezA7_3.jpg: 1.5191378650678606
output/comparegeorge-lopezA7_4.jpg: 1.480067387836303
output/comparegeorge-lopezA7_5.jpg: 1.4493133409748946
output/comparegeorge-lopezA7_6.jpg: 1.350379036539286
output/comparegeorge-lopezA7_7.jpg: 1.4708053932178835
output/comparegeorge-lopezA7_8.jpg: 1.3404738229612034
output/comparegeorge-lopezA7_9.jpg: 1.4967325598380696
output/comparegeorge-lopezA7_10.jpg: 1.5117848137127634
output/comparegeorge-lopezA7_11.jpg: 1.4476619448835075
output/comparegeorge-lopezA7_12.jpg: 1.418861071777851
output/comparegeorge-lopezA7_13.jpg: 1.456421648119746
output/comparegeorge-lopezA7_14.jpg: 1.280170398024707
output/comparegeorge-lopezA7_15.jpg: 1.4800560866310262
output/comparegeorge-lopezA7_16.jpg: 1.4876994539673227
output/comparegeorge-lopezA7_17.jpg: 1.4694182169882712
output/comparegeorge-lopezA7_18.jpg: 1.4662693229780883
output/

output/comparegeorge-lopezA14_1.jpg: 1.3183702047231787
output/comparegeorge-lopezA14_2.jpg: 1.5031698470686667
output/comparegeorge-lopezA14_3.jpg: 1.4467108660571266
output/comparegeorge-lopezA14_4.jpg: 1.1096511659248829
output/comparegeorge-lopezA14_5.jpg: 1.492461363266873
output/comparegeorge-lopezA14_6.jpg: 1.5186863386666833
output/comparegeorge-lopezA14_7.jpg: 1.498143768393581
output/comparegeorge-lopezA14_8.jpg: 1.5649114964641428
output/comparegeorge-lopezA14_9.jpg: 1.4201592506049625
output/comparegeorge-lopezA14_10.jpg: 1.4931488419820997
output/comparegeorge-lopezA14_11.jpg: 1.3197731982037615
output/comparegeorge-lopezA14_12.jpg: 1.3029892926607354
output/comparegeorge-lopezA14_13.jpg: 1.4382214654245251
output/comparegeorge-lopezA14_14.jpg: 1.3333576433749368
output/comparegeorge-lopezA14_15.jpg: 1.495993364387463
output/comparegeorge-lopezA14_16.jpg: 1.4894884757576228
output/comparegeorge-lopezA14_17.jpg: 1.5085163720398258
output/comparegeorge-lopezA14_18.jpg: 1.459

output/comparegeorge-lopezA20_20.jpg: 1.481370011309696
Fittest: output/comparegeorge-lopezA14_4.jpg 1.1096511659248829
output/comparegeorge-lopezA21_1.jpg: 1.4320338507978878
output/comparegeorge-lopezA21_2.jpg: 1.502155471422714
output/comparegeorge-lopezA21_3.jpg: 1.4282324392597006
output/comparegeorge-lopezA21_4.jpg: 1.4351473480052457
output/comparegeorge-lopezA21_5.jpg: 1.437708233469725
output/comparegeorge-lopezA21_6.jpg: 1.439940107509879
output/comparegeorge-lopezA21_7.jpg: 1.4625214322724267
output/comparegeorge-lopezA21_8.jpg: 1.400962970307921
output/comparegeorge-lopezA21_9.jpg: 1.379496414849744
output/comparegeorge-lopezA21_10.jpg: 1.450217977090392
output/comparegeorge-lopezA21_11.jpg: 1.5503822570561372
output/comparegeorge-lopezA21_12.jpg: 1.4457100891050447
output/comparegeorge-lopezA21_13.jpg: 1.1633055231470788
output/comparegeorge-lopezA21_14.jpg: 1.472482431524612
output/comparegeorge-lopezA21_15.jpg: 1.4830364061365124
output/comparegeorge-lopezA21_16.jpg: 1.4

output/comparegeorge-lopezA27_18.jpg: 1.4916312370137437
output/comparegeorge-lopezA27_19.jpg: 1.5031246428267606
output/comparegeorge-lopezA27_20.jpg: 1.2694934063793106
Fittest: output/comparegeorge-lopezA14_4.jpg 1.1096511659248829
output/comparegeorge-lopezA28_1.jpg: 1.1714383424959594
output/comparegeorge-lopezA28_2.jpg: 1.5042202377636333
output/comparegeorge-lopezA28_3.jpg: 1.4409057649269452
output/comparegeorge-lopezA28_4.jpg: 1.4545142350223277
output/comparegeorge-lopezA28_5.jpg: 1.413273945885063
output/comparegeorge-lopezA28_6.jpg: 1.4659540495732788
output/comparegeorge-lopezA28_7.jpg: 1.4980631507646731
output/comparegeorge-lopezA28_8.jpg: 1.5081841907692404
output/comparegeorge-lopezA28_9.jpg: 1.4790883618539858
output/comparegeorge-lopezA28_10.jpg: 1.4823282824629838
output/comparegeorge-lopezA28_11.jpg: 1.481690387348901
output/comparegeorge-lopezA28_12.jpg: 1.469264996842486
output/comparegeorge-lopezA28_13.jpg: 1.4389645876665855
output/comparegeorge-lopezA28_14.jpg

...

output/comparegeorge-lopezA219_3.jpg: 1.465633618491173
output/comparegeorge-lopezA219_4.jpg: 1.4227890449756313
output/comparegeorge-lopezA219_5.jpg: 1.3814452056161892
output/comparegeorge-lopezA219_6.jpg: 1.2362197656913074
output/comparegeorge-lopezA219_7.jpg: 1.3158235083683487
output/comparegeorge-lopezA219_8.jpg: 1.4954941016339007
output/comparegeorge-lopezA219_9.jpg: 1.1519799132547366
output/comparegeorge-lopezA219_10.jpg: 1.3141909586294989
output/comparegeorge-lopezA219_11.jpg: 1.3329940929959037
output/comparegeorge-lopezA219_12.jpg: 1.4758208879244794
output/comparegeorge-lopezA219_13.jpg: 1.4049592323393902
output/comparegeorge-lopezA219_14.jpg: 1.3738218153634867
output/comparegeorge-lopezA219_15.jpg: 1.4516220540326903
output/comparegeorge-lopezA219_16.jpg: 1.402730627440269
output/comparegeorge-lopezA219_17.jpg: 1.3880289817901308
output/comparegeorge-lopezA219_18.jpg: 1.4138476517349332
output/comparegeorge-lopezA219_19.jpg: 1.1457246810063242
output/comparegeorge-lo

output/comparegeorge-lopezA225_19.jpg: 1.2627466350272365
output/comparegeorge-lopezA225_20.jpg: 1.2818770937564867
Fittest: output/comparegeorge-lopezA117_14.jpg 1.0611626670973286
output/comparegeorge-lopezA226_1.jpg: 1.2939899858333848
output/comparegeorge-lopezA226_2.jpg: 1.403889110367661
output/comparegeorge-lopezA226_3.jpg: 1.4150327546631647
output/comparegeorge-lopezA226_4.jpg: 1.3115312853837362
output/comparegeorge-lopezA226_5.jpg: 1.4600549385560861
output/comparegeorge-lopezA226_6.jpg: 1.448877505503142
output/comparegeorge-lopezA226_7.jpg: 1.388511206199596
output/comparegeorge-lopezA226_8.jpg: 1.4720098048538386
output/comparegeorge-lopezA226_9.jpg: 1.2162998418005202
output/comparegeorge-lopezA226_10.jpg: 1.1411774076101446
output/comparegeorge-lopezA226_11.jpg: 1.4016008731654805
output/comparegeorge-lopezA226_12.jpg: 1.4185333254855648
output/comparegeorge-lopezA226_13.jpg: 1.2710827275712542
output/comparegeorge-lopezA226_14.jpg: 1.388957917319281
output/comparegeorg

output/comparegeorge-lopezA232_14.jpg: 1.3819502023830244
output/comparegeorge-lopezA232_15.jpg: 1.4080016629939727
output/comparegeorge-lopezA232_16.jpg: 1.3845773007099358
output/comparegeorge-lopezA232_17.jpg: 1.3205615536954107
output/comparegeorge-lopezA232_18.jpg: 1.4595721851207362
output/comparegeorge-lopezA232_19.jpg: 1.4129108526900678
output/comparegeorge-lopezA232_20.jpg: 1.2505888126347338
Fittest: output/comparegeorge-lopezA117_14.jpg 1.0611626670973286
output/comparegeorge-lopezA233_1.jpg: 1.1857399466526388
output/comparegeorge-lopezA233_2.jpg: 1.4537151139375535
output/comparegeorge-lopezA233_3.jpg: 1.4845339109423468
output/comparegeorge-lopezA233_4.jpg: 1.2351979251745586
output/comparegeorge-lopezA233_5.jpg: 1.185705336242755
output/comparegeorge-lopezA233_6.jpg: 1.1639533024121862
output/comparegeorge-lopezA233_7.jpg: 1.4761105786983064
output/comparegeorge-lopezA233_8.jpg: 1.323506850778769
output/comparegeorge-lopezA233_9.jpg: 1.4319099246122513
output/comparegeo

output/comparegeorge-lopezA239_9.jpg: 1.3547358157819906
output/comparegeorge-lopezA239_10.jpg: 1.2649224417333655
output/comparegeorge-lopezA239_11.jpg: 1.5084872142156156
output/comparegeorge-lopezA239_12.jpg: 1.431320444403443
output/comparegeorge-lopezA239_13.jpg: 1.327337433484531
output/comparegeorge-lopezA239_14.jpg: 1.424347293417715
output/comparegeorge-lopezA239_15.jpg: 1.3549695503718107
output/comparegeorge-lopezA239_16.jpg: 1.1792349800315325
output/comparegeorge-lopezA239_17.jpg: 1.337161389344405
output/comparegeorge-lopezA239_18.jpg: 1.2979335473001292
output/comparegeorge-lopezA239_19.jpg: 1.3844524867736738
output/comparegeorge-lopezA239_20.jpg: 1.3421478200922539
Fittest: output/comparegeorge-lopezA117_14.jpg 1.0611626670973286
output/comparegeorge-lopezA240_1.jpg: 1.5201019187446962
output/comparegeorge-lopezA240_2.jpg: 1.3373237104849767
output/comparegeorge-lopezA240_3.jpg: 1.1657975466306878
output/comparegeorge-lopezA240_4.jpg: 1.4493221027227334
output/compareg

output/comparegeorge-lopezA246_4.jpg: 1.1831890883679783
output/comparegeorge-lopezA246_5.jpg: 1.4327230262587762
output/comparegeorge-lopezA246_6.jpg: 1.4326351296814996
output/comparegeorge-lopezA246_7.jpg: 1.4280740019743656
output/comparegeorge-lopezA246_8.jpg: 1.2769964092222408
output/comparegeorge-lopezA246_9.jpg: 1.4651056405675922
output/comparegeorge-lopezA246_10.jpg: 1.1242155090911607
output/comparegeorge-lopezA246_11.jpg: 1.362214028799138
output/comparegeorge-lopezA246_12.jpg: 1.3647513259372834
output/comparegeorge-lopezA246_13.jpg: 1.1503622518822287
output/comparegeorge-lopezA246_14.jpg: 1.3607493439212233
output/comparegeorge-lopezA246_15.jpg: 1.365042320594057
output/comparegeorge-lopezA246_16.jpg: 1.2232079161127334
output/comparegeorge-lopezA246_17.jpg: 1.200184442074824
output/comparegeorge-lopezA246_18.jpg: 1.268870977314199
output/comparegeorge-lopezA246_19.jpg: 1.4117364193672395
output/comparegeorge-lopezA246_20.jpg: 1.2961402028671203
Fittest: output/compareg

In [21]:
evolve('test-images/samuel_jackson.jpg', 'test-images/ken_watanabe.jpg', 'samuel-l-jackson','B')

Start: 2.2429793394657542


Exception: Unable to find a face: output/comparesamuel-l-jacksonB0_1.jpg

In [11]:
evolve('test-images/ken_watanabe.jpg', 'test-images/samuel_jackson.jpg', 'ken-watanabe','A')

Start: 2.2429793394657542
output/compareken-watanabeA0_1.jpg: 2.0883143091587444
output/compareken-watanabeA0_2.jpg: 2.0709856449140185
output/compareken-watanabeA0_3.jpg: 2.0562254562902877
output/compareken-watanabeA0_4.jpg: 2.07814042661037
output/compareken-watanabeA0_5.jpg: 2.0303679531080294
output/compareken-watanabeA0_6.jpg: 2.0536935958092895
output/compareken-watanabeA0_7.jpg: 2.1467288099744177
output/compareken-watanabeA0_8.jpg: 2.0966777378268997
output/compareken-watanabeA0_9.jpg: 1.961716972004811
output/compareken-watanabeA0_10.jpg: 2.0668801961228884
output/compareken-watanabeA0_11.jpg: 2.037364617897468
output/compareken-watanabeA0_12.jpg: 2.0693479636644883
output/compareken-watanabeA0_13.jpg: 2.0771216199814244
output/compareken-watanabeA0_14.jpg: 2.0336428126867103
output/compareken-watanabeA0_15.jpg: 2.044031998660521
output/compareken-watanabeA0_16.jpg: 2.0789224380860394
output/compareken-watanabeA0_17.jpg: 2.0047238591989474
output/compareken-watanabeA0_18.jpg:

output/compareken-watanabeA7_2.jpg: 2.0795686863087175
output/compareken-watanabeA7_3.jpg: 2.0611829116492726
output/compareken-watanabeA7_4.jpg: 2.052405731643126
output/compareken-watanabeA7_5.jpg: 2.116503274996629
output/compareken-watanabeA7_6.jpg: 2.1531353681227063
output/compareken-watanabeA7_7.jpg: 2.071479040582168
output/compareken-watanabeA7_8.jpg: 2.0692322674087493
output/compareken-watanabeA7_9.jpg: 2.137123776331974
output/compareken-watanabeA7_10.jpg: 2.103590073751872
output/compareken-watanabeA7_11.jpg: 2.138651371520907
output/compareken-watanabeA7_12.jpg: 2.0822374954777634
output/compareken-watanabeA7_13.jpg: 2.031869700768018
output/compareken-watanabeA7_14.jpg: 2.082128372841261
output/compareken-watanabeA7_15.jpg: 2.066672014606073
output/compareken-watanabeA7_16.jpg: 2.0740124369599466
output/compareken-watanabeA7_17.jpg: 2.1121343921891635
output/compareken-watanabeA7_18.jpg: 2.0504930480922745
output/compareken-watanabeA7_19.jpg: 2.1378276109710592
output/co

output/compareken-watanabeA14_2.jpg: 2.042738143906469
output/compareken-watanabeA14_3.jpg: 2.0937122655794633
output/compareken-watanabeA14_4.jpg: 2.040940498238066
output/compareken-watanabeA14_5.jpg: 2.1881125812259166
output/compareken-watanabeA14_6.jpg: 2.0988855851924364
output/compareken-watanabeA14_7.jpg: 2.087621951790468
output/compareken-watanabeA14_8.jpg: 2.081732704434948
output/compareken-watanabeA14_9.jpg: 2.109903192066077
output/compareken-watanabeA14_10.jpg: 2.0919190837907613
output/compareken-watanabeA14_11.jpg: 2.0579040828516675
output/compareken-watanabeA14_12.jpg: 2.1232878775921327
output/compareken-watanabeA14_13.jpg: 2.0808038622363023
output/compareken-watanabeA14_14.jpg: 2.0681543092188264
output/compareken-watanabeA14_15.jpg: 2.130972201845056
output/compareken-watanabeA14_16.jpg: 2.092847823870314
output/compareken-watanabeA14_17.jpg: 2.124400869831946
output/compareken-watanabeA14_18.jpg: 2.0621401009350486
output/compareken-watanabeA14_19.jpg: 2.1071947

output/compareken-watanabeA21_1.jpg: 2.1241947292147376
output/compareken-watanabeA21_2.jpg: 2.1134283195163097
output/compareken-watanabeA21_3.jpg: 2.0846204067508105
output/compareken-watanabeA21_4.jpg: 2.0905196114377804
output/compareken-watanabeA21_5.jpg: 2.1142469833156197
output/compareken-watanabeA21_6.jpg: 2.063740743923271
output/compareken-watanabeA21_7.jpg: 2.0425051374507346
output/compareken-watanabeA21_8.jpg: 2.0990624853861326
output/compareken-watanabeA21_9.jpg: 2.0567395351706232
output/compareken-watanabeA21_10.jpg: 2.108122981364401
output/compareken-watanabeA21_11.jpg: 2.118311277386128
output/compareken-watanabeA21_12.jpg: 2.125050020951872
output/compareken-watanabeA21_13.jpg: 2.1061964234794766
output/compareken-watanabeA21_14.jpg: 2.087209073290142
output/compareken-watanabeA21_15.jpg: 2.0624473510631485
output/compareken-watanabeA21_16.jpg: 2.097514657977624
output/compareken-watanabeA21_17.jpg: 2.0677843810880843
output/compareken-watanabeA21_18.jpg: 2.099211

output/compareken-watanabeA28_1.jpg: 2.1219004061489097
output/compareken-watanabeA28_2.jpg: 2.191343840684278
output/compareken-watanabeA28_3.jpg: 2.110285024740466
output/compareken-watanabeA28_4.jpg: 2.1107374125863454
output/compareken-watanabeA28_5.jpg: 2.0488376916060616
output/compareken-watanabeA28_6.jpg: 2.0217857087030957
output/compareken-watanabeA28_7.jpg: 2.1136699295462043
output/compareken-watanabeA28_8.jpg: 2.1396382546783244
output/compareken-watanabeA28_9.jpg: 2.1648590464489192
output/compareken-watanabeA28_10.jpg: 2.0314600112643264
output/compareken-watanabeA28_11.jpg: 2.0844629809914093
output/compareken-watanabeA28_12.jpg: 2.1169293068791717
output/compareken-watanabeA28_13.jpg: 2.1435150270434287
output/compareken-watanabeA28_14.jpg: 2.105968475605379
output/compareken-watanabeA28_15.jpg: 2.1048741137471767
output/compareken-watanabeA28_16.jpg: 2.080544583212069
output/compareken-watanabeA28_17.jpg: 1.9990155633022826
output/compareken-watanabeA28_18.jpg: 2.1498

...

output/compareken-watanabeA220_8.jpg: 2.0754670700503155
output/compareken-watanabeA220_9.jpg: 2.0511550326852444
output/compareken-watanabeA220_10.jpg: 2.03494820575468
output/compareken-watanabeA220_11.jpg: 2.074879776686453
output/compareken-watanabeA220_12.jpg: 2.096656365110474
output/compareken-watanabeA220_13.jpg: 1.9773048050714812
output/compareken-watanabeA220_14.jpg: 2.1142899342376476
output/compareken-watanabeA220_15.jpg: 2.077240721911445
output/compareken-watanabeA220_16.jpg: 2.0764931423576063
output/compareken-watanabeA220_17.jpg: 2.098265231918965
output/compareken-watanabeA220_18.jpg: 2.10418539016168
output/compareken-watanabeA220_19.jpg: 2.0674019679984244
output/compareken-watanabeA220_20.jpg: 2.0708439080968244
Fittest: output/compareken-watanabeA185_13.jpg 1.9168774664399528
output/compareken-watanabeA221_1.jpg: 2.0923147550622483
output/compareken-watanabeA221_2.jpg: 2.072471486930625
output/compareken-watanabeA221_3.jpg: 2.0746574202363077
output/compareken-wa

output/compareken-watanabeA227_4.jpg: 2.044343650688572
output/compareken-watanabeA227_5.jpg: 2.0858852830059442
output/compareken-watanabeA227_6.jpg: 2.0801779272507295
output/compareken-watanabeA227_7.jpg: 2.0961358375753214
output/compareken-watanabeA227_8.jpg: 2.0920849443662224
output/compareken-watanabeA227_9.jpg: 2.0353829606891587
output/compareken-watanabeA227_10.jpg: 2.0733708090531042
output/compareken-watanabeA227_11.jpg: 2.0918590268926245
output/compareken-watanabeA227_12.jpg: 2.096541110315399
output/compareken-watanabeA227_13.jpg: 2.0938505170866266
output/compareken-watanabeA227_14.jpg: 2.0441618723228303
output/compareken-watanabeA227_15.jpg: 2.0615893848017066
output/compareken-watanabeA227_16.jpg: 2.046317044072814
output/compareken-watanabeA227_17.jpg: 2.00553522103034
output/compareken-watanabeA227_18.jpg: 2.038246441654324
output/compareken-watanabeA227_19.jpg: 2.0568624130983233
output/compareken-watanabeA227_20.jpg: 2.04524970252854
Fittest: output/compareken-w

output/compareken-watanabeA234_1.jpg: 2.1433782641215022
output/compareken-watanabeA234_2.jpg: 2.0454101528640662
output/compareken-watanabeA234_3.jpg: 2.017286457856146
output/compareken-watanabeA234_4.jpg: 2.0757436468802473
output/compareken-watanabeA234_5.jpg: 2.017306192466892
output/compareken-watanabeA234_6.jpg: 2.101557206548454
output/compareken-watanabeA234_7.jpg: 2.0524498149955606
output/compareken-watanabeA234_8.jpg: 2.104143146567475
output/compareken-watanabeA234_9.jpg: 2.0588413625952136
output/compareken-watanabeA234_10.jpg: 2.0829537496198607
output/compareken-watanabeA234_11.jpg: 2.1634985866940672
output/compareken-watanabeA234_12.jpg: 2.0951439440065207
output/compareken-watanabeA234_13.jpg: 2.092011452002492
output/compareken-watanabeA234_14.jpg: 2.0699340525807526
output/compareken-watanabeA234_15.jpg: 2.0552634961448084
output/compareken-watanabeA234_16.jpg: 2.0527761870349552
output/compareken-watanabeA234_17.jpg: 2.006304391183482
output/compareken-watanabeA23

output/compareken-watanabeA240_18.jpg: 2.021041068332929
output/compareken-watanabeA240_19.jpg: 2.044266445580429
output/compareken-watanabeA240_20.jpg: 2.14147123009772
Fittest: output/compareken-watanabeA185_13.jpg 1.9168774664399528
output/compareken-watanabeA241_1.jpg: 2.090980752513168
output/compareken-watanabeA241_2.jpg: 2.0946234848669536
output/compareken-watanabeA241_3.jpg: 2.137431538211531
output/compareken-watanabeA241_4.jpg: 2.043741505555707
output/compareken-watanabeA241_5.jpg: 2.0356799041780413
output/compareken-watanabeA241_6.jpg: 2.099153157959795
output/compareken-watanabeA241_7.jpg: 2.086129287870503
output/compareken-watanabeA241_8.jpg: 2.069276817429853
output/compareken-watanabeA241_9.jpg: 2.0930222947634904
output/compareken-watanabeA241_10.jpg: 2.0565459572512137
output/compareken-watanabeA241_11.jpg: 2.0378036888213416
output/compareken-watanabeA241_12.jpg: 2.121809614010248
output/compareken-watanabeA241_13.jpg: 2.0870226199334816
output/compareken-watanabe

output/compareken-watanabeA247_14.jpg: 2.0495502003635497
output/compareken-watanabeA247_15.jpg: 2.0568700039446473
output/compareken-watanabeA247_16.jpg: 2.0773126017449677
output/compareken-watanabeA247_17.jpg: 2.0317876378841007
output/compareken-watanabeA247_18.jpg: 1.99778363932129
output/compareken-watanabeA247_19.jpg: 2.0635882662266054
output/compareken-watanabeA247_20.jpg: 2.0532345580957347
Fittest: output/compareken-watanabeA185_13.jpg 1.9168774664399528
output/compareken-watanabeA248_1.jpg: 2.0917272922591787
output/compareken-watanabeA248_2.jpg: 2.094082761453775
output/compareken-watanabeA248_3.jpg: 2.059545741620589
output/compareken-watanabeA248_4.jpg: 2.0491383832925756
output/compareken-watanabeA248_5.jpg: 2.1343763533309925
output/compareken-watanabeA248_6.jpg: 2.0465994854920897
output/compareken-watanabeA248_7.jpg: 2.1021495124713163
output/compareken-watanabeA248_8.jpg: 2.107205516295991
output/compareken-watanabeA248_9.jpg: 2.094717180263367
output/compareken-wat

In [12]:
evolve('test-images/kristin_chenoweth.jpg', 'test-images/tatyana_ali.jpg', 'kristin-chenoweth','Y')

Start: 1.8877606562991072
output/comparekristin-chenowethY0_1.jpg: 1.9711642485629413
output/comparekristin-chenowethY0_2.jpg: 2.000812873599779
output/comparekristin-chenowethY0_3.jpg: 1.966117269047159
output/comparekristin-chenowethY0_4.jpg: 2.0241703729856875
output/comparekristin-chenowethY0_5.jpg: 1.9692901138220473
output/comparekristin-chenowethY0_6.jpg: 1.9001511378954372
output/comparekristin-chenowethY0_7.jpg: 2.0310431992053886
output/comparekristin-chenowethY0_8.jpg: 2.018843313701309
output/comparekristin-chenowethY0_9.jpg: 2.0423655138765806
output/comparekristin-chenowethY0_10.jpg: 2.0426206521792607
output/comparekristin-chenowethY0_11.jpg: 1.9751780645662236
output/comparekristin-chenowethY0_12.jpg: 2.1260390076135383
output/comparekristin-chenowethY0_13.jpg: 1.9869970441906823
output/comparekristin-chenowethY0_14.jpg: 1.9901131893908253
output/comparekristin-chenowethY0_15.jpg: 2.013095302384892
output/comparekristin-chenowethY0_16.jpg: 2.0916830109682554
output/comp

output/comparekristin-chenowethY6_10.jpg: 1.916023154143764
output/comparekristin-chenowethY6_11.jpg: 1.8710358186106983
output/comparekristin-chenowethY6_12.jpg: 1.9864108505047784
output/comparekristin-chenowethY6_13.jpg: 2.036174649529471
output/comparekristin-chenowethY6_14.jpg: 2.103039012831941
output/comparekristin-chenowethY6_15.jpg: 2.0339083997422693
output/comparekristin-chenowethY6_16.jpg: 2.0094056382672774
output/comparekristin-chenowethY6_17.jpg: 1.9320059148760689
output/comparekristin-chenowethY6_18.jpg: 1.9613806323337801
output/comparekristin-chenowethY6_19.jpg: 1.9963758642755771
output/comparekristin-chenowethY6_20.jpg: 1.9958634844418244
Fittest: output/comparekristin-chenowethY4_15.jpg 1.7934107264076058
output/comparekristin-chenowethY7_1.jpg: 1.937233981764047
output/comparekristin-chenowethY7_2.jpg: 1.9465562022892158
output/comparekristin-chenowethY7_3.jpg: 2.037667307176922
output/comparekristin-chenowethY7_4.jpg: 2.144340514372577
output/comparekristin-chen

output/comparekristin-chenowethY12_19.jpg: 1.9925206706741303
output/comparekristin-chenowethY12_20.jpg: 2.1038530577318193
Fittest: output/comparekristin-chenowethY4_15.jpg 1.7934107264076058
output/comparekristin-chenowethY13_1.jpg: 1.9466891518163452
output/comparekristin-chenowethY13_2.jpg: 1.9278620659762635
output/comparekristin-chenowethY13_3.jpg: 2.0995065681251823
output/comparekristin-chenowethY13_4.jpg: 1.8873028817715478
output/comparekristin-chenowethY13_5.jpg: 1.9382764899439104
output/comparekristin-chenowethY13_6.jpg: 1.9525556990746007
output/comparekristin-chenowethY13_7.jpg: 1.9456367655663562
output/comparekristin-chenowethY13_8.jpg: 1.9877910370345648
output/comparekristin-chenowethY13_9.jpg: 2.053824140308378
output/comparekristin-chenowethY13_10.jpg: 2.006079130082013
output/comparekristin-chenowethY13_11.jpg: 2.0288618660938487
output/comparekristin-chenowethY13_12.jpg: 2.0704797879607706
output/comparekristin-chenowethY13_13.jpg: 1.9560615105005439
output/compa

output/comparekristin-chenowethY19_5.jpg: 1.9696176688029494
output/comparekristin-chenowethY19_6.jpg: 1.9700323817219203
output/comparekristin-chenowethY19_7.jpg: 2.005202969012987
output/comparekristin-chenowethY19_8.jpg: 1.931782338520256
output/comparekristin-chenowethY19_9.jpg: 1.9376395913149633
output/comparekristin-chenowethY19_10.jpg: 2.075196951468205
output/comparekristin-chenowethY19_11.jpg: 2.0586316088657415
output/comparekristin-chenowethY19_12.jpg: 2.0773440112052297
output/comparekristin-chenowethY19_13.jpg: 1.9203330124306328
output/comparekristin-chenowethY19_14.jpg: 2.123405635586711
output/comparekristin-chenowethY19_15.jpg: 2.0892905204452905
output/comparekristin-chenowethY19_16.jpg: 1.9917350938248737
output/comparekristin-chenowethY19_17.jpg: 1.9395752942742064
output/comparekristin-chenowethY19_18.jpg: 2.0103630111037383
output/comparekristin-chenowethY19_19.jpg: 1.941426578432916
output/comparekristin-chenowethY19_20.jpg: 2.0059774115918616
Fittest: output/co

output/comparekristin-chenowethY25_13.jpg: 2.0636645736006836
output/comparekristin-chenowethY25_14.jpg: 1.9819815894339547
output/comparekristin-chenowethY25_15.jpg: 1.867074768530514
output/comparekristin-chenowethY25_16.jpg: 1.9789086312808637
output/comparekristin-chenowethY25_17.jpg: 2.0196519998004505
output/comparekristin-chenowethY25_18.jpg: 1.9493175346898963
output/comparekristin-chenowethY25_19.jpg: 2.0427672710243407
output/comparekristin-chenowethY25_20.jpg: 2.0730991999478805
Fittest: output/comparekristin-chenowethY4_15.jpg 1.7934107264076058
output/comparekristin-chenowethY26_1.jpg: 2.054155338640733
output/comparekristin-chenowethY26_2.jpg: 2.0800089865044
output/comparekristin-chenowethY26_3.jpg: 1.9223576630446462
output/comparekristin-chenowethY26_4.jpg: 1.8782244039823537
output/comparekristin-chenowethY26_5.jpg: 1.9698289100189679
output/comparekristin-chenowethY26_6.jpg: 1.9484834003433387
output/comparekristin-chenowethY26_7.jpg: 2.000122074804258
output/compare

...

output/comparekristin-chenowethY220_11.jpg: 1.9278985830883488
output/comparekristin-chenowethY220_12.jpg: 1.9315417028963426
output/comparekristin-chenowethY220_13.jpg: 1.9856454948828821
output/comparekristin-chenowethY220_14.jpg: 1.9026258400306397
output/comparekristin-chenowethY220_15.jpg: 1.9553934319598787
output/comparekristin-chenowethY220_16.jpg: 1.9418269499754888
output/comparekristin-chenowethY220_17.jpg: 1.882223994844252
output/comparekristin-chenowethY220_18.jpg: 1.976241843503583
output/comparekristin-chenowethY220_19.jpg: 1.9668897895867625
output/comparekristin-chenowethY220_20.jpg: 2.03617690897705
Fittest: output/comparekristin-chenowethY150_10.jpg 1.7136668810280846
output/comparekristin-chenowethY221_1.jpg: 1.9598300933652193
output/comparekristin-chenowethY221_2.jpg: 2.0036227231652943
output/comparekristin-chenowethY221_3.jpg: 1.973780972321761
output/comparekristin-chenowethY221_4.jpg: 1.874925555438217
output/comparekristin-chenowethY221_5.jpg: 2.068244063849

output/comparekristin-chenowethY226_16.jpg: 1.9355235514215654
output/comparekristin-chenowethY226_17.jpg: 2.041798638541474
output/comparekristin-chenowethY226_18.jpg: 1.8786297460781038
output/comparekristin-chenowethY226_19.jpg: 1.927419673606933
output/comparekristin-chenowethY226_20.jpg: 1.967975395634815
Fittest: output/comparekristin-chenowethY150_10.jpg 1.7136668810280846
output/comparekristin-chenowethY227_1.jpg: 1.977520112874406
output/comparekristin-chenowethY227_2.jpg: 1.9846502071540257
output/comparekristin-chenowethY227_3.jpg: 1.9644126735249294
output/comparekristin-chenowethY227_4.jpg: 2.00272099851374
output/comparekristin-chenowethY227_5.jpg: 1.9503602209130415
output/comparekristin-chenowethY227_6.jpg: 2.0105474018324507
output/comparekristin-chenowethY227_7.jpg: 1.9109614816957048
output/comparekristin-chenowethY227_8.jpg: 1.9770040600694496
output/comparekristin-chenowethY227_9.jpg: 1.914382159955446
output/comparekristin-chenowethY227_10.jpg: 1.9778800858691707


output/comparekristin-chenowethY233_1.jpg: 1.836532386705168
output/comparekristin-chenowethY233_2.jpg: 1.9586101096423674
output/comparekristin-chenowethY233_3.jpg: 1.9798687750492818
output/comparekristin-chenowethY233_4.jpg: 1.9805448917029584
output/comparekristin-chenowethY233_5.jpg: 1.93606819845869
output/comparekristin-chenowethY233_6.jpg: 1.9828858110586152
output/comparekristin-chenowethY233_7.jpg: 1.986202254676361
output/comparekristin-chenowethY233_8.jpg: 2.0024305266235056
output/comparekristin-chenowethY233_9.jpg: 1.9160005724786577
output/comparekristin-chenowethY233_10.jpg: 1.9455306638242087
output/comparekristin-chenowethY233_11.jpg: 1.9922804845170714
output/comparekristin-chenowethY233_12.jpg: 2.047436187427153
output/comparekristin-chenowethY233_13.jpg: 2.054027239574708
output/comparekristin-chenowethY233_14.jpg: 2.0715296898373445
output/comparekristin-chenowethY233_15.jpg: 1.919896184535089
output/comparekristin-chenowethY233_16.jpg: 1.9884000729704987
output/c

output/comparekristin-chenowethY239_6.jpg: 1.9639652182865055
output/comparekristin-chenowethY239_7.jpg: 1.9535751361903155
output/comparekristin-chenowethY239_8.jpg: 1.953649378252295
output/comparekristin-chenowethY239_9.jpg: 1.97570656943657
output/comparekristin-chenowethY239_10.jpg: 1.9789418430623475
output/comparekristin-chenowethY239_11.jpg: 1.9853541493197064
output/comparekristin-chenowethY239_12.jpg: 2.0140692366928095
output/comparekristin-chenowethY239_13.jpg: 1.999371467958696
output/comparekristin-chenowethY239_14.jpg: 1.986277501546906
output/comparekristin-chenowethY239_15.jpg: 1.948378607959364
output/comparekristin-chenowethY239_16.jpg: 1.8985037899710853
output/comparekristin-chenowethY239_17.jpg: 1.9825608646013348
output/comparekristin-chenowethY239_18.jpg: 2.0141940355983694
output/comparekristin-chenowethY239_19.jpg: 1.8117776599302677
output/comparekristin-chenowethY239_20.jpg: 2.0088718935717202
Fittest: output/comparekristin-chenowethY150_10.jpg 1.71366688102

output/comparekristin-chenowethY245_11.jpg: 1.8658562339472193
output/comparekristin-chenowethY245_12.jpg: 1.9789473444166241
output/comparekristin-chenowethY245_13.jpg: 1.9427263980395044
output/comparekristin-chenowethY245_14.jpg: 1.9364738222260243
output/comparekristin-chenowethY245_15.jpg: 1.9584995176710862
output/comparekristin-chenowethY245_16.jpg: 1.899401285742078
output/comparekristin-chenowethY245_17.jpg: 2.0869912727871585
output/comparekristin-chenowethY245_18.jpg: 1.953855864716052
output/comparekristin-chenowethY245_19.jpg: 1.9439876792451027
output/comparekristin-chenowethY245_20.jpg: 1.9473839219245905
Fittest: output/comparekristin-chenowethY150_10.jpg 1.7136668810280846
output/comparekristin-chenowethY246_1.jpg: 2.1154466060096926
output/comparekristin-chenowethY246_2.jpg: 1.9356293681090475
output/comparekristin-chenowethY246_3.jpg: 1.8952813344355712
output/comparekristin-chenowethY246_4.jpg: 1.8721967767396108
output/comparekristin-chenowethY246_5.jpg: 1.91883431

In [14]:
evolve('test-images/tatyana_ali.jpg', 'test-images/kristin_chenoweth.jpg', 'tatyana-ali','B')

Start: 1.8877606562991072
output/comparetatyana-aliB0_1.jpg: 1.7406771667924974
output/comparetatyana-aliB0_2.jpg: 1.7560590675437897
output/comparetatyana-aliB0_3.jpg: 1.725655260306564
output/comparetatyana-aliB0_4.jpg: 1.7891914245538272
output/comparetatyana-aliB0_5.jpg: 1.7145595678780592
output/comparetatyana-aliB0_6.jpg: 1.699307199924527
output/comparetatyana-aliB0_7.jpg: 1.7268737216950756
output/comparetatyana-aliB0_8.jpg: 1.7371219036685674
output/comparetatyana-aliB0_9.jpg: 1.7319533642551197
output/comparetatyana-aliB0_10.jpg: 1.717367605395049
output/comparetatyana-aliB0_11.jpg: 1.7256336553213742
output/comparetatyana-aliB0_12.jpg: 1.7826671526597453
output/comparetatyana-aliB0_13.jpg: 1.7136859864901233
output/comparetatyana-aliB0_14.jpg: 1.7197636467223862
output/comparetatyana-aliB0_15.jpg: 1.7904966000608182
output/comparetatyana-aliB0_16.jpg: 1.7112884972422169
output/comparetatyana-aliB0_17.jpg: 1.825844735370866
output/comparetatyana-aliB0_18.jpg: 1.83451378051291

output/comparetatyana-aliB7_4.jpg: 1.6933747709015246
output/comparetatyana-aliB7_5.jpg: 1.7025587382614213
output/comparetatyana-aliB7_6.jpg: 1.8114605717747136
output/comparetatyana-aliB7_7.jpg: 1.805981675306779
output/comparetatyana-aliB7_8.jpg: 1.704066480378959
output/comparetatyana-aliB7_9.jpg: 1.7625329488251467
output/comparetatyana-aliB7_10.jpg: 1.744800890660036
output/comparetatyana-aliB7_11.jpg: 1.7063421739992881
output/comparetatyana-aliB7_12.jpg: 1.7226137291311896
output/comparetatyana-aliB7_13.jpg: 1.7537846708799965
output/comparetatyana-aliB7_14.jpg: 1.791233272371355
output/comparetatyana-aliB7_15.jpg: 1.7408144975752802
output/comparetatyana-aliB7_16.jpg: 1.727684313825252
output/comparetatyana-aliB7_17.jpg: 1.7381217641348041
output/comparetatyana-aliB7_18.jpg: 1.7100087587691282
output/comparetatyana-aliB7_19.jpg: 1.7135209973193695
output/comparetatyana-aliB7_20.jpg: 1.7302587631954527
Fittest: output/comparetatyana-aliB2_6.jpg 1.6529558038004075
output/compare

output/comparetatyana-aliB14_6.jpg: 1.7600971349098244
output/comparetatyana-aliB14_7.jpg: 1.8721251219232569
output/comparetatyana-aliB14_8.jpg: 1.8156932486608082
output/comparetatyana-aliB14_9.jpg: 1.804829414925376
output/comparetatyana-aliB14_10.jpg: 1.776602981758407
output/comparetatyana-aliB14_11.jpg: 1.7202374563705034
output/comparetatyana-aliB14_12.jpg: 1.7414569303215583
output/comparetatyana-aliB14_13.jpg: 1.6716934781187556
output/comparetatyana-aliB14_14.jpg: 1.6840840445583372
output/comparetatyana-aliB14_15.jpg: 1.7920162057921107
output/comparetatyana-aliB14_16.jpg: 1.8048302135574585
output/comparetatyana-aliB14_17.jpg: 1.7429117520052548
output/comparetatyana-aliB14_18.jpg: 1.726962963871699
output/comparetatyana-aliB14_19.jpg: 1.6324498231189732
output/comparetatyana-aliB14_20.jpg: 1.7904667826633287
Fittest: output/comparetatyana-aliB14_19.jpg 1.6324498231189732
output/comparetatyana-aliB15_1.jpg: 1.862649530334302
output/comparetatyana-aliB15_2.jpg: 1.72792974022

output/comparetatyana-aliB21_6.jpg: 1.7766686275253598
output/comparetatyana-aliB21_7.jpg: 1.6985102421810303
output/comparetatyana-aliB21_8.jpg: 1.7844815720707574
output/comparetatyana-aliB21_9.jpg: 1.7808098476435639
output/comparetatyana-aliB21_10.jpg: 1.66954276946025
output/comparetatyana-aliB21_11.jpg: 1.740073967635591
output/comparetatyana-aliB21_12.jpg: 1.7137655285052682
output/comparetatyana-aliB21_13.jpg: 1.7503654237844941
output/comparetatyana-aliB21_14.jpg: 1.7531772823958631
output/comparetatyana-aliB21_15.jpg: 1.8342898702193886
output/comparetatyana-aliB21_16.jpg: 1.6916776804331497
output/comparetatyana-aliB21_17.jpg: 1.7740306116551228
output/comparetatyana-aliB21_18.jpg: 1.6471342550987713
output/comparetatyana-aliB21_19.jpg: 1.7594374663166252
output/comparetatyana-aliB21_20.jpg: 1.7258090087409528
Fittest: output/comparetatyana-aliB15_17.jpg 1.6052829794546506
output/comparetatyana-aliB22_1.jpg: 1.7859513954210517
output/comparetatyana-aliB22_2.jpg: 1.7689070087

output/comparetatyana-aliB28_7.jpg: 1.744021331503864
output/comparetatyana-aliB28_8.jpg: 1.724829163384107
output/comparetatyana-aliB28_9.jpg: 1.7528059554936277
output/comparetatyana-aliB28_10.jpg: 1.7044833697388726
output/comparetatyana-aliB28_11.jpg: 1.8030774585252933
output/comparetatyana-aliB28_12.jpg: 1.7533056982142181
output/comparetatyana-aliB28_13.jpg: 1.8472863451348576
output/comparetatyana-aliB28_14.jpg: 1.7530101679632721
output/comparetatyana-aliB28_15.jpg: 1.740024926937322
output/comparetatyana-aliB28_16.jpg: 1.8352431245430592
output/comparetatyana-aliB28_17.jpg: 1.7841615982027967
output/comparetatyana-aliB28_18.jpg: 1.7351270617419945
output/comparetatyana-aliB28_19.jpg: 1.7294322062471887
output/comparetatyana-aliB28_20.jpg: 1.6968020889426692
Fittest: output/comparetatyana-aliB15_17.jpg 1.6052829794546506
output/comparetatyana-aliB29_1.jpg: 1.7635984268999345
output/comparetatyana-aliB29_2.jpg: 1.7007477091091876
output/comparetatyana-aliB29_3.jpg: 1.8008198458

...

output/comparetatyana-aliB216_6.jpg: 1.6453039126888291
output/comparetatyana-aliB216_7.jpg: 1.85161284287678
output/comparetatyana-aliB216_8.jpg: 1.7747127266316236
output/comparetatyana-aliB216_9.jpg: 1.80473176995717
output/comparetatyana-aliB216_10.jpg: 1.7314981108593952
output/comparetatyana-aliB216_11.jpg: 1.7856133277243813
output/comparetatyana-aliB216_12.jpg: 1.7401035202728048
output/comparetatyana-aliB216_13.jpg: 1.7496908755655984
output/comparetatyana-aliB216_14.jpg: 1.8236438547586697
output/comparetatyana-aliB216_15.jpg: 1.790418200823483
output/comparetatyana-aliB216_16.jpg: 1.763763580492448
output/comparetatyana-aliB216_17.jpg: 1.7121069372167512
output/comparetatyana-aliB216_18.jpg: 1.8064787690081408
output/comparetatyana-aliB216_19.jpg: 1.7657953672660613
output/comparetatyana-aliB216_20.jpg: 1.6838459988299042
Fittest: output/comparetatyana-aliB44_4.jpg 1.566060536916321
output/comparetatyana-aliB217_1.jpg: 1.7431892989462252
output/comparetatyana-aliB217_2.jpg: 

output/comparetatyana-aliB223_4.jpg: 1.8445527277172291
output/comparetatyana-aliB223_5.jpg: 1.8336995756247845
output/comparetatyana-aliB223_6.jpg: 1.8242607191519626
output/comparetatyana-aliB223_7.jpg: 1.742590042741
output/comparetatyana-aliB223_8.jpg: 1.7322274630382184
output/comparetatyana-aliB223_9.jpg: 1.7933286942930824
output/comparetatyana-aliB223_10.jpg: 1.716116919185579
output/comparetatyana-aliB223_11.jpg: 1.8316136638257483
output/comparetatyana-aliB223_12.jpg: 1.7331437954915927
output/comparetatyana-aliB223_13.jpg: 1.6778713765068702
output/comparetatyana-aliB223_14.jpg: 1.6767085037794023
output/comparetatyana-aliB223_15.jpg: 1.71459406898383
output/comparetatyana-aliB223_16.jpg: 1.7815444690703974
output/comparetatyana-aliB223_17.jpg: 1.7483052794103475
output/comparetatyana-aliB223_18.jpg: 1.6928310074856447
output/comparetatyana-aliB223_19.jpg: 1.8561184379163775
output/comparetatyana-aliB223_20.jpg: 1.6688189277028618
Fittest: output/comparetatyana-aliB44_4.jpg 

output/comparetatyana-aliB230_2.jpg: 1.86112586373679
output/comparetatyana-aliB230_3.jpg: 1.766399480192508
output/comparetatyana-aliB230_4.jpg: 1.7528491889798485
output/comparetatyana-aliB230_5.jpg: 1.7560294911125875
output/comparetatyana-aliB230_6.jpg: 1.795696075097958
output/comparetatyana-aliB230_7.jpg: 1.607040374263295
output/comparetatyana-aliB230_8.jpg: 1.8211687525962619
output/comparetatyana-aliB230_9.jpg: 1.7458644757217472
output/comparetatyana-aliB230_10.jpg: 1.7680667949989783
output/comparetatyana-aliB230_11.jpg: 1.708960104443195
output/comparetatyana-aliB230_12.jpg: 1.73791663307949
output/comparetatyana-aliB230_13.jpg: 1.7833728053603612
output/comparetatyana-aliB230_14.jpg: 1.7664339915012053
output/comparetatyana-aliB230_15.jpg: 1.760365203016207
output/comparetatyana-aliB230_16.jpg: 1.7371524651691996
output/comparetatyana-aliB230_17.jpg: 1.7487827489439955
output/comparetatyana-aliB230_18.jpg: 1.6945434942574318
output/comparetatyana-aliB230_19.jpg: 1.83292188

output/comparetatyana-aliB237_1.jpg: 1.880842886861243
output/comparetatyana-aliB237_2.jpg: 1.8088850300346222
output/comparetatyana-aliB237_3.jpg: 1.8370392440923857
output/comparetatyana-aliB237_4.jpg: 1.72052314515508
output/comparetatyana-aliB237_5.jpg: 1.781473669842729
output/comparetatyana-aliB237_6.jpg: 1.7764129352821776
output/comparetatyana-aliB237_7.jpg: 1.8333889364496534
output/comparetatyana-aliB237_8.jpg: 1.8024080506900024
output/comparetatyana-aliB237_9.jpg: 1.7942936004808656
output/comparetatyana-aliB237_10.jpg: 1.796849179237769
output/comparetatyana-aliB237_11.jpg: 1.7852366661581978
output/comparetatyana-aliB237_12.jpg: 1.741547388109151
output/comparetatyana-aliB237_13.jpg: 1.6858346448916282
output/comparetatyana-aliB237_14.jpg: 1.6855175170881438
output/comparetatyana-aliB237_15.jpg: 1.7306244240261437
output/comparetatyana-aliB237_16.jpg: 1.8476843151054088
output/comparetatyana-aliB237_17.jpg: 1.7859020830397694
output/comparetatyana-aliB237_18.jpg: 1.778209

output/comparetatyana-aliB243_20.jpg: 1.7424847834634627
Fittest: output/comparetatyana-aliB44_4.jpg 1.566060536916321
output/comparetatyana-aliB244_1.jpg: 1.7423538764416882
output/comparetatyana-aliB244_2.jpg: 1.7705617122815194
output/comparetatyana-aliB244_3.jpg: 1.8396507333581549
output/comparetatyana-aliB244_4.jpg: 1.804814604457724
output/comparetatyana-aliB244_5.jpg: 1.794754835107951
output/comparetatyana-aliB244_6.jpg: 1.7492133832603913
output/comparetatyana-aliB244_7.jpg: 1.7325207886070007
output/comparetatyana-aliB244_8.jpg: 1.7333681245448036
output/comparetatyana-aliB244_9.jpg: 1.8056617865163356
output/comparetatyana-aliB244_10.jpg: 1.708970780892236
output/comparetatyana-aliB244_11.jpg: 1.7732898053050863
output/comparetatyana-aliB244_12.jpg: 1.7073343387210205
output/comparetatyana-aliB244_13.jpg: 1.716242468424038
output/comparetatyana-aliB244_14.jpg: 1.7835653151419575
output/comparetatyana-aliB244_15.jpg: 1.7858296903882045
output/comparetatyana-aliB244_16.jpg: 1

In [15]:
evolve('test-images/kristin_chenoweth.jpg', 'test-images/george_lopez.jpg', 'kristin-chenoweth','D')

Start: 1.8165709664049365
output/comparekristin-chenowethD0_1.jpg: 1.666154369872789
output/comparekristin-chenowethD0_2.jpg: 1.6143486070047568
output/comparekristin-chenowethD0_3.jpg: 1.891588916638189
output/comparekristin-chenowethD0_4.jpg: 1.5991753481743882
output/comparekristin-chenowethD0_5.jpg: 1.6710462660437528
output/comparekristin-chenowethD0_6.jpg: 2.016617914566359
output/comparekristin-chenowethD0_7.jpg: 1.6085313816575342
output/comparekristin-chenowethD0_8.jpg: 1.8283648240812913
output/comparekristin-chenowethD0_9.jpg: 1.6537029300935628
output/comparekristin-chenowethD0_10.jpg: 1.8306212223237701
output/comparekristin-chenowethD0_11.jpg: 1.683513881698364
output/comparekristin-chenowethD0_12.jpg: 1.8695793456779064
output/comparekristin-chenowethD0_13.jpg: 1.6767124066879293
output/comparekristin-chenowethD0_14.jpg: 1.608940999837124
output/comparekristin-chenowethD0_15.jpg: 1.867824373197084
output/comparekristin-chenowethD0_16.jpg: 1.5996875605777143
output/compar

output/comparekristin-chenowethD6_10.jpg: 1.654783793120001
output/comparekristin-chenowethD6_11.jpg: 1.6392838921250943
output/comparekristin-chenowethD6_12.jpg: 1.8444458551318759
output/comparekristin-chenowethD6_13.jpg: 1.874389779477267
output/comparekristin-chenowethD6_14.jpg: 1.6212361440751395
output/comparekristin-chenowethD6_15.jpg: 1.9016840212404893
output/comparekristin-chenowethD6_16.jpg: 1.6491504102305536
output/comparekristin-chenowethD6_17.jpg: 1.8972769526199
output/comparekristin-chenowethD6_18.jpg: 1.6550982844602076
output/comparekristin-chenowethD6_19.jpg: 1.638856008537114
output/comparekristin-chenowethD6_20.jpg: 1.7914777704427416
Fittest: output/comparekristin-chenowethD4_10.jpg 1.5694859736708147
output/comparekristin-chenowethD7_1.jpg: 1.6417994205707236
output/comparekristin-chenowethD7_2.jpg: 1.5573154223573393
output/comparekristin-chenowethD7_3.jpg: 1.6055653851490455
output/comparekristin-chenowethD7_4.jpg: 1.572334239487915
output/comparekristin-cheno

output/comparekristin-chenowethD12_19.jpg: 1.5914532756765294
output/comparekristin-chenowethD12_20.jpg: 1.6066498478426772
Fittest: output/comparekristin-chenowethD7_2.jpg 1.5573154223573393
output/comparekristin-chenowethD13_1.jpg: 1.6041347160477821
output/comparekristin-chenowethD13_2.jpg: 1.6396648647642824
output/comparekristin-chenowethD13_3.jpg: 1.639573281269266
output/comparekristin-chenowethD13_4.jpg: 1.6417317195389853
output/comparekristin-chenowethD13_5.jpg: 1.5706299357231788
output/comparekristin-chenowethD13_6.jpg: 1.580592520741518
output/comparekristin-chenowethD13_7.jpg: 1.6401037559029705
output/comparekristin-chenowethD13_8.jpg: 2.0293350276090862
output/comparekristin-chenowethD13_9.jpg: 1.5876979529118154
output/comparekristin-chenowethD13_10.jpg: 1.6079667831960804
output/comparekristin-chenowethD13_11.jpg: 1.589768949297968
output/comparekristin-chenowethD13_12.jpg: 1.6235382902201771
output/comparekristin-chenowethD13_13.jpg: 1.5817018973913541
output/compare

output/comparekristin-chenowethD19_5.jpg: 1.6198306875236872
output/comparekristin-chenowethD19_6.jpg: 1.830824809465231
output/comparekristin-chenowethD19_7.jpg: 1.5899955205345364
output/comparekristin-chenowethD19_8.jpg: 1.6018284142110797
output/comparekristin-chenowethD19_9.jpg: 1.7568342768693685
output/comparekristin-chenowethD19_10.jpg: 1.5415617644040926
output/comparekristin-chenowethD19_11.jpg: 1.5698547249644137
output/comparekristin-chenowethD19_12.jpg: 1.9138474431561288
output/comparekristin-chenowethD19_13.jpg: 1.570360985733997
output/comparekristin-chenowethD19_14.jpg: 1.5814028468409767
output/comparekristin-chenowethD19_15.jpg: 1.6031367290295628
output/comparekristin-chenowethD19_16.jpg: 1.5930227078619088
output/comparekristin-chenowethD19_17.jpg: 1.897204837088442
output/comparekristin-chenowethD19_18.jpg: 1.6090454091968869
output/comparekristin-chenowethD19_19.jpg: 1.560322868372942
output/comparekristin-chenowethD19_20.jpg: 1.5849863849043637
Fittest: output/c

output/comparekristin-chenowethD25_12.jpg: 1.6020692984375562
output/comparekristin-chenowethD25_13.jpg: 1.5641454055026203
output/comparekristin-chenowethD25_14.jpg: 1.5873171395580044
output/comparekristin-chenowethD25_15.jpg: 1.585706096887172
output/comparekristin-chenowethD25_16.jpg: 1.9556514772405071
output/comparekristin-chenowethD25_17.jpg: 2.0236556687434963
output/comparekristin-chenowethD25_18.jpg: 1.9214107373114362
output/comparekristin-chenowethD25_19.jpg: 1.9056238178945788
output/comparekristin-chenowethD25_20.jpg: 1.558231936259271
Fittest: output/comparekristin-chenowethD18_6.jpg 1.5295199649529945
output/comparekristin-chenowethD26_1.jpg: 1.5250715318727541
output/comparekristin-chenowethD26_2.jpg: 1.6110392675372072
output/comparekristin-chenowethD26_3.jpg: 1.582118970851668
output/comparekristin-chenowethD26_4.jpg: 1.5682621077412002
output/comparekristin-chenowethD26_5.jpg: 1.5865703687653339
output/comparekristin-chenowethD26_6.jpg: 1.56287606155529
output/compa

...

output/comparekristin-chenowethD220_6.jpg: 1.5958440725711123
output/comparekristin-chenowethD220_7.jpg: 2.065116179787897
output/comparekristin-chenowethD220_8.jpg: 1.5966632370542748
output/comparekristin-chenowethD220_9.jpg: 1.5921739993802893
output/comparekristin-chenowethD220_10.jpg: 1.5424068535290623
output/comparekristin-chenowethD220_11.jpg: 1.5863103503545029
output/comparekristin-chenowethD220_12.jpg: 1.568429702194099
output/comparekristin-chenowethD220_13.jpg: 1.5861350264420777
output/comparekristin-chenowethD220_14.jpg: 1.5719891261130932
output/comparekristin-chenowethD220_15.jpg: 1.6014404745080149
output/comparekristin-chenowethD220_16.jpg: 1.6010592695738577
output/comparekristin-chenowethD220_17.jpg: 1.5843155548309924
output/comparekristin-chenowethD220_18.jpg: 2.029925012665674
output/comparekristin-chenowethD220_19.jpg: 1.843466952162565
output/comparekristin-chenowethD220_20.jpg: 1.859507160881129
Fittest: output/comparekristin-chenowethD30_13.jpg 1.50498789066

output/comparekristin-chenowethD226_11.jpg: 1.58373968371136
output/comparekristin-chenowethD226_12.jpg: 1.5929831539678543
output/comparekristin-chenowethD226_13.jpg: 1.620012271851928
output/comparekristin-chenowethD226_14.jpg: 1.8974593146207615
output/comparekristin-chenowethD226_15.jpg: 1.5940666136750898
output/comparekristin-chenowethD226_16.jpg: 1.577942723010735
output/comparekristin-chenowethD226_17.jpg: 1.8573022963140455
output/comparekristin-chenowethD226_18.jpg: 1.584450203231475
output/comparekristin-chenowethD226_19.jpg: 1.60730591526749
output/comparekristin-chenowethD226_20.jpg: 1.5632843322658234
Fittest: output/comparekristin-chenowethD30_13.jpg 1.5049878906677252
output/comparekristin-chenowethD227_1.jpg: 1.967242983932859
output/comparekristin-chenowethD227_2.jpg: 1.9594155360009886
output/comparekristin-chenowethD227_3.jpg: 1.8735159861341328
output/comparekristin-chenowethD227_4.jpg: 1.5793267644909803
output/comparekristin-chenowethD227_5.jpg: 1.555660562374760

output/comparekristin-chenowethD232_16.jpg: 1.595982503135707
output/comparekristin-chenowethD232_17.jpg: 1.6094584818565647
output/comparekristin-chenowethD232_18.jpg: 1.6116193853697083
output/comparekristin-chenowethD232_19.jpg: 1.5921140865652026
output/comparekristin-chenowethD232_20.jpg: 1.8886453431966645
Fittest: output/comparekristin-chenowethD30_13.jpg 1.5049878906677252
output/comparekristin-chenowethD233_1.jpg: 1.588856330930711
output/comparekristin-chenowethD233_2.jpg: 1.9437877047818715
output/comparekristin-chenowethD233_3.jpg: 1.5963204532343866
output/comparekristin-chenowethD233_4.jpg: 1.5765849668974123
output/comparekristin-chenowethD233_5.jpg: 1.6035681340215056
output/comparekristin-chenowethD233_6.jpg: 1.5814575912096072
output/comparekristin-chenowethD233_7.jpg: 2.0125161167580186
output/comparekristin-chenowethD233_8.jpg: 1.622048399976763
output/comparekristin-chenowethD233_9.jpg: 1.8961727677579225
output/comparekristin-chenowethD233_10.jpg: 1.59772052565823

output/comparekristin-chenowethD239_1.jpg: 1.606337986824843
output/comparekristin-chenowethD239_2.jpg: 1.5667743723155338
output/comparekristin-chenowethD239_3.jpg: 1.6071899109562222
output/comparekristin-chenowethD239_4.jpg: 1.9783544238457926
output/comparekristin-chenowethD239_5.jpg: 1.588613056359984
output/comparekristin-chenowethD239_6.jpg: 1.594191560401481
output/comparekristin-chenowethD239_7.jpg: 1.5655643433415345
output/comparekristin-chenowethD239_8.jpg: 1.9368799577279074
output/comparekristin-chenowethD239_9.jpg: 1.8822967880361186
output/comparekristin-chenowethD239_10.jpg: 1.5888978251727484
output/comparekristin-chenowethD239_11.jpg: 1.5807803465765407
output/comparekristin-chenowethD239_12.jpg: 2.0020548242909664
output/comparekristin-chenowethD239_13.jpg: 1.6242094234251925
output/comparekristin-chenowethD239_14.jpg: 1.5951880385894501
output/comparekristin-chenowethD239_15.jpg: 1.578402999400907
output/comparekristin-chenowethD239_16.jpg: 2.025905495002463
output

output/comparekristin-chenowethD245_6.jpg: 1.5772793662470894
output/comparekristin-chenowethD245_7.jpg: 2.0092531895619383
output/comparekristin-chenowethD245_8.jpg: 1.6232711582900246
output/comparekristin-chenowethD245_9.jpg: 1.5681842282369487
output/comparekristin-chenowethD245_10.jpg: 1.9194071337652583
output/comparekristin-chenowethD245_11.jpg: 1.5922973445043689
output/comparekristin-chenowethD245_12.jpg: 1.5922823783831959
output/comparekristin-chenowethD245_13.jpg: 1.5897033136505923
output/comparekristin-chenowethD245_14.jpg: 1.574593135447247
output/comparekristin-chenowethD245_15.jpg: 1.617123882374568
output/comparekristin-chenowethD245_16.jpg: 2.017065669871381
output/comparekristin-chenowethD245_17.jpg: 1.6029609393027555
output/comparekristin-chenowethD245_18.jpg: 1.553102645224202
output/comparekristin-chenowethD245_19.jpg: 1.5732155936496162
output/comparekristin-chenowethD245_20.jpg: 1.5943461105747425
Fittest: output/comparekristin-chenowethD30_13.jpg 1.5049878906

In [16]:
evolve('test-images/george_lopez.jpg', 'test-images/kristin_chenoweth.jpg', 'george-lopez','B')

Start: 1.8165709664049365
output/comparegeorge-lopezB0_1.jpg: 1.7666112997828447
output/comparegeorge-lopezB0_2.jpg: 1.8118877347358286
output/comparegeorge-lopezB0_3.jpg: 1.7727613463079193
output/comparegeorge-lopezB0_4.jpg: 1.7875415681731797
output/comparegeorge-lopezB0_5.jpg: 1.8988314484656592
output/comparegeorge-lopezB0_6.jpg: 1.7897109966489504
output/comparegeorge-lopezB0_7.jpg: 1.8001808433896285
output/comparegeorge-lopezB0_8.jpg: 1.812951311784731
output/comparegeorge-lopezB0_9.jpg: 1.7849625350296368
output/comparegeorge-lopezB0_10.jpg: 1.787973138030004
output/comparegeorge-lopezB0_11.jpg: 1.7426812335999213
output/comparegeorge-lopezB0_12.jpg: 1.8000265731415557
output/comparegeorge-lopezB0_13.jpg: 1.7856754553206358
output/comparegeorge-lopezB0_14.jpg: 1.7988780430995275
output/comparegeorge-lopezB0_15.jpg: 1.814521609063475
output/comparegeorge-lopezB0_16.jpg: 1.7667407327413909
output/comparegeorge-lopezB0_17.jpg: 1.7935199033211844
output/comparegeorge-lopezB0_18.jp

output/comparegeorge-lopezB7_1.jpg: 1.791326802934332
output/comparegeorge-lopezB7_2.jpg: 1.8238089999885958
output/comparegeorge-lopezB7_3.jpg: 1.766891703495687
output/comparegeorge-lopezB7_4.jpg: 1.7830560928200505
output/comparegeorge-lopezB7_5.jpg: 1.8073212678254023
output/comparegeorge-lopezB7_6.jpg: 1.7848549828988411
output/comparegeorge-lopezB7_7.jpg: 1.7907283192147139
output/comparegeorge-lopezB7_8.jpg: 1.8144567316891305
output/comparegeorge-lopezB7_9.jpg: 1.7847748722220897
output/comparegeorge-lopezB7_10.jpg: 1.7845756570881715
output/comparegeorge-lopezB7_11.jpg: 1.8150010967586945
output/comparegeorge-lopezB7_12.jpg: 1.783844138584298
output/comparegeorge-lopezB7_13.jpg: 1.8099780466754674
output/comparegeorge-lopezB7_14.jpg: 1.8053755116229029
output/comparegeorge-lopezB7_15.jpg: 1.7624631855476942
output/comparegeorge-lopezB7_16.jpg: 1.7824698535563392
output/comparegeorge-lopezB7_17.jpg: 1.7367758440411483
output/comparegeorge-lopezB7_18.jpg: 1.7949807865693117
outp

output/comparegeorge-lopezB14_1.jpg: 1.8196839404765892
output/comparegeorge-lopezB14_2.jpg: 1.7902342386739214
output/comparegeorge-lopezB14_3.jpg: 1.783785428509598
output/comparegeorge-lopezB14_4.jpg: 1.7701252330767712
output/comparegeorge-lopezB14_5.jpg: 1.7990867651944578
output/comparegeorge-lopezB14_6.jpg: 1.8334417087688697
output/comparegeorge-lopezB14_7.jpg: 1.795212450076065
output/comparegeorge-lopezB14_8.jpg: 1.7825097601686466
output/comparegeorge-lopezB14_9.jpg: 1.7986902299765015
output/comparegeorge-lopezB14_10.jpg: 1.722731153692316
output/comparegeorge-lopezB14_11.jpg: 1.7876119507255332
output/comparegeorge-lopezB14_12.jpg: 1.7767484593655656
output/comparegeorge-lopezB14_13.jpg: 1.811190825128318
output/comparegeorge-lopezB14_14.jpg: 1.797210376438067
output/comparegeorge-lopezB14_15.jpg: 1.7713681205283665
output/comparegeorge-lopezB14_16.jpg: 1.7760426838412604
output/comparegeorge-lopezB14_17.jpg: 1.7863716101141691
output/comparegeorge-lopezB14_18.jpg: 1.80188

output/comparegeorge-lopezB20_20.jpg: 1.7790934604362239
Fittest: output/comparegeorge-lopezB15_16.jpg 1.7097450984617515
output/comparegeorge-lopezB21_1.jpg: 1.7873392552018281
output/comparegeorge-lopezB21_2.jpg: 1.8005014742974421
output/comparegeorge-lopezB21_3.jpg: 1.7763681055164313
output/comparegeorge-lopezB21_4.jpg: 1.8063519171683997
output/comparegeorge-lopezB21_5.jpg: 1.769132466811281
output/comparegeorge-lopezB21_6.jpg: 1.7532592535939435
output/comparegeorge-lopezB21_7.jpg: 1.7681106635302515
output/comparegeorge-lopezB21_8.jpg: 1.7740041399777067
output/comparegeorge-lopezB21_9.jpg: 1.748449189426935
output/comparegeorge-lopezB21_10.jpg: 1.8108327186403423
output/comparegeorge-lopezB21_11.jpg: 1.7896712930910352
output/comparegeorge-lopezB21_12.jpg: 1.7918683967783249
output/comparegeorge-lopezB21_13.jpg: 1.7649536579415552
output/comparegeorge-lopezB21_14.jpg: 1.76416735578273
output/comparegeorge-lopezB21_15.jpg: 1.7537820195573337
output/comparegeorge-lopezB21_16.jpg

output/comparegeorge-lopezB27_18.jpg: 1.7694597196532542
output/comparegeorge-lopezB27_19.jpg: 1.7361142762622972
output/comparegeorge-lopezB27_20.jpg: 1.874077742965011
Fittest: output/comparegeorge-lopezB26_4.jpg 1.707624026979676
output/comparegeorge-lopezB28_1.jpg: 1.7913531053416951
output/comparegeorge-lopezB28_2.jpg: 1.7926917052281717
output/comparegeorge-lopezB28_3.jpg: 1.7860760635933786
output/comparegeorge-lopezB28_4.jpg: 1.7864693424435032
output/comparegeorge-lopezB28_5.jpg: 1.7758989863426309
output/comparegeorge-lopezB28_6.jpg: 1.817511075870428
output/comparegeorge-lopezB28_7.jpg: 1.8090981119711433
output/comparegeorge-lopezB28_8.jpg: 1.7747105600094564
output/comparegeorge-lopezB28_9.jpg: 1.8071754749657991
output/comparegeorge-lopezB28_10.jpg: 1.8013448354444372
output/comparegeorge-lopezB28_11.jpg: 1.796969320205998
output/comparegeorge-lopezB28_12.jpg: 1.7865500478296434
output/comparegeorge-lopezB28_13.jpg: 1.7837708117155435
output/comparegeorge-lopezB28_14.jpg:

...

output/comparegeorge-lopezB219_7.jpg: 1.783996540949205
output/comparegeorge-lopezB219_8.jpg: 1.756987165185731
output/comparegeorge-lopezB219_9.jpg: 1.8508835862912463
output/comparegeorge-lopezB219_10.jpg: 1.8519897861387493
output/comparegeorge-lopezB219_11.jpg: 1.761822063541365
output/comparegeorge-lopezB219_12.jpg: 1.776041481011112
output/comparegeorge-lopezB219_13.jpg: 1.7728521070254848
output/comparegeorge-lopezB219_14.jpg: 1.8343009988099495
output/comparegeorge-lopezB219_15.jpg: 1.7927797696828323
output/comparegeorge-lopezB219_16.jpg: 1.7453865891271414
output/comparegeorge-lopezB219_17.jpg: 1.8063914805440104
output/comparegeorge-lopezB219_18.jpg: 1.7812168322223672
output/comparegeorge-lopezB219_19.jpg: 1.7928464131661246
output/comparegeorge-lopezB219_20.jpg: 1.7709459320261116
Fittest: output/comparegeorge-lopezB177_14.jpg 1.6811418185193978
output/comparegeorge-lopezB220_1.jpg: 1.8012913926716687
output/comparegeorge-lopezB220_2.jpg: 1.7825231857234807
output/compareg

output/comparegeorge-lopezB226_2.jpg: 1.780420190323603
output/comparegeorge-lopezB226_3.jpg: 1.7922686954275882
output/comparegeorge-lopezB226_4.jpg: 1.7976510385081879
output/comparegeorge-lopezB226_5.jpg: 1.7543608252298695
output/comparegeorge-lopezB226_6.jpg: 1.7899042934561014
output/comparegeorge-lopezB226_7.jpg: 1.8001233718208445
output/comparegeorge-lopezB226_8.jpg: 1.7556308880623293
output/comparegeorge-lopezB226_9.jpg: 1.790096908449643
output/comparegeorge-lopezB226_10.jpg: 1.8027101298536565
output/comparegeorge-lopezB226_11.jpg: 1.7631029274867929
output/comparegeorge-lopezB226_12.jpg: 1.7636480063455566
output/comparegeorge-lopezB226_13.jpg: 1.7606842881124736
output/comparegeorge-lopezB226_14.jpg: 1.76071779318087
output/comparegeorge-lopezB226_15.jpg: 1.8563840925215813
output/comparegeorge-lopezB226_16.jpg: 1.775368062506847
output/comparegeorge-lopezB226_17.jpg: 1.791314422262149
output/comparegeorge-lopezB226_18.jpg: 1.810971714935468
output/comparegeorge-lopezB22

output/comparegeorge-lopezB232_19.jpg: 1.807760374821652
output/comparegeorge-lopezB232_20.jpg: 1.7722376618331772
Fittest: output/comparegeorge-lopezB177_14.jpg 1.6811418185193978
output/comparegeorge-lopezB233_1.jpg: 1.7830523538820824
output/comparegeorge-lopezB233_2.jpg: 1.8073617368377155
output/comparegeorge-lopezB233_3.jpg: 1.7836245175455514
output/comparegeorge-lopezB233_4.jpg: 1.7770047388049068
output/comparegeorge-lopezB233_5.jpg: 1.7778982161986914
output/comparegeorge-lopezB233_6.jpg: 1.781926504296801
output/comparegeorge-lopezB233_7.jpg: 1.798008780776042
output/comparegeorge-lopezB233_8.jpg: 1.7880508328433868
output/comparegeorge-lopezB233_9.jpg: 1.917003448596342
output/comparegeorge-lopezB233_10.jpg: 1.7875884300070748
output/comparegeorge-lopezB233_11.jpg: 1.7878249078160988
output/comparegeorge-lopezB233_12.jpg: 1.7978899837498992
output/comparegeorge-lopezB233_13.jpg: 1.7459290890929933
output/comparegeorge-lopezB233_14.jpg: 1.8829845872222126
output/comparegeorg

output/comparegeorge-lopezB239_14.jpg: 1.7637625643060635
output/comparegeorge-lopezB239_15.jpg: 1.7451553699217017
output/comparegeorge-lopezB239_16.jpg: 1.7287827508240214
output/comparegeorge-lopezB239_17.jpg: 1.745618112559029
output/comparegeorge-lopezB239_18.jpg: 1.7687114515864817
output/comparegeorge-lopezB239_19.jpg: 1.778970931720509
output/comparegeorge-lopezB239_20.jpg: 1.802827089922232
Fittest: output/comparegeorge-lopezB177_14.jpg 1.6811418185193978
output/comparegeorge-lopezB240_1.jpg: 1.7551009006247442
output/comparegeorge-lopezB240_2.jpg: 1.8399097444709107
output/comparegeorge-lopezB240_3.jpg: 1.7834410815015669
output/comparegeorge-lopezB240_4.jpg: 1.817786580171183
output/comparegeorge-lopezB240_5.jpg: 1.7786849312855608
output/comparegeorge-lopezB240_6.jpg: 1.7296925816559905
output/comparegeorge-lopezB240_7.jpg: 1.773981103242714
output/comparegeorge-lopezB240_8.jpg: 1.747411250315905
output/comparegeorge-lopezB240_9.jpg: 1.798228343689556
output/comparegeorge-l

output/comparegeorge-lopezB246_10.jpg: 1.800294864405112
output/comparegeorge-lopezB246_11.jpg: 1.7522790014986998
output/comparegeorge-lopezB246_12.jpg: 1.7996979239043736
output/comparegeorge-lopezB246_13.jpg: 1.7636441209755298
output/comparegeorge-lopezB246_14.jpg: 1.8267743223857371
output/comparegeorge-lopezB246_15.jpg: 1.752408105987157
output/comparegeorge-lopezB246_16.jpg: 1.7965357627006886
output/comparegeorge-lopezB246_17.jpg: 1.8173036961127604
output/comparegeorge-lopezB246_18.jpg: 1.793098134894878
output/comparegeorge-lopezB246_19.jpg: 1.7918875479523038
output/comparegeorge-lopezB246_20.jpg: 1.8876721382096944
Fittest: output/comparegeorge-lopezB177_14.jpg 1.6811418185193978
output/comparegeorge-lopezB247_1.jpg: 1.7384564576847432
output/comparegeorge-lopezB247_2.jpg: 1.7598393469628395
output/comparegeorge-lopezB247_3.jpg: 1.7756206946237976
output/comparegeorge-lopezB247_4.jpg: 1.750890658950445
output/comparegeorge-lopezB247_5.jpg: 1.7649144902776097
output/compareg

In [17]:
evolve('test-images/tatyana_ali.jpg', 'test-images/ken_watanabe.jpg', 'tatyana-ali','C')

Start: 1.4172949709118567
output/comparetatyana-aliC0_1.jpg: 1.5738407097376585
output/comparetatyana-aliC0_2.jpg: 1.669021117824284
output/comparetatyana-aliC0_3.jpg: 1.588670179007001
output/comparetatyana-aliC0_4.jpg: 1.6194716589544456
output/comparetatyana-aliC0_5.jpg: 1.6357911583653084
output/comparetatyana-aliC0_6.jpg: 1.59324493890853
output/comparetatyana-aliC0_7.jpg: 1.5734665615592305
output/comparetatyana-aliC0_8.jpg: 1.596753139378034
output/comparetatyana-aliC0_9.jpg: 1.6172172866938679
output/comparetatyana-aliC0_10.jpg: 1.5987751105757804
output/comparetatyana-aliC0_11.jpg: 1.5749005861886398
output/comparetatyana-aliC0_12.jpg: 1.5874262786499722
output/comparetatyana-aliC0_13.jpg: 1.5008846479157867
output/comparetatyana-aliC0_14.jpg: 1.6189097309695746
output/comparetatyana-aliC0_15.jpg: 1.6331129802618771
output/comparetatyana-aliC0_16.jpg: 1.6095675416572748
output/comparetatyana-aliC0_17.jpg: 1.636168861835087
output/comparetatyana-aliC0_18.jpg: 1.5481196532944033

output/comparetatyana-aliC7_5.jpg: 1.558994417346021
output/comparetatyana-aliC7_6.jpg: 1.6107189192482858
output/comparetatyana-aliC7_7.jpg: 1.6111840815432217
output/comparetatyana-aliC7_8.jpg: 1.5162523810451631
output/comparetatyana-aliC7_9.jpg: 1.5629270581481047
output/comparetatyana-aliC7_10.jpg: 1.5741130958369294
output/comparetatyana-aliC7_11.jpg: 1.580078486137127
output/comparetatyana-aliC7_12.jpg: 1.5926835463537623
output/comparetatyana-aliC7_13.jpg: 1.6141441897621363
output/comparetatyana-aliC7_14.jpg: 1.602417596052669
output/comparetatyana-aliC7_15.jpg: 1.59880358984257
output/comparetatyana-aliC7_16.jpg: 1.614212709299528
output/comparetatyana-aliC7_17.jpg: 1.6257829852618393
output/comparetatyana-aliC7_18.jpg: 1.6676752955898022
output/comparetatyana-aliC7_19.jpg: 1.6387906663136038
output/comparetatyana-aliC7_20.jpg: 1.5830456771313361
Fittest: test-images/tatyana_ali.jpg 1.4172949709118567
output/comparetatyana-aliC8_1.jpg: 1.57691045057877
output/comparetatyana-a

output/comparetatyana-aliC14_8.jpg: 1.547862834797034
output/comparetatyana-aliC14_9.jpg: 1.6348110976188914
output/comparetatyana-aliC14_10.jpg: 1.554987831808468
output/comparetatyana-aliC14_11.jpg: 1.5800846199509029
output/comparetatyana-aliC14_12.jpg: 1.5829703084729918
output/comparetatyana-aliC14_13.jpg: 1.607910457026367
output/comparetatyana-aliC14_14.jpg: 1.633782913664625
output/comparetatyana-aliC14_15.jpg: 1.5949874716978747
output/comparetatyana-aliC14_16.jpg: 1.5903065575493887
output/comparetatyana-aliC14_17.jpg: 1.5956328426564148
output/comparetatyana-aliC14_18.jpg: 1.6166234331683882
output/comparetatyana-aliC14_19.jpg: 1.6120002292604716
output/comparetatyana-aliC14_20.jpg: 1.6031262125510262
Fittest: test-images/tatyana_ali.jpg 1.4172949709118567
output/comparetatyana-aliC15_1.jpg: 1.5637679471926642
output/comparetatyana-aliC15_2.jpg: 1.5918181883675289
output/comparetatyana-aliC15_3.jpg: 1.559194537385039
output/comparetatyana-aliC15_4.jpg: 1.5860263873403093
out

output/comparetatyana-aliC21_10.jpg: 1.5889462758341
output/comparetatyana-aliC21_11.jpg: 1.5978294134850426
output/comparetatyana-aliC21_12.jpg: 1.627903710102076
output/comparetatyana-aliC21_13.jpg: 1.5739470726812534
output/comparetatyana-aliC21_14.jpg: 1.6197839390210524
output/comparetatyana-aliC21_15.jpg: 1.5744761817997546
output/comparetatyana-aliC21_16.jpg: 1.6256006478752272
output/comparetatyana-aliC21_17.jpg: 1.5607443150038933
output/comparetatyana-aliC21_18.jpg: 1.6299398323059298
output/comparetatyana-aliC21_19.jpg: 1.582176667211741
output/comparetatyana-aliC21_20.jpg: 1.5793387254300204
Fittest: test-images/tatyana_ali.jpg 1.4172949709118567
output/comparetatyana-aliC22_1.jpg: 1.6235319025791264
output/comparetatyana-aliC22_2.jpg: 1.584534032996125
output/comparetatyana-aliC22_3.jpg: 1.5667999498506044
output/comparetatyana-aliC22_4.jpg: 1.575543754552522
output/comparetatyana-aliC22_5.jpg: 1.6054308373659265
output/comparetatyana-aliC22_6.jpg: 1.5905828975780671
outpu

output/comparetatyana-aliC28_11.jpg: 1.5577092079382224
output/comparetatyana-aliC28_12.jpg: 1.5915149335273093
output/comparetatyana-aliC28_13.jpg: 1.6407868997685686
output/comparetatyana-aliC28_14.jpg: 1.5895297076286776
output/comparetatyana-aliC28_15.jpg: 1.601740687568476
output/comparetatyana-aliC28_16.jpg: 1.6105991511927036
output/comparetatyana-aliC28_17.jpg: 1.5625190456485558
output/comparetatyana-aliC28_18.jpg: 1.5727107804468408
output/comparetatyana-aliC28_19.jpg: 1.4817242480225907
output/comparetatyana-aliC28_20.jpg: 1.62547918229306
Fittest: test-images/tatyana_ali.jpg 1.4172949709118567
output/comparetatyana-aliC29_1.jpg: 1.5936639910402624
output/comparetatyana-aliC29_2.jpg: 1.5911435335021848
output/comparetatyana-aliC29_3.jpg: 1.6391320388772304
output/comparetatyana-aliC29_4.jpg: 1.5900501726518375
output/comparetatyana-aliC29_5.jpg: 1.5303680671091695
output/comparetatyana-aliC29_6.jpg: 1.6159372949652213
output/comparetatyana-aliC29_7.jpg: 1.5646038733809071
ou

...

output/comparetatyana-aliC218_1.jpg: 1.5831984789641687
output/comparetatyana-aliC218_2.jpg: 1.567618516684227
output/comparetatyana-aliC218_3.jpg: 1.581841078441462
output/comparetatyana-aliC218_4.jpg: 1.609217688016396
output/comparetatyana-aliC218_5.jpg: 1.6136220685404796
output/comparetatyana-aliC218_6.jpg: 1.6332627513489693
output/comparetatyana-aliC218_7.jpg: 1.5895783135611334
output/comparetatyana-aliC218_8.jpg: 1.5729760129060235
output/comparetatyana-aliC218_9.jpg: 1.6263323609814921
output/comparetatyana-aliC218_10.jpg: 1.6630734041691912
output/comparetatyana-aliC218_11.jpg: 1.5222629747254852
output/comparetatyana-aliC218_12.jpg: 1.5760587870006537
output/comparetatyana-aliC218_13.jpg: 1.6384497771478892
output/comparetatyana-aliC218_14.jpg: 1.6283184599982774
output/comparetatyana-aliC218_15.jpg: 1.6063267515726558
output/comparetatyana-aliC218_16.jpg: 1.617568683600908
output/comparetatyana-aliC218_17.jpg: 1.6393027916655694
output/comparetatyana-aliC218_18.jpg: 1.6600

output/comparetatyana-aliC225_1.jpg: 1.5740408157479218
output/comparetatyana-aliC225_2.jpg: 1.6270226758252808
output/comparetatyana-aliC225_3.jpg: 1.5776012408303641
output/comparetatyana-aliC225_4.jpg: 1.61199054380598
output/comparetatyana-aliC225_5.jpg: 1.6514410914240734
output/comparetatyana-aliC225_6.jpg: 1.6287655223891018
output/comparetatyana-aliC225_7.jpg: 1.5866789314629046
output/comparetatyana-aliC225_8.jpg: 1.5829025556505272
output/comparetatyana-aliC225_9.jpg: 1.5414320200108707
output/comparetatyana-aliC225_10.jpg: 1.6089006272258033
output/comparetatyana-aliC225_11.jpg: 1.6363111667196315
output/comparetatyana-aliC225_12.jpg: 1.6015117300138229
output/comparetatyana-aliC225_13.jpg: 1.6254306720964915
output/comparetatyana-aliC225_14.jpg: 1.5768208645162058
output/comparetatyana-aliC225_15.jpg: 1.560480494274461
output/comparetatyana-aliC225_16.jpg: 1.5881226620506081
output/comparetatyana-aliC225_17.jpg: 1.5930627777977047
output/comparetatyana-aliC225_18.jpg: 1.589

output/comparetatyana-aliC232_1.jpg: 1.6266507695047139
output/comparetatyana-aliC232_2.jpg: 1.628342504336837
output/comparetatyana-aliC232_3.jpg: 1.6117603546437138
output/comparetatyana-aliC232_4.jpg: 1.6121721663514554
output/comparetatyana-aliC232_5.jpg: 1.6616468672615794
output/comparetatyana-aliC232_6.jpg: 1.53233763527374
output/comparetatyana-aliC232_7.jpg: 1.6240655075175616
output/comparetatyana-aliC232_8.jpg: 1.5000827342007168
output/comparetatyana-aliC232_9.jpg: 1.5838692028560157
output/comparetatyana-aliC232_10.jpg: 1.6089367284880547
output/comparetatyana-aliC232_11.jpg: 1.6148913086954522
output/comparetatyana-aliC232_12.jpg: 1.6379140389206859
output/comparetatyana-aliC232_13.jpg: 1.6254093824159197
output/comparetatyana-aliC232_14.jpg: 1.6304292045547197
output/comparetatyana-aliC232_15.jpg: 1.5932393357918917
output/comparetatyana-aliC232_16.jpg: 1.613779140735466
output/comparetatyana-aliC232_17.jpg: 1.5829469427486993
output/comparetatyana-aliC232_18.jpg: 1.5852

output/comparetatyana-aliC239_1.jpg: 1.547344509611876
output/comparetatyana-aliC239_2.jpg: 1.6560726574139975
output/comparetatyana-aliC239_3.jpg: 1.607646592177678
output/comparetatyana-aliC239_4.jpg: 1.5764906337913502
output/comparetatyana-aliC239_5.jpg: 1.6189097269131565
output/comparetatyana-aliC239_6.jpg: 1.5764199410704618
output/comparetatyana-aliC239_7.jpg: 1.651542105456818
output/comparetatyana-aliC239_8.jpg: 1.6347968880602204
output/comparetatyana-aliC239_9.jpg: 1.6206099243492542
output/comparetatyana-aliC239_10.jpg: 1.6871766112377324
output/comparetatyana-aliC239_11.jpg: 1.5869767409107065
output/comparetatyana-aliC239_12.jpg: 1.5188733622550457
output/comparetatyana-aliC239_13.jpg: 1.5569017344369436
output/comparetatyana-aliC239_14.jpg: 1.6340032242843128
output/comparetatyana-aliC239_15.jpg: 1.6342833309631128
output/comparetatyana-aliC239_16.jpg: 1.587833195314758
output/comparetatyana-aliC239_17.jpg: 1.5833311822180107
output/comparetatyana-aliC239_18.jpg: 1.6027

output/comparetatyana-aliC246_1.jpg: 1.5893511803239573
output/comparetatyana-aliC246_2.jpg: 1.5789671782200312
output/comparetatyana-aliC246_3.jpg: 1.6131178349038606
output/comparetatyana-aliC246_4.jpg: 1.6125835614573711
output/comparetatyana-aliC246_5.jpg: 1.631866238148029
output/comparetatyana-aliC246_6.jpg: 1.597819511350151
output/comparetatyana-aliC246_7.jpg: 1.6128314652677074
output/comparetatyana-aliC246_8.jpg: 1.6180867058003205
output/comparetatyana-aliC246_9.jpg: 1.5861899345437966
output/comparetatyana-aliC246_10.jpg: 1.5777440372984122
output/comparetatyana-aliC246_11.jpg: 1.503342804906643
output/comparetatyana-aliC246_12.jpg: 1.619551903038194
output/comparetatyana-aliC246_13.jpg: 1.596300253674113
output/comparetatyana-aliC246_14.jpg: 1.5976382520936603
output/comparetatyana-aliC246_15.jpg: 1.5240696391640811
output/comparetatyana-aliC246_16.jpg: 1.6185130925489633
output/comparetatyana-aliC246_17.jpg: 1.6375776694237394
output/comparetatyana-aliC246_18.jpg: 1.54016

In [18]:
evolve('test-images/ken_watanabe.jpg', 'test-images/tatyana_ali.jpg', 'ken-watanabe','B')

Start: 1.4172949709118567
output/compareken-watanabeB0_1.jpg: 1.4426141821891934
output/compareken-watanabeB0_2.jpg: 1.4432989137241
output/compareken-watanabeB0_3.jpg: 1.4209507645063182
output/compareken-watanabeB0_4.jpg: 1.4147783548616775
output/compareken-watanabeB0_5.jpg: 1.4361547870061409
output/compareken-watanabeB0_6.jpg: 1.4159971694997113
output/compareken-watanabeB0_7.jpg: 1.4048145619991692
output/compareken-watanabeB0_8.jpg: 1.4228952377973711
output/compareken-watanabeB0_9.jpg: 1.4733385633863652
output/compareken-watanabeB0_10.jpg: 1.4437304813375222
output/compareken-watanabeB0_11.jpg: 1.4275165838874542
output/compareken-watanabeB0_12.jpg: 1.41978034362607
output/compareken-watanabeB0_13.jpg: 1.4192901751818274
output/compareken-watanabeB0_14.jpg: 1.3944184899136773
output/compareken-watanabeB0_15.jpg: 1.4336733045171073
output/compareken-watanabeB0_16.jpg: 1.4259718215355193
output/compareken-watanabeB0_17.jpg: 1.453639699188578
output/compareken-watanabeB0_18.jpg: 

output/compareken-watanabeB7_1.jpg: 1.4156663226300017
output/compareken-watanabeB7_2.jpg: 1.3924675500074013
output/compareken-watanabeB7_3.jpg: 1.384814203312021
output/compareken-watanabeB7_4.jpg: 1.411143746094986
output/compareken-watanabeB7_5.jpg: 1.41641320820664
output/compareken-watanabeB7_6.jpg: 1.429940261593372
output/compareken-watanabeB7_7.jpg: 1.3857811444233494
output/compareken-watanabeB7_8.jpg: 1.4110032704311202
output/compareken-watanabeB7_9.jpg: 1.4085678677329931
output/compareken-watanabeB7_10.jpg: 1.4387910825495798
output/compareken-watanabeB7_11.jpg: 1.4169945386359295
output/compareken-watanabeB7_12.jpg: 1.4017606673309808
output/compareken-watanabeB7_13.jpg: 1.3801947418319873
output/compareken-watanabeB7_14.jpg: 1.4009722408677825
output/compareken-watanabeB7_15.jpg: 1.4009364239007616
output/compareken-watanabeB7_16.jpg: 1.3893819391742617
output/compareken-watanabeB7_17.jpg: 1.3853480660795547
output/compareken-watanabeB7_18.jpg: 1.4043750757464777
output

output/compareken-watanabeB14_1.jpg: 1.4069555662106552
output/compareken-watanabeB14_2.jpg: 1.3869796503738212
output/compareken-watanabeB14_3.jpg: 1.419649996084749
output/compareken-watanabeB14_4.jpg: 1.4060914820794674
output/compareken-watanabeB14_5.jpg: 1.3988946289083535
output/compareken-watanabeB14_6.jpg: 1.404222420661806
output/compareken-watanabeB14_7.jpg: 1.405845048952966
output/compareken-watanabeB14_8.jpg: 1.4415004045265292
output/compareken-watanabeB14_9.jpg: 1.4025662100456098
output/compareken-watanabeB14_10.jpg: 1.3867551646125065
output/compareken-watanabeB14_11.jpg: 1.4162340987385966
output/compareken-watanabeB14_12.jpg: 1.401137618438253
output/compareken-watanabeB14_13.jpg: 1.3763726929862472
output/compareken-watanabeB14_14.jpg: 1.3840543775536467
output/compareken-watanabeB14_15.jpg: 1.3971478004602833
output/compareken-watanabeB14_16.jpg: 1.4362847688117242
output/compareken-watanabeB14_17.jpg: 1.3984610855547395
output/compareken-watanabeB14_18.jpg: 1.3774

output/compareken-watanabeB20_20.jpg: 1.3960568197982877
Fittest: output/compareken-watanabeB17_15.jpg 1.3540403361364093
output/compareken-watanabeB21_1.jpg: 1.3978822017001096
output/compareken-watanabeB21_2.jpg: 1.468527249055167
output/compareken-watanabeB21_3.jpg: 1.3761630546579986
output/compareken-watanabeB21_4.jpg: 1.3928828930566377
output/compareken-watanabeB21_5.jpg: 1.3946107880101286
output/compareken-watanabeB21_6.jpg: 1.3961783399754544
output/compareken-watanabeB21_7.jpg: 1.3657230737722732
output/compareken-watanabeB21_8.jpg: 1.4442024436548937
output/compareken-watanabeB21_9.jpg: 1.4222756070139018
output/compareken-watanabeB21_10.jpg: 1.3702267229325236
output/compareken-watanabeB21_11.jpg: 1.4269457165466153
output/compareken-watanabeB21_12.jpg: 1.385157402619786
output/compareken-watanabeB21_13.jpg: 1.4062092772122585
output/compareken-watanabeB21_14.jpg: 1.4067884478845682
output/compareken-watanabeB21_15.jpg: 1.393006936911704
output/compareken-watanabeB21_16.jp

output/compareken-watanabeB27_18.jpg: 1.5235658309263218
output/compareken-watanabeB27_19.jpg: 1.3915198213411122
output/compareken-watanabeB27_20.jpg: 1.3574618108100553
Fittest: output/compareken-watanabeB17_15.jpg 1.3540403361364093
output/compareken-watanabeB28_1.jpg: 1.419999199991809
output/compareken-watanabeB28_2.jpg: 1.405108385824448
output/compareken-watanabeB28_3.jpg: 1.3903777216425657
output/compareken-watanabeB28_4.jpg: 1.3775253796499913
output/compareken-watanabeB28_5.jpg: 1.4463342555980574
output/compareken-watanabeB28_6.jpg: 1.405030926364876
output/compareken-watanabeB28_7.jpg: 1.4106520753364333
output/compareken-watanabeB28_8.jpg: 1.3922822645116897
output/compareken-watanabeB28_9.jpg: 1.3855684865036302
output/compareken-watanabeB28_10.jpg: 1.4170107176665387
output/compareken-watanabeB28_11.jpg: 1.3828025127106844
output/compareken-watanabeB28_12.jpg: 1.4224664512625451
output/compareken-watanabeB28_13.jpg: 1.3858281824269294
output/compareken-watanabeB28_14.jp

...

output/compareken-watanabeB219_7.jpg: 1.4223720343169375
output/compareken-watanabeB219_8.jpg: 1.3816532629394753
output/compareken-watanabeB219_9.jpg: 1.3719908926250468
output/compareken-watanabeB219_10.jpg: 1.3838606747510975
output/compareken-watanabeB219_11.jpg: 1.3781205159050605
output/compareken-watanabeB219_12.jpg: 1.3824431287591619
output/compareken-watanabeB219_13.jpg: 1.3833870203088485
output/compareken-watanabeB219_14.jpg: 1.3724448462753902
output/compareken-watanabeB219_15.jpg: 1.3733558715054839
output/compareken-watanabeB219_16.jpg: 1.3751041409793445
output/compareken-watanabeB219_17.jpg: 1.4230330162609452
output/compareken-watanabeB219_18.jpg: 1.3818488869487964
output/compareken-watanabeB219_19.jpg: 1.3847360811574265
output/compareken-watanabeB219_20.jpg: 1.4169520410107568
Fittest: output/compareken-watanabeB193_19.jpg 1.3338967103288135
output/compareken-watanabeB220_1.jpg: 1.3740134594824345
output/compareken-watanabeB220_2.jpg: 1.382391734314884
output/compa

output/compareken-watanabeB226_2.jpg: 1.37197531477369
output/compareken-watanabeB226_3.jpg: 1.3822693828696213
output/compareken-watanabeB226_4.jpg: 1.3894641280496343
output/compareken-watanabeB226_5.jpg: 1.3865160089504227
output/compareken-watanabeB226_6.jpg: 1.3909914656481588
output/compareken-watanabeB226_7.jpg: 1.3689280534462458
output/compareken-watanabeB226_8.jpg: 1.4019151228158144
output/compareken-watanabeB226_9.jpg: 1.3531702033054624
output/compareken-watanabeB226_10.jpg: 1.3808675659165328
output/compareken-watanabeB226_11.jpg: 1.4064441617357981
output/compareken-watanabeB226_12.jpg: 1.3806273537662792
output/compareken-watanabeB226_13.jpg: 1.3732908321749144
output/compareken-watanabeB226_14.jpg: 1.4030419475056426
output/compareken-watanabeB226_15.jpg: 1.4029073548971014
output/compareken-watanabeB226_16.jpg: 1.371624582546397
output/compareken-watanabeB226_17.jpg: 1.389280299990555
output/compareken-watanabeB226_18.jpg: 1.40207762343305
output/compareken-watanabeB2

output/compareken-watanabeB232_19.jpg: 1.3606976204637733
output/compareken-watanabeB232_20.jpg: 1.3982467079806216
Fittest: output/compareken-watanabeB193_19.jpg 1.3338967103288135
output/compareken-watanabeB233_1.jpg: 1.394964541136936
output/compareken-watanabeB233_2.jpg: 1.380959032936315
output/compareken-watanabeB233_3.jpg: 1.3627055565047883
output/compareken-watanabeB233_4.jpg: 1.3706236316802536
output/compareken-watanabeB233_5.jpg: 1.375490296057945
output/compareken-watanabeB233_6.jpg: 1.3715948516443306
output/compareken-watanabeB233_7.jpg: 1.3990151108411182
output/compareken-watanabeB233_8.jpg: 1.360822477141039
output/compareken-watanabeB233_9.jpg: 1.389882328844354
output/compareken-watanabeB233_10.jpg: 1.373015668529321
output/compareken-watanabeB233_11.jpg: 1.3832158390757359
output/compareken-watanabeB233_12.jpg: 1.3913166438247409
output/compareken-watanabeB233_13.jpg: 1.372249916127509
output/compareken-watanabeB233_14.jpg: 1.3755986548298664
output/compareken-wata

output/compareken-watanabeB239_15.jpg: 1.4220378288313271
output/compareken-watanabeB239_16.jpg: 1.387988181397886
output/compareken-watanabeB239_17.jpg: 1.3940346783329658
output/compareken-watanabeB239_18.jpg: 1.379759831077112
output/compareken-watanabeB239_19.jpg: 1.3676046617964275
output/compareken-watanabeB239_20.jpg: 1.3732142555722198
Fittest: output/compareken-watanabeB193_19.jpg 1.3338967103288135
output/compareken-watanabeB240_1.jpg: 1.371849284339786
output/compareken-watanabeB240_2.jpg: 1.3770594848156141
output/compareken-watanabeB240_3.jpg: 1.4399758097754474
output/compareken-watanabeB240_4.jpg: 1.4081447991341496
output/compareken-watanabeB240_5.jpg: 1.3863402325216256
output/compareken-watanabeB240_6.jpg: 1.4399980127340268
output/compareken-watanabeB240_7.jpg: 1.3749548983188469
output/compareken-watanabeB240_8.jpg: 1.3886600881527025
output/compareken-watanabeB240_9.jpg: 1.3859666175147782
output/compareken-watanabeB240_10.jpg: 1.360493598314462
output/compareken-w

output/compareken-watanabeB246_10.jpg: 1.3719962471810652
output/compareken-watanabeB246_11.jpg: 1.389200187143673
output/compareken-watanabeB246_12.jpg: 1.3869993518747326
output/compareken-watanabeB246_13.jpg: 1.387641199264513
output/compareken-watanabeB246_14.jpg: 1.3834688888438522
output/compareken-watanabeB246_15.jpg: 1.3968288573274301
output/compareken-watanabeB246_16.jpg: 1.3845702780040454
output/compareken-watanabeB246_17.jpg: 1.383983347742605
output/compareken-watanabeB246_18.jpg: 1.4257241020671918
output/compareken-watanabeB246_19.jpg: 1.3731746350565945
output/compareken-watanabeB246_20.jpg: 1.373291271706097
Fittest: output/compareken-watanabeB193_19.jpg 1.3338967103288135
output/compareken-watanabeB247_1.jpg: 1.368117327487888
output/compareken-watanabeB247_2.jpg: 1.3810343004513816
output/compareken-watanabeB247_3.jpg: 1.3726085183520753
output/compareken-watanabeB247_4.jpg: 1.3911849857909178
output/compareken-watanabeB247_5.jpg: 1.35916589207759
output/compareken-

The genetic algorithm failed to improve the distances for Keira Knightley and Natalie Portman, and for Tatyana M Ali targeting Ken Watanabe. Interestingly, any modifications to Samuel L Jackson cause his face to no longer be detected even with repeated tries of running the code. But for the other test subject pairings we can use their fittest images as test images. 

To simplify reproducability, we'll rename the fittest images to a standard format and move them to the test-images folder. Since the noise is randomly generated, you likely will have different fittest images so replace those file names with the ones from your results.

In [55]:
# Keira Knightley --> Kristin Chenoweth
os.rename('output/comparekeira-knightleyR110_7.jpg','test-images/keira_knightly_KC_GA.jpg')
# Kristin Chenoweth --> Keira Knightley 
os.rename('output/comparekristin-chenowethA195_6.jpg','test-images/kristin_chenoweth_KK_GA.jpg')
# Matthew Perry --> Colin Firth
os.rename('output/comparematthew-perryA178_16.jpg','test-images/matthew_perry_CF_GA.jpg')
# Colin Firth --> Matthew Perry
os.rename('output/comparecolin-firthA169_18.jpg','test-images/colin_firth_MP_GA.jpg')
# Kristin Chenoweth --> Colin Firth
os.rename('output/comparekristin-chenowethB169_4.jpg','test-images/kristin_chenoweth_CF_GA.jpg')
# Colin Firth --> Kristin Chenoweth
os.rename('output/comparecolin-firthR8_20.jpg','test-images/colin_firth_KC_GA.jpg')
# Tatyana M Ali --> Samuel L Jackson
os.rename('output/comparetatyana-aliA116_6.jpg', 'test-images/tatyana_ali_SJ_GA.jpg')
# Colin Firth --> George Lopez
os.rename('output/comparecolin-firthC86_4.jpg','test-images/colin_firth_GL_GA.jpg')
# George Lopez --> Colin Firth
os.rename('output/comparegeorge-lopezA248_11.jpg','test-images/george_lopez_CF_GA.jpg')
# Ken Watanabe --> Samuel L Jackson
os.rename('output/compareken-watanabeA185_13.jpg','test-images/ken_watanabe_SJ_GA.jpg')
# Tatyana M Ali --> Kristin Chenoweth
os.rename('output/comparetatyana-aliB44_4.jpg','test-images/tatyana_ali_KC_GA.jpg')
# Kristin Chenoweth --> Tatyana M Ali
os.rename('output/comparekristin-chenowethY150_10.jpg','test-images/kristin_chenoweth_TA_GA.jpg')
# Kristin Chenoweth --> George Lopez
os.rename('output/comparekristin-chenowethD30_13.jpg','test-images/kristin_chenoweth_GL_GA.jpg')
# George Lopez --> Kristin Chenoweth
os.rename('output/comparegeorge-lopezB177_14.jpg','test-images/george_lopez_KC_GA.jpg')
# Ken Watanabe --> Tatyana M Ali
os.rename('output/compareken-watanabeB193_19.jpg','test-images/ken_watanabe_TA_GA.jpg')

### Brute Force Targeting
Now that most of the the images have been optimized for targeting their intended labels, we can achieve those labels through brute force. The method for brute forcing the adversarial modifications of the image is similar to method used in the genetic algorithm for generating children in each generation. The main difference is that this code does not use a maximum change restriction. The code first checks if the genetic algorithm already successfully changed the source image to be identified as the target. If it did not, the brute force method has 300 tries to reach the target image or modify the image so much that a face can no longer be detected.

In [56]:
# Consulted https://medium.com/@ageitgey/machine-learning-is-fun-part-8-how-to-intentionally-trick-neural-networks-b55da32b7196

def adversarial(model, filename, source, target, suffix):
    result = infer(model, filename)
    if result == target: 
        print("Success! " + target + " achieved through genetic algorithm")
    else:
        count = 0

        original = Image.open(filename)
        original.load()
        original = np.asarray(original)

        while (result !=target and count < 300):
            img = Image.open(filename)
            img.load()
            img_a = np.asarray(img)
            l, w, d = img_a.shape
            mult = np.random.randint(3, size=(l, w, d), dtype=np.uint8)
            r = random.randint(0,1)
            if r == 0:
                img_a = img_a + mult
            else:
                img_a = img_a - mult
            img_a = np.clip(img_a, 0, 255)
            img = Image.fromarray(img_a, 'RGB')
            filename = 'output/' + source + suffix + str(count) + '.jpg'
            count += 1
            img.save(filename)
            result = infer(model, filename)
            print(result)

### Test Case B1: People with Similar Faces
For this test case I am using Natalie Portman and Keira Knightley, two actresses who are commonly mistaken for each other. I am running four tests within this: an image of Keira Knightley with a target of Natalie Portman first using the limited data set then the full FaceScrub model, and then switching.

In [19]:
adversarial('generated-embeddings/limited/classifier.pkl', 'test-images/keira_knightley2.jpg', 'keira-knightley','natalie-portman', 'F')


=== test-images/keira_knightley2.jpg ===

=== output/keira_knightleyF0.jpg ===
keira-knightley

=== output/keira_knightleyF1.jpg ===
keira-knightley

=== output/keira_knightleyF2.jpg ===
keira-knightley

=== output/keira_knightleyF3.jpg ===
keira-knightley

=== output/keira_knightleyF4.jpg ===
keira-knightley

=== output/keira_knightleyF5.jpg ===
keira-knightley

=== output/keira_knightleyF6.jpg ===
keira-knightley

=== output/keira_knightleyF7.jpg ===
natalie-portman


In [20]:
os.rename('output/keira_knightleyF7.jpg','output/B1_7f_keira_knightley.jpg')

In [24]:
adversarial('generated-embeddings/fullfacescrub/classifier.pkl', 'test-images/keira_knightley2.jpg', 'keira-knightley','natalie-portman', 'H')


=== test-images/keira_knightley2.jpg ===

=== output/keira_knightleyH0.jpg ===
keira-knightley

=== output/keira_knightleyH1.jpg ===
keira-knightley

=== output/keira_knightleyH2.jpg ===
courteney-cox

=== output/keira_knightleyH3.jpg ===
sherilyn-fenn

=== output/keira_knightleyH4.jpg ===
sherilyn-fenn

=== output/keira_knightleyH5.jpg ===
sherilyn-fenn

=== output/keira_knightleyH6.jpg ===
sherilyn-fenn

=== output/keira_knightleyH7.jpg ===
sherilyn-fenn

=== output/keira_knightleyH8.jpg ===
sherilyn-fenn

=== output/keira_knightleyH9.jpg ===
sherilyn-fenn

=== output/keira_knightleyH10.jpg ===
sherilyn-fenn

=== output/keira_knightleyH11.jpg ===
sherilyn-fenn

=== output/keira_knightleyH12.jpg ===
sherilyn-fenn

=== output/keira_knightleyH13.jpg ===
sherilyn-fenn

=== output/keira_knightleyH14.jpg ===
sherilyn-fenn

=== output/keira_knightleyH15.jpg ===
sherilyn-fenn

=== output/keira_knightleyH16.jpg ===
sherilyn-fenn

=== output/keira_knightleyH17.jpg ===
sherilyn-fenn

=== outpu

joan-collins

=== output/keira_knightleyH155.jpg ===
sherilyn-fenn

=== output/keira_knightleyH156.jpg ===
sherilyn-fenn

=== output/keira_knightleyH157.jpg ===
sherilyn-fenn

=== output/keira_knightleyH158.jpg ===
sherilyn-fenn

=== output/keira_knightleyH159.jpg ===
sherilyn-fenn

=== output/keira_knightleyH160.jpg ===
sherilyn-fenn

=== output/keira_knightleyH161.jpg ===
sherilyn-fenn

=== output/keira_knightleyH162.jpg ===
sherilyn-fenn

=== output/keira_knightleyH163.jpg ===
sherilyn-fenn

=== output/keira_knightleyH164.jpg ===
sherilyn-fenn

=== output/keira_knightleyH165.jpg ===
sherilyn-fenn

=== output/keira_knightleyH166.jpg ===
tina-louise

=== output/keira_knightleyH167.jpg ===
sherilyn-fenn

=== output/keira_knightleyH168.jpg ===
joan-collins

=== output/keira_knightleyH169.jpg ===
sherilyn-fenn

=== output/keira_knightleyH170.jpg ===
sherilyn-fenn

=== output/keira_knightleyH171.jpg ===
sherilyn-fenn

=== output/keira_knightleyH172.jpg ===
sherilyn-fenn

=== output/keira_

Exception: Unable to find a face: output/keira_knightleyH290.jpg

In [87]:
adversarial('generated-embeddings/limited/classifier.pkl', 'test-images/natalie_portman2.jpg', 'natalie-portman', 'keira-knightley','E')


=== test-images/natalie_portman2.jpg ===

=== output/natalie-portmanE0.jpg ===
natalie-portman

=== output/natalie-portmanE1.jpg ===
natalie-portman

=== output/natalie-portmanE2.jpg ===
natalie-portman

=== output/natalie-portmanE3.jpg ===
natalie-portman

=== output/natalie-portmanE4.jpg ===
natalie-portman

=== output/natalie-portmanE5.jpg ===
natalie-portman

=== output/natalie-portmanE6.jpg ===
natalie-portman

=== output/natalie-portmanE7.jpg ===
natalie-portman

=== output/natalie-portmanE8.jpg ===
kristin-chenoweth

=== output/natalie-portmanE9.jpg ===
kristin-chenoweth

=== output/natalie-portmanE10.jpg ===
keira-knightley


In [88]:
os.rename('output/natalie-portmanE10.jpg','output/B1_1bE_natalie_portman.jpg')

In [89]:
adversarial('generated-embeddings/fullfacescrub/classifier.pkl', 'test-images/natalie_portman2.jpg', 'natalie-portman', 'keira-knightley','E')


=== test-images/natalie_portman2.jpg ===

=== output/natalie-portmanE0.jpg ===
natalie-portman

=== output/natalie-portmanE1.jpg ===
natalie-portman

=== output/natalie-portmanE2.jpg ===
chase-masterson

=== output/natalie-portmanE3.jpg ===
neve-campbell

=== output/natalie-portmanE4.jpg ===
chase-masterson

=== output/natalie-portmanE5.jpg ===
olivia-dabo

=== output/natalie-portmanE6.jpg ===
olivia-dabo

=== output/natalie-portmanE7.jpg ===
kim-cattrall

=== output/natalie-portmanE8.jpg ===
chase-masterson

=== output/natalie-portmanE9.jpg ===
dominic-monaghan

=== output/natalie-portmanE10.jpg ===
olivia-dabo

=== output/natalie-portmanE11.jpg ===
olivia-dabo

=== output/natalie-portmanE12.jpg ===
eliza-coupe

=== output/natalie-portmanE13.jpg ===
olivia-dabo

=== output/natalie-portmanE14.jpg ===
kim-cattrall

=== output/natalie-portmanE15.jpg ===
olivia-dabo

=== output/natalie-portmanE16.jpg ===
sharon-gless

=== output/natalie-portmanE17.jpg ===
susan-dey

=== output/natalie-po

Exception: Unable to find a face: output/natalie-portmanE19.jpg

Both targetings succeeded with the limited model where there are fewer labels available, but neither succeeded against the full FaceScrub data set.
### Test Case B2: People with dissimilar faces
#### Pair 1: Keira Knightley and Kristin Chenoweth

In [90]:
adversarial('generated-embeddings/limited/classifier.pkl', 'test-images/keira_knightly_KC_GA.jpg', 'keira-knightley', 'kristin-chenoweth','D')


=== test-images/keira_knightly_KC_GA.jpg ===

=== output/keira-knightleyD0.jpg ===
keira-knightley

=== output/keira-knightleyD1.jpg ===
keira-knightley

=== output/keira-knightleyD2.jpg ===
keira-knightley

=== output/keira-knightleyD3.jpg ===
keira-knightley

=== output/keira-knightleyD4.jpg ===
keira-knightley

=== output/keira-knightleyD5.jpg ===
keira-knightley

=== output/keira-knightleyD6.jpg ===
keira-knightley

=== output/keira-knightleyD7.jpg ===
keira-knightley

=== output/keira-knightleyD8.jpg ===
keira-knightley

=== output/keira-knightleyD9.jpg ===
keira-knightley

=== output/keira-knightleyD10.jpg ===
keira-knightley

=== output/keira-knightleyD11.jpg ===
keira-knightley

=== output/keira-knightleyD12.jpg ===
keira-knightley

=== output/keira-knightleyD13.jpg ===
keira-knightley

=== output/keira-knightleyD14.jpg ===
keira-knightley

=== output/keira-knightleyD15.jpg ===
keira-knightley

=== output/keira-knightleyD16.jpg ===
keira-knightley

=== output/keira-knightleyD1

In [57]:
os.rename('output/keira-knightleyD66.jpg','output/B2_1a_keira_knightley_KC.jpg')

In [96]:
adversarial('generated-embeddings/fullfacescrub/classifier.pkl', 'test-images/keira_knightly_KC_GA.jpg', 'keira-knightley', 'kristin-chenoweth','E')


=== test-images/keira_knightly_KC_GA.jpg ===

=== output/keira-knightleyE0.jpg ===
courteney-cox

=== output/keira-knightleyE1.jpg ===
sherilyn-fenn

=== output/keira-knightleyE2.jpg ===
sherilyn-fenn

=== output/keira-knightleyE3.jpg ===
sherilyn-fenn

=== output/keira-knightleyE4.jpg ===
sherilyn-fenn

=== output/keira-knightleyE5.jpg ===
sherilyn-fenn

=== output/keira-knightleyE6.jpg ===
sherilyn-fenn

=== output/keira-knightleyE7.jpg ===
sherilyn-fenn

=== output/keira-knightleyE8.jpg ===
sherilyn-fenn

=== output/keira-knightleyE9.jpg ===
sherilyn-fenn

=== output/keira-knightleyE10.jpg ===
sherilyn-fenn

=== output/keira-knightleyE11.jpg ===
sherilyn-fenn

=== output/keira-knightleyE12.jpg ===
sherilyn-fenn

=== output/keira-knightleyE13.jpg ===
sherilyn-fenn

=== output/keira-knightleyE14.jpg ===
sherilyn-fenn

=== output/keira-knightleyE15.jpg ===
sherilyn-fenn

=== output/keira-knightleyE16.jpg ===
sherilyn-fenn

=== output/keira-knightleyE17.jpg ===
sherilyn-fenn

=== outpu


=== output/keira-knightleyE153.jpg ===
sherilyn-fenn

=== output/keira-knightleyE154.jpg ===
sherilyn-fenn

=== output/keira-knightleyE155.jpg ===
sherilyn-fenn

=== output/keira-knightleyE156.jpg ===
sherilyn-fenn

=== output/keira-knightleyE157.jpg ===
sherilyn-fenn

=== output/keira-knightleyE158.jpg ===
sherilyn-fenn

=== output/keira-knightleyE159.jpg ===
sherilyn-fenn

=== output/keira-knightleyE160.jpg ===
sherilyn-fenn

=== output/keira-knightleyE161.jpg ===
sherilyn-fenn

=== output/keira-knightleyE162.jpg ===
sherilyn-fenn

=== output/keira-knightleyE163.jpg ===
sherilyn-fenn

=== output/keira-knightleyE164.jpg ===
sherilyn-fenn

=== output/keira-knightleyE165.jpg ===
sherilyn-fenn

=== output/keira-knightleyE166.jpg ===
sherilyn-fenn

=== output/keira-knightleyE167.jpg ===
sherilyn-fenn

=== output/keira-knightleyE168.jpg ===
sherilyn-fenn

=== output/keira-knightleyE169.jpg ===
sherilyn-fenn

=== output/keira-knightleyE170.jpg ===
sherilyn-fenn

=== output/keira-knightleyE

In [91]:
adversarial('generated-embeddings/limited/classifier.pkl', 'test-images/kristin_chenoweth_KK_GA.jpg', 'kristin-chenoweth', 'keira-knightley', 'A')


=== test-images/kristin_chenoweth_KK_GA.jpg ===

=== output/kristin-chenowethA0.jpg ===
kristin-chenoweth

=== output/kristin-chenowethA1.jpg ===
kristin-chenoweth

=== output/kristin-chenowethA2.jpg ===
kristin-chenoweth

=== output/kristin-chenowethA3.jpg ===
kristin-chenoweth

=== output/kristin-chenowethA4.jpg ===
kristin-chenoweth

=== output/kristin-chenowethA5.jpg ===
kristin-chenoweth

=== output/kristin-chenowethA6.jpg ===
kristin-chenoweth

=== output/kristin-chenowethA7.jpg ===
kristin-chenoweth

=== output/kristin-chenowethA8.jpg ===
kristin-chenoweth

=== output/kristin-chenowethA9.jpg ===
kristin-chenoweth

=== output/kristin-chenowethA10.jpg ===
kristin-chenoweth

=== output/kristin-chenowethA11.jpg ===
kristin-chenoweth

=== output/kristin-chenowethA12.jpg ===
kristin-chenoweth

=== output/kristin-chenowethA13.jpg ===
kristin-chenoweth

=== output/kristin-chenowethA14.jpg ===
kristin-chenoweth

=== output/kristin-chenowethA15.jpg ===
kristin-chenoweth

=== output/krist

kristin-chenoweth

=== output/kristin-chenowethA138.jpg ===
kristin-chenoweth

=== output/kristin-chenowethA139.jpg ===
kristin-chenoweth

=== output/kristin-chenowethA140.jpg ===
kristin-chenoweth

=== output/kristin-chenowethA141.jpg ===
kristin-chenoweth

=== output/kristin-chenowethA142.jpg ===
kristin-chenoweth

=== output/kristin-chenowethA143.jpg ===
kristin-chenoweth

=== output/kristin-chenowethA144.jpg ===
kristin-chenoweth

=== output/kristin-chenowethA145.jpg ===
kristin-chenoweth

=== output/kristin-chenowethA146.jpg ===
kristin-chenoweth

=== output/kristin-chenowethA147.jpg ===
kristin-chenoweth

=== output/kristin-chenowethA148.jpg ===
kristin-chenoweth

=== output/kristin-chenowethA149.jpg ===
kristin-chenoweth

=== output/kristin-chenowethA150.jpg ===
kristin-chenoweth

=== output/kristin-chenowethA151.jpg ===
kristin-chenoweth

=== output/kristin-chenowethA152.jpg ===
kristin-chenoweth

=== output/kristin-chenowethA153.jpg ===
kristin-chenoweth

=== output/kristin-ch

kristin-chenoweth

=== output/kristin-chenowethA275.jpg ===
kristin-chenoweth

=== output/kristin-chenowethA276.jpg ===
kristin-chenoweth

=== output/kristin-chenowethA277.jpg ===
kristin-chenoweth

=== output/kristin-chenowethA278.jpg ===
kristin-chenoweth

=== output/kristin-chenowethA279.jpg ===
kristin-chenoweth

=== output/kristin-chenowethA280.jpg ===
kristin-chenoweth

=== output/kristin-chenowethA281.jpg ===
kristin-chenoweth

=== output/kristin-chenowethA282.jpg ===
kristin-chenoweth

=== output/kristin-chenowethA283.jpg ===
kristin-chenoweth

=== output/kristin-chenowethA284.jpg ===
kristin-chenoweth

=== output/kristin-chenowethA285.jpg ===
kristin-chenoweth

=== output/kristin-chenowethA286.jpg ===
kristin-chenoweth

=== output/kristin-chenowethA287.jpg ===
kristin-chenoweth

=== output/kristin-chenowethA288.jpg ===
kristin-chenoweth

=== output/kristin-chenowethA289.jpg ===
kristin-chenoweth

=== output/kristin-chenowethA290.jpg ===
kristin-chenoweth

=== output/kristin-ch

In [97]:
adversarial('generated-embeddings/fullfacescrub/classifier.pkl', 'test-images/kristin_chenoweth_KK_GA.jpg', 'kristin-chenoweth', 'keira-knightley', 'D')


=== test-images/kristin_chenoweth_KK_GA.jpg ===

=== output/kristin-chenowethD0.jpg ===
kristin-chenoweth

=== output/kristin-chenowethD1.jpg ===
kristin-chenoweth

=== output/kristin-chenowethD2.jpg ===
kristin-chenoweth

=== output/kristin-chenowethD3.jpg ===
kristin-chenoweth

=== output/kristin-chenowethD4.jpg ===
kristin-chenoweth

=== output/kristin-chenowethD5.jpg ===
kristin-chenoweth

=== output/kristin-chenowethD6.jpg ===
kristin-chenoweth

=== output/kristin-chenowethD7.jpg ===
kristin-chenoweth

=== output/kristin-chenowethD8.jpg ===
kristin-chenoweth

=== output/kristin-chenowethD9.jpg ===
kristin-chenoweth

=== output/kristin-chenowethD10.jpg ===
kristin-chenoweth

=== output/kristin-chenowethD11.jpg ===
kristin-chenoweth

=== output/kristin-chenowethD12.jpg ===
kristin-chenoweth

=== output/kristin-chenowethD13.jpg ===
kristin-chenoweth

=== output/kristin-chenowethD14.jpg ===
kristin-chenoweth

=== output/kristin-chenowethD15.jpg ===
kristin-chenoweth

=== output/krist

kristin-chenoweth

=== output/kristin-chenowethD138.jpg ===
kristin-chenoweth

=== output/kristin-chenowethD139.jpg ===
kristin-chenoweth

=== output/kristin-chenowethD140.jpg ===
kristin-chenoweth

=== output/kristin-chenowethD141.jpg ===
kristin-chenoweth

=== output/kristin-chenowethD142.jpg ===
kristin-chenoweth

=== output/kristin-chenowethD143.jpg ===
kristin-chenoweth

=== output/kristin-chenowethD144.jpg ===
kristin-chenoweth

=== output/kristin-chenowethD145.jpg ===
kristin-chenoweth

=== output/kristin-chenowethD146.jpg ===
kristin-chenoweth

=== output/kristin-chenowethD147.jpg ===
kristin-chenoweth

=== output/kristin-chenowethD148.jpg ===
kristin-chenoweth

=== output/kristin-chenowethD149.jpg ===
kristin-chenoweth

=== output/kristin-chenowethD150.jpg ===
kristin-chenoweth

=== output/kristin-chenowethD151.jpg ===
kristin-chenoweth

=== output/kristin-chenowethD152.jpg ===
kristin-chenoweth

=== output/kristin-chenowethD153.jpg ===
kristin-chenoweth

=== output/kristin-ch

kristin-chenoweth

=== output/kristin-chenowethD275.jpg ===
kristin-chenoweth

=== output/kristin-chenowethD276.jpg ===
kristin-chenoweth

=== output/kristin-chenowethD277.jpg ===
kristin-chenoweth

=== output/kristin-chenowethD278.jpg ===
kristin-chenoweth

=== output/kristin-chenowethD279.jpg ===
kristin-chenoweth

=== output/kristin-chenowethD280.jpg ===
kristin-chenoweth

=== output/kristin-chenowethD281.jpg ===
kristin-chenoweth

=== output/kristin-chenowethD282.jpg ===
kristin-chenoweth

=== output/kristin-chenowethD283.jpg ===
kristin-chenoweth

=== output/kristin-chenowethD284.jpg ===
kristin-chenoweth

=== output/kristin-chenowethD285.jpg ===
kristin-chenoweth

=== output/kristin-chenowethD286.jpg ===
kristin-chenoweth

=== output/kristin-chenowethD287.jpg ===
kristin-chenoweth

=== output/kristin-chenowethD288.jpg ===
kristin-chenoweth

=== output/kristin-chenowethD289.jpg ===
kristin-chenoweth

=== output/kristin-chenowethD290.jpg ===
kristin-chenoweth

=== output/kristin-ch

#### Pair 2: Matthew Perry and Colin Firth

In [92]:
adversarial('generated-embeddings/limited/classifier.pkl', 'test-images/matthew_perry_CF_GA.jpg', 'matthew-perry', 'colin-firth', 'A')


=== test-images/matthew_perry_CF_GA.jpg ===

=== output/matthew-perryA0.jpg ===
matthew-perry

=== output/matthew-perryA1.jpg ===
matthew-perry

=== output/matthew-perryA2.jpg ===
matthew-perry

=== output/matthew-perryA3.jpg ===
matthew-perry

=== output/matthew-perryA4.jpg ===
matthew-perry

=== output/matthew-perryA5.jpg ===
matthew-perry

=== output/matthew-perryA6.jpg ===
matthew-perry

=== output/matthew-perryA7.jpg ===
matthew-perry

=== output/matthew-perryA8.jpg ===
matthew-perry

=== output/matthew-perryA9.jpg ===
matthew-perry

=== output/matthew-perryA10.jpg ===
matthew-perry

=== output/matthew-perryA11.jpg ===
matthew-perry

=== output/matthew-perryA12.jpg ===
matthew-perry

=== output/matthew-perryA13.jpg ===
matthew-perry

=== output/matthew-perryA14.jpg ===
matthew-perry

=== output/matthew-perryA15.jpg ===
matthew-perry

=== output/matthew-perryA16.jpg ===
matthew-perry

=== output/matthew-perryA17.jpg ===
matthew-perry

=== output/matthew-perryA18.jpg ===
matthew-pe

matthew-perry

=== output/matthew-perryA160.jpg ===
matthew-perry

=== output/matthew-perryA161.jpg ===
matthew-perry

=== output/matthew-perryA162.jpg ===
matthew-perry

=== output/matthew-perryA163.jpg ===
matthew-perry

=== output/matthew-perryA164.jpg ===
matthew-perry

=== output/matthew-perryA165.jpg ===
matthew-perry

=== output/matthew-perryA166.jpg ===
matthew-perry

=== output/matthew-perryA167.jpg ===
matthew-perry

=== output/matthew-perryA168.jpg ===
matthew-perry

=== output/matthew-perryA169.jpg ===
matthew-perry

=== output/matthew-perryA170.jpg ===
matthew-perry

=== output/matthew-perryA171.jpg ===
matthew-perry

=== output/matthew-perryA172.jpg ===
matthew-perry

=== output/matthew-perryA173.jpg ===
matthew-perry

=== output/matthew-perryA174.jpg ===
matthew-perry

=== output/matthew-perryA175.jpg ===
matthew-perry

=== output/matthew-perryA176.jpg ===
matthew-perry

=== output/matthew-perryA177.jpg ===
matthew-perry

=== output/matthew-perryA178.jpg ===
matthew-perr

In [98]:
adversarial('generated-embeddings/fullfacescrub/classifier.pkl', 'test-images/matthew_perry_CF_GA.jpg', 'matthew-perry', 'colin-firth', 'B')


=== test-images/matthew_perry_CF_GA.jpg ===

=== output/matthew-perryB0.jpg ===
matthew-perry

=== output/matthew-perryB1.jpg ===
matthew-perry

=== output/matthew-perryB2.jpg ===
matthew-perry

=== output/matthew-perryB3.jpg ===
matthew-perry

=== output/matthew-perryB4.jpg ===
matthew-perry

=== output/matthew-perryB5.jpg ===
matthew-perry

=== output/matthew-perryB6.jpg ===
matthew-perry

=== output/matthew-perryB7.jpg ===
matthew-perry

=== output/matthew-perryB8.jpg ===
matthew-perry

=== output/matthew-perryB9.jpg ===
matthew-perry

=== output/matthew-perryB10.jpg ===
matthew-perry

=== output/matthew-perryB11.jpg ===
matthew-perry

=== output/matthew-perryB12.jpg ===
matthew-perry

=== output/matthew-perryB13.jpg ===
matthew-perry

=== output/matthew-perryB14.jpg ===
matthew-perry

=== output/matthew-perryB15.jpg ===
matthew-perry

=== output/matthew-perryB16.jpg ===
matthew-perry

=== output/matthew-perryB17.jpg ===
matthew-perry

=== output/matthew-perryB18.jpg ===
matthew-pe

Exception: Unable to find a face: output/matthew-perryB68.jpg

In [89]:
adversarial('generated-embeddings/limited/classifier.pkl', 'test-images/colin_firth_MP_GA.jpg', 'colin-firth', 'matthew-perry', 'A')


=== test-images/colin_firth_MP_GA.jpg ===

=== output/colin-firthA0.jpg ===
colin-firth

=== output/colin-firthA1.jpg ===
colin-firth

=== output/colin-firthA2.jpg ===
colin-firth

=== output/colin-firthA3.jpg ===
colin-firth

=== output/colin-firthA4.jpg ===
colin-firth

=== output/colin-firthA5.jpg ===
colin-firth

=== output/colin-firthA6.jpg ===
colin-firth

=== output/colin-firthA7.jpg ===
colin-firth

=== output/colin-firthA8.jpg ===
colin-firth

=== output/colin-firthA9.jpg ===
colin-firth

=== output/colin-firthA10.jpg ===
colin-firth

=== output/colin-firthA11.jpg ===
colin-firth

=== output/colin-firthA12.jpg ===
colin-firth

=== output/colin-firthA13.jpg ===
colin-firth

=== output/colin-firthA14.jpg ===
colin-firth

=== output/colin-firthA15.jpg ===
colin-firth

=== output/colin-firthA16.jpg ===
colin-firth

=== output/colin-firthA17.jpg ===
colin-firth

=== output/colin-firthA18.jpg ===
colin-firth

=== output/colin-firthA19.jpg ===
colin-firth

=== output/colin-firthA20.

colin-firth

=== output/colin-firthA173.jpg ===
colin-firth

=== output/colin-firthA174.jpg ===
colin-firth

=== output/colin-firthA175.jpg ===
colin-firth

=== output/colin-firthA176.jpg ===
colin-firth

=== output/colin-firthA177.jpg ===
colin-firth

=== output/colin-firthA178.jpg ===
colin-firth

=== output/colin-firthA179.jpg ===
colin-firth

=== output/colin-firthA180.jpg ===
colin-firth

=== output/colin-firthA181.jpg ===
colin-firth

=== output/colin-firthA182.jpg ===
colin-firth

=== output/colin-firthA183.jpg ===
colin-firth

=== output/colin-firthA184.jpg ===
colin-firth

=== output/colin-firthA185.jpg ===
colin-firth

=== output/colin-firthA186.jpg ===
colin-firth

=== output/colin-firthA187.jpg ===
colin-firth

=== output/colin-firthA188.jpg ===
colin-firth

=== output/colin-firthA189.jpg ===
colin-firth

=== output/colin-firthA190.jpg ===
colin-firth

=== output/colin-firthA191.jpg ===
colin-firth

=== output/colin-firthA192.jpg ===
colin-firth

=== output/colin-firthA193.

In [99]:
adversarial('generated-embeddings/fullfacescrub/classifier.pkl', 'test-images/colin_firth_MP_GA.jpg', 'colin-firth', 'matthew-perry', 'D')


=== test-images/colin_firth_MP_GA.jpg ===

=== output/colin-firthD0.jpg ===
colin-firth

=== output/colin-firthD1.jpg ===
colin-firth

=== output/colin-firthD2.jpg ===
colin-firth

=== output/colin-firthD3.jpg ===
colin-firth

=== output/colin-firthD4.jpg ===
colin-firth

=== output/colin-firthD5.jpg ===
colin-firth

=== output/colin-firthD6.jpg ===
colin-firth

=== output/colin-firthD7.jpg ===
colin-firth

=== output/colin-firthD8.jpg ===
colin-firth

=== output/colin-firthD9.jpg ===
colin-firth

=== output/colin-firthD10.jpg ===
colin-firth

=== output/colin-firthD11.jpg ===
colin-firth

=== output/colin-firthD12.jpg ===
colin-firth

=== output/colin-firthD13.jpg ===
colin-firth

=== output/colin-firthD14.jpg ===
colin-firth

=== output/colin-firthD15.jpg ===
colin-firth

=== output/colin-firthD16.jpg ===
colin-firth

=== output/colin-firthD17.jpg ===
colin-firth

=== output/colin-firthD18.jpg ===
colin-firth

=== output/colin-firthD19.jpg ===
colin-firth

=== output/colin-firthD20.

colin-firth

=== output/colin-firthD169.jpg ===
neal-mcdonough

=== output/colin-firthD170.jpg ===
colin-firth

=== output/colin-firthD171.jpg ===
neal-mcdonough

=== output/colin-firthD172.jpg ===
colin-firth

=== output/colin-firthD173.jpg ===
anthony-stewart-head

=== output/colin-firthD174.jpg ===
anthony-stewart-head

=== output/colin-firthD175.jpg ===
anthony-stewart-head

=== output/colin-firthD176.jpg ===
anthony-stewart-head

=== output/colin-firthD177.jpg ===
anthony-stewart-head

=== output/colin-firthD178.jpg ===
anthony-stewart-head

=== output/colin-firthD179.jpg ===
colin-firth

=== output/colin-firthD180.jpg ===
colin-firth

=== output/colin-firthD181.jpg ===
colin-firth

=== output/colin-firthD182.jpg ===
colin-firth

=== output/colin-firthD183.jpg ===
anthony-stewart-head

=== output/colin-firthD184.jpg ===
alan-alda

=== output/colin-firthD185.jpg ===
robert-redford

=== output/colin-firthD186.jpg ===
robert-redford

=== output/colin-firthD187.jpg ===
robert-redford


### Test Case B3: People of Different Genders
#### Pair 1: Kristin Chenoweth and Colin Firth

In [94]:
adversarial('generated-embeddings/limited/classifier.pkl', 'test-images/kristin_chenoweth_CF_GA.jpg', 'kristin-chenoweth','colin-firth', 'C')


=== test-images/kristin_chenoweth_CF_GA.jpg ===

=== output/kristin-chenowethC0.jpg ===
kristin-chenoweth

=== output/kristin-chenowethC1.jpg ===
kristin-chenoweth

=== output/kristin-chenowethC2.jpg ===
kristin-chenoweth

=== output/kristin-chenowethC3.jpg ===
kristin-chenoweth

=== output/kristin-chenowethC4.jpg ===
kristin-chenoweth

=== output/kristin-chenowethC5.jpg ===
kristin-chenoweth

=== output/kristin-chenowethC6.jpg ===
kristin-chenoweth

=== output/kristin-chenowethC7.jpg ===
kristin-chenoweth

=== output/kristin-chenowethC8.jpg ===
kristin-chenoweth

=== output/kristin-chenowethC9.jpg ===
kristin-chenoweth

=== output/kristin-chenowethC10.jpg ===
kristin-chenoweth

=== output/kristin-chenowethC11.jpg ===
kristin-chenoweth

=== output/kristin-chenowethC12.jpg ===
kristin-chenoweth

=== output/kristin-chenowethC13.jpg ===
kristin-chenoweth

=== output/kristin-chenowethC14.jpg ===
kristin-chenoweth

=== output/kristin-chenowethC15.jpg ===
kristin-chenoweth

=== output/krist

kristin-chenoweth

=== output/kristin-chenowethC138.jpg ===
kristin-chenoweth

=== output/kristin-chenowethC139.jpg ===
kristin-chenoweth

=== output/kristin-chenowethC140.jpg ===
kristin-chenoweth

=== output/kristin-chenowethC141.jpg ===
kristin-chenoweth

=== output/kristin-chenowethC142.jpg ===
kristin-chenoweth

=== output/kristin-chenowethC143.jpg ===
kristin-chenoweth

=== output/kristin-chenowethC144.jpg ===
kristin-chenoweth

=== output/kristin-chenowethC145.jpg ===
kristin-chenoweth

=== output/kristin-chenowethC146.jpg ===
kristin-chenoweth

=== output/kristin-chenowethC147.jpg ===
kristin-chenoweth

=== output/kristin-chenowethC148.jpg ===
kristin-chenoweth

=== output/kristin-chenowethC149.jpg ===
kristin-chenoweth

=== output/kristin-chenowethC150.jpg ===
kristin-chenoweth

=== output/kristin-chenowethC151.jpg ===
kristin-chenoweth

=== output/kristin-chenowethC152.jpg ===
kristin-chenoweth

=== output/kristin-chenowethC153.jpg ===
kristin-chenoweth

=== output/kristin-ch

kristin-chenoweth

=== output/kristin-chenowethC275.jpg ===
kristin-chenoweth

=== output/kristin-chenowethC276.jpg ===
kristin-chenoweth

=== output/kristin-chenowethC277.jpg ===
kristin-chenoweth

=== output/kristin-chenowethC278.jpg ===
kristin-chenoweth

=== output/kristin-chenowethC279.jpg ===
kristin-chenoweth

=== output/kristin-chenowethC280.jpg ===
kristin-chenoweth

=== output/kristin-chenowethC281.jpg ===
kristin-chenoweth

=== output/kristin-chenowethC282.jpg ===
kristin-chenoweth

=== output/kristin-chenowethC283.jpg ===
kristin-chenoweth

=== output/kristin-chenowethC284.jpg ===
kristin-chenoweth

=== output/kristin-chenowethC285.jpg ===
kristin-chenoweth

=== output/kristin-chenowethC286.jpg ===
kristin-chenoweth

=== output/kristin-chenowethC287.jpg ===
kristin-chenoweth

=== output/kristin-chenowethC288.jpg ===
kristin-chenoweth

=== output/kristin-chenowethC289.jpg ===
kristin-chenoweth

=== output/kristin-chenowethC290.jpg ===
kristin-chenoweth

=== output/kristin-ch

In [95]:
adversarial('generated-embeddings/limited/classifier.pkl', 'test-images/colin_firth_KC_GA.jpg', 'colin-firth', 'kristin-chenoweth', 'C')


=== test-images/colin_firth_KC_GA.jpg ===

=== output/colin-firthC0.jpg ===
colin-firth

=== output/colin-firthC1.jpg ===
colin-firth

=== output/colin-firthC2.jpg ===
colin-firth

=== output/colin-firthC3.jpg ===
colin-firth

=== output/colin-firthC4.jpg ===
colin-firth

=== output/colin-firthC5.jpg ===
colin-firth

=== output/colin-firthC6.jpg ===
colin-firth

=== output/colin-firthC7.jpg ===
colin-firth

=== output/colin-firthC8.jpg ===
colin-firth

=== output/colin-firthC9.jpg ===
colin-firth

=== output/colin-firthC10.jpg ===
colin-firth

=== output/colin-firthC11.jpg ===
colin-firth

=== output/colin-firthC12.jpg ===
colin-firth

=== output/colin-firthC13.jpg ===
colin-firth

=== output/colin-firthC14.jpg ===
colin-firth

=== output/colin-firthC15.jpg ===
colin-firth

=== output/colin-firthC16.jpg ===
colin-firth

=== output/colin-firthC17.jpg ===
colin-firth

=== output/colin-firthC18.jpg ===
colin-firth

=== output/colin-firthC19.jpg ===
colin-firth

=== output/colin-firthC20.

colin-firth

=== output/colin-firthC173.jpg ===
colin-firth

=== output/colin-firthC174.jpg ===
colin-firth

=== output/colin-firthC175.jpg ===
colin-firth

=== output/colin-firthC176.jpg ===
colin-firth

=== output/colin-firthC177.jpg ===
colin-firth

=== output/colin-firthC178.jpg ===
colin-firth

=== output/colin-firthC179.jpg ===
colin-firth

=== output/colin-firthC180.jpg ===
colin-firth

=== output/colin-firthC181.jpg ===
colin-firth

=== output/colin-firthC182.jpg ===
colin-firth

=== output/colin-firthC183.jpg ===
colin-firth

=== output/colin-firthC184.jpg ===
colin-firth

=== output/colin-firthC185.jpg ===
colin-firth

=== output/colin-firthC186.jpg ===
colin-firth

=== output/colin-firthC187.jpg ===
colin-firth

=== output/colin-firthC188.jpg ===
colin-firth

=== output/colin-firthC189.jpg ===
colin-firth

=== output/colin-firthC190.jpg ===
colin-firth

=== output/colin-firthC191.jpg ===
colin-firth

=== output/colin-firthC192.jpg ===
colin-firth

=== output/colin-firthC193.

Since neither of the test cases succeeded with the limited data set, I am not running the images against the full FaceScrub since they would be even less likely to succeed.

#### Pair 2: Tatyana M. Ali and Samuel L. Jackson

In [81]:
adversarial('generated-embeddings/limited/classifier.pkl', 'test-images/tatyana_ali_SJ_GA.jpg', 'tatyana-m.-ali', 'samuel-l.-jackson', 'C')


=== test-images/tatyana_ali_SJ_GA.jpg ===

=== output/tatyana-m.-aliC0.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliC1.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliC2.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliC3.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliC4.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliC5.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliC6.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliC7.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliC8.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliC9.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliC10.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliC11.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliC12.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliC13.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliC14.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliC15.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliC16.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliC17.jpg ===
tatyana-m.-ali

=== output/t

tatyana-m.-ali

=== output/tatyana-m.-aliC154.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliC155.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliC156.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliC157.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliC158.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliC159.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliC160.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliC161.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliC162.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliC163.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliC164.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliC165.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliC166.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliC167.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliC168.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliC169.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliC170.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliC171.jpg ===
tatyana-m.-ali

=== output/t

In [70]:
adversarial('generated-embeddings/limited/classifier.pkl', 'test-images/samuel_jackson.jpg', 'samuel-l.-jackson', 'tatyana-m.-ali', 'C')


=== test-images/samuel_jackson.jpg ===

=== output/samuel-l.-jacksonC0.jpg ===
samuel-l.-jackson

=== output/samuel-l.-jacksonC1.jpg ===


Exception: Unable to find a face: output/samuel-l.-jacksonC1.jpg

Here it took two iterations of random noise to make Samuel L. Jackson's face undetectable, but again it happened much sooner than with any of the other test subjects.
### Test Case B4: People of Different Races
#### Pair 1: Colin Firth and George Lopez

In [100]:
adversarial('generated-embeddings/limited/classifier.pkl', 'test-images/colin_firth_GL_GA.jpg', 'colin-firth', 'george-lopez', 'H')


=== test-images/colin_firth_GL_GA.jpg ===

=== output/colin-firthH0.jpg ===
colin-firth

=== output/colin-firthH1.jpg ===
colin-firth

=== output/colin-firthH2.jpg ===
colin-firth

=== output/colin-firthH3.jpg ===
colin-firth

=== output/colin-firthH4.jpg ===
colin-firth

=== output/colin-firthH5.jpg ===
colin-firth

=== output/colin-firthH6.jpg ===
colin-firth

=== output/colin-firthH7.jpg ===
colin-firth

=== output/colin-firthH8.jpg ===
colin-firth

=== output/colin-firthH9.jpg ===
colin-firth

=== output/colin-firthH10.jpg ===
colin-firth

=== output/colin-firthH11.jpg ===
colin-firth

=== output/colin-firthH12.jpg ===
colin-firth

=== output/colin-firthH13.jpg ===
colin-firth

=== output/colin-firthH14.jpg ===
colin-firth

=== output/colin-firthH15.jpg ===
colin-firth

=== output/colin-firthH16.jpg ===
colin-firth

=== output/colin-firthH17.jpg ===
colin-firth

=== output/colin-firthH18.jpg ===
colin-firth

=== output/colin-firthH19.jpg ===
colin-firth

=== output/colin-firthH20.

colin-firth

=== output/colin-firthH173.jpg ===
colin-firth

=== output/colin-firthH174.jpg ===
colin-firth

=== output/colin-firthH175.jpg ===
colin-firth

=== output/colin-firthH176.jpg ===
colin-firth

=== output/colin-firthH177.jpg ===
matthew-perry

=== output/colin-firthH178.jpg ===
colin-firth

=== output/colin-firthH179.jpg ===
colin-firth

=== output/colin-firthH180.jpg ===
colin-firth

=== output/colin-firthH181.jpg ===
colin-firth

=== output/colin-firthH182.jpg ===
colin-firth

=== output/colin-firthH183.jpg ===
matthew-perry

=== output/colin-firthH184.jpg ===
colin-firth

=== output/colin-firthH185.jpg ===
colin-firth

=== output/colin-firthH186.jpg ===
colin-firth

=== output/colin-firthH187.jpg ===
colin-firth

=== output/colin-firthH188.jpg ===
colin-firth

=== output/colin-firthH189.jpg ===
colin-firth

=== output/colin-firthH190.jpg ===
colin-firth

=== output/colin-firthH191.jpg ===
colin-firth

=== output/colin-firthH192.jpg ===
colin-firth

=== output/colin-firthH

In [87]:
adversarial('generated-embeddings/limited/classifier.pkl', 'test-images/george_lopez_CF_GA.jpg', 'george-lopez', 'colin-firth', 'A')


=== test-images/george_lopez_CF_GA.jpg ===

=== output/george-lopezA0.jpg ===
george-lopez

=== output/george-lopezA1.jpg ===
george-lopez

=== output/george-lopezA2.jpg ===
george-lopez

=== output/george-lopezA3.jpg ===
george-lopez

=== output/george-lopezA4.jpg ===
george-lopez

=== output/george-lopezA5.jpg ===
george-lopez

=== output/george-lopezA6.jpg ===
george-lopez

=== output/george-lopezA7.jpg ===
george-lopez

=== output/george-lopezA8.jpg ===
george-lopez

=== output/george-lopezA9.jpg ===
george-lopez

=== output/george-lopezA10.jpg ===
george-lopez

=== output/george-lopezA11.jpg ===
george-lopez

=== output/george-lopezA12.jpg ===
george-lopez

=== output/george-lopezA13.jpg ===
george-lopez

=== output/george-lopezA14.jpg ===
george-lopez

=== output/george-lopezA15.jpg ===
george-lopez

=== output/george-lopezA16.jpg ===
george-lopez

=== output/george-lopezA17.jpg ===
george-lopez

=== output/george-lopezA18.jpg ===
george-lopez

=== output/george-lopezA19.jpg ===

george-lopez

=== output/george-lopezA166.jpg ===
george-lopez

=== output/george-lopezA167.jpg ===
george-lopez

=== output/george-lopezA168.jpg ===
george-lopez

=== output/george-lopezA169.jpg ===
george-lopez

=== output/george-lopezA170.jpg ===
george-lopez

=== output/george-lopezA171.jpg ===
george-lopez

=== output/george-lopezA172.jpg ===
george-lopez

=== output/george-lopezA173.jpg ===
george-lopez

=== output/george-lopezA174.jpg ===
george-lopez

=== output/george-lopezA175.jpg ===
george-lopez

=== output/george-lopezA176.jpg ===
george-lopez

=== output/george-lopezA177.jpg ===
george-lopez

=== output/george-lopezA178.jpg ===
george-lopez

=== output/george-lopezA179.jpg ===
george-lopez

=== output/george-lopezA180.jpg ===
george-lopez

=== output/george-lopezA181.jpg ===
george-lopez

=== output/george-lopezA182.jpg ===
george-lopez

=== output/george-lopezA183.jpg ===
george-lopez

=== output/george-lopezA184.jpg ===
george-lopez

=== output/george-lopezA185.jpg ===


#### Pair 2: Samuel L. Jackson and Ken Watanabe

In [71]:
adversarial('generated-embeddings/limited/classifier.pkl', 'test-images/samuel_jackson.jpg', 'samuel-l.-jackson', 'ken-watanabe', 'F')


=== test-images/samuel_jackson.jpg ===

=== output/samuel-l.-jacksonF0.jpg ===
samuel-l.-jackson

=== output/samuel-l.-jacksonF1.jpg ===
samuel-l.-jackson

=== output/samuel-l.-jacksonF2.jpg ===


Exception: Unable to find a face: output/samuel-l.-jacksonF2.jpg

In [72]:
adversarial('generated-embeddings/limited/classifier.pkl', 'test-images/ken_watanabe_SJ_GA.jpg', 'ken-watanabe', 'samuel-l.-jackson', 'A')


=== test-images/ken_watanabe_SJ_GA.jpg ===

=== output/ken-watanabeA0.jpg ===
ken-watanabe

=== output/ken-watanabeA1.jpg ===
ken-watanabe

=== output/ken-watanabeA2.jpg ===
ken-watanabe

=== output/ken-watanabeA3.jpg ===
ken-watanabe

=== output/ken-watanabeA4.jpg ===
ken-watanabe

=== output/ken-watanabeA5.jpg ===
ken-watanabe

=== output/ken-watanabeA6.jpg ===
ken-watanabe

=== output/ken-watanabeA7.jpg ===
ken-watanabe

=== output/ken-watanabeA8.jpg ===
ken-watanabe

=== output/ken-watanabeA9.jpg ===
ken-watanabe

=== output/ken-watanabeA10.jpg ===
ken-watanabe

=== output/ken-watanabeA11.jpg ===
ken-watanabe

=== output/ken-watanabeA12.jpg ===
ken-watanabe

=== output/ken-watanabeA13.jpg ===
ken-watanabe

=== output/ken-watanabeA14.jpg ===
ken-watanabe

=== output/ken-watanabeA15.jpg ===
ken-watanabe

=== output/ken-watanabeA16.jpg ===
ken-watanabe

=== output/ken-watanabeA17.jpg ===
ken-watanabe

=== output/ken-watanabeA18.jpg ===
ken-watanabe

=== output/ken-watanabeA19.jpg ===

ken-watanabe

=== output/ken-watanabeA166.jpg ===
ken-watanabe

=== output/ken-watanabeA167.jpg ===
ken-watanabe

=== output/ken-watanabeA168.jpg ===
ken-watanabe

=== output/ken-watanabeA169.jpg ===
ken-watanabe

=== output/ken-watanabeA170.jpg ===
ken-watanabe

=== output/ken-watanabeA171.jpg ===
ken-watanabe

=== output/ken-watanabeA172.jpg ===
ken-watanabe

=== output/ken-watanabeA173.jpg ===
ken-watanabe

=== output/ken-watanabeA174.jpg ===
ken-watanabe

=== output/ken-watanabeA175.jpg ===
ken-watanabe

=== output/ken-watanabeA176.jpg ===
ken-watanabe

=== output/ken-watanabeA177.jpg ===
ken-watanabe

=== output/ken-watanabeA178.jpg ===
ken-watanabe

=== output/ken-watanabeA179.jpg ===
ken-watanabe

=== output/ken-watanabeA180.jpg ===
ken-watanabe

=== output/ken-watanabeA181.jpg ===
ken-watanabe

=== output/ken-watanabeA182.jpg ===
ken-watanabe

=== output/ken-watanabeA183.jpg ===
ken-watanabe

=== output/ken-watanabeA184.jpg ===
ken-watanabe

=== output/ken-watanabeA185.jpg ===


#### Pair 3: Kristin Chenoweth and Tatyana M. Ali

In [74]:
adversarial('generated-embeddings/limited/classifier.pkl', 'test-images/kristin_chenoweth_TA_GA.jpg', 'kristin-chenoweth', 'tatyana-m.-ali', 'K')


=== test-images/kristin_chenoweth_TA_GA.jpg ===

=== output/kristin-chenowethK0.jpg ===
kristin-chenoweth

=== output/kristin-chenowethK1.jpg ===
kristin-chenoweth

=== output/kristin-chenowethK2.jpg ===
kristin-chenoweth

=== output/kristin-chenowethK3.jpg ===
kristin-chenoweth

=== output/kristin-chenowethK4.jpg ===
kristin-chenoweth

=== output/kristin-chenowethK5.jpg ===
kristin-chenoweth

=== output/kristin-chenowethK6.jpg ===
kristin-chenoweth

=== output/kristin-chenowethK7.jpg ===
kristin-chenoweth

=== output/kristin-chenowethK8.jpg ===
kristin-chenoweth

=== output/kristin-chenowethK9.jpg ===
kristin-chenoweth

=== output/kristin-chenowethK10.jpg ===
kristin-chenoweth

=== output/kristin-chenowethK11.jpg ===
kristin-chenoweth

=== output/kristin-chenowethK12.jpg ===
kristin-chenoweth

=== output/kristin-chenowethK13.jpg ===
kristin-chenoweth

=== output/kristin-chenowethK14.jpg ===
kristin-chenoweth

=== output/kristin-chenowethK15.jpg ===
kristin-chenoweth

=== output/krist

kristin-chenoweth

=== output/kristin-chenowethK138.jpg ===
kristin-chenoweth

=== output/kristin-chenowethK139.jpg ===
kristin-chenoweth

=== output/kristin-chenowethK140.jpg ===
kristin-chenoweth

=== output/kristin-chenowethK141.jpg ===
kristin-chenoweth

=== output/kristin-chenowethK142.jpg ===
kristin-chenoweth

=== output/kristin-chenowethK143.jpg ===
kristin-chenoweth

=== output/kristin-chenowethK144.jpg ===
kristin-chenoweth

=== output/kristin-chenowethK145.jpg ===
kristin-chenoweth

=== output/kristin-chenowethK146.jpg ===
kristin-chenoweth

=== output/kristin-chenowethK147.jpg ===
kristin-chenoweth

=== output/kristin-chenowethK148.jpg ===
kristin-chenoweth

=== output/kristin-chenowethK149.jpg ===
kristin-chenoweth

=== output/kristin-chenowethK150.jpg ===
kristin-chenoweth

=== output/kristin-chenowethK151.jpg ===
kristin-chenoweth

=== output/kristin-chenowethK152.jpg ===
kristin-chenoweth

=== output/kristin-chenowethK153.jpg ===
kristin-chenoweth

=== output/kristin-ch

Exception: Unable to find a face: output/kristin-chenowethK267.jpg

In [75]:
adversarial('generated-embeddings/limited/classifier.pkl', 'test-images/tatyana_ali_KC_GA.jpg','tatyana-m.-ali', 'kristin-chenoweth',  'B')


=== test-images/tatyana_ali_KC_GA.jpg ===

=== output/tatyana-m.-aliB0.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliB1.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliB2.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliB3.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliB4.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliB5.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliB6.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliB7.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliB8.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliB9.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliB10.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliB11.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliB12.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliB13.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliB14.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliB15.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliB16.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliB17.jpg ===
tatyana-m.-ali

=== output/t

tatyana-m.-ali

=== output/tatyana-m.-aliB154.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliB155.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliB156.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliB157.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliB158.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliB159.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliB160.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliB161.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliB162.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliB163.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliB164.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliB165.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliB166.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliB167.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliB168.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliB169.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliB170.jpg ===
tatyana-m.-ali

=== output/tatyana-m.-aliB171.jpg ===
tatyana-m.-ali

=== output/t

### Test Case B5: People of Different Races and Genders
#### Pair 1: Kristin Chenoweth and George Lopez

In [76]:
adversarial('generated-embeddings/limited/classifier.pkl', 'test-images/kristin_chenoweth_GL_GA.jpg', 'george-lopez', 'kristin-chenoweth', 'J')


=== test-images/kristin_chenoweth_GL_GA.jpg ===
Success! kristin-chenoweth achieved through genetic algorithm


Finally there is an image that the genetic algorithm optimized to an extent the brute forcing is unnecessary. Let's also check the image against the full FaceScrub:

In [86]:
adversarial('generated-embeddings/fullfacescrub/classifier.pkl', 'test-images/kristin_chenoweth_GL_GA.jpg', 'george-lopez', 'kristin-chenoweth', 'J')


=== test-images/kristin_chenoweth_GL_GA.jpg ===
Success! kristin-chenoweth achieved through genetic algorithm


In [77]:
adversarial('generated-embeddings/limited/classifier.pkl', 'test-images/george_lopez_KC_GA.jpg', 'george-lopez', 'kristin-chenoweth', 'B')


=== test-images/george_lopez_KC_GA.jpg ===

=== output/george-lopezB0.jpg ===
george-lopez

=== output/george-lopezB1.jpg ===
george-lopez

=== output/george-lopezB2.jpg ===
george-lopez

=== output/george-lopezB3.jpg ===
george-lopez

=== output/george-lopezB4.jpg ===
george-lopez

=== output/george-lopezB5.jpg ===
george-lopez

=== output/george-lopezB6.jpg ===
george-lopez

=== output/george-lopezB7.jpg ===
george-lopez

=== output/george-lopezB8.jpg ===
george-lopez

=== output/george-lopezB9.jpg ===
george-lopez

=== output/george-lopezB10.jpg ===
george-lopez

=== output/george-lopezB11.jpg ===
george-lopez

=== output/george-lopezB12.jpg ===
george-lopez

=== output/george-lopezB13.jpg ===
george-lopez

=== output/george-lopezB14.jpg ===
george-lopez

=== output/george-lopezB15.jpg ===
george-lopez

=== output/george-lopezB16.jpg ===
george-lopez

=== output/george-lopezB17.jpg ===
george-lopez

=== output/george-lopezB18.jpg ===
george-lopez

=== output/george-lopezB19.jpg ===

george-lopez

=== output/george-lopezB166.jpg ===
george-lopez

=== output/george-lopezB167.jpg ===
george-lopez

=== output/george-lopezB168.jpg ===
george-lopez

=== output/george-lopezB169.jpg ===
george-lopez

=== output/george-lopezB170.jpg ===
george-lopez

=== output/george-lopezB171.jpg ===
george-lopez

=== output/george-lopezB172.jpg ===
george-lopez

=== output/george-lopezB173.jpg ===
george-lopez

=== output/george-lopezB174.jpg ===
george-lopez

=== output/george-lopezB175.jpg ===
george-lopez

=== output/george-lopezB176.jpg ===
george-lopez

=== output/george-lopezB177.jpg ===
george-lopez

=== output/george-lopezB178.jpg ===
george-lopez

=== output/george-lopezB179.jpg ===
george-lopez

=== output/george-lopezB180.jpg ===
george-lopez

=== output/george-lopezB181.jpg ===
george-lopez

=== output/george-lopezB182.jpg ===
george-lopez

=== output/george-lopezB183.jpg ===
george-lopez

=== output/george-lopezB184.jpg ===
george-lopez

=== output/george-lopezB185.jpg ===


Interestingly, it is only the image of Kristin Chenoweth that was successfully optimized, likely a reflection of the random nature of the algorithm. Indeed, if you run the code yourself you might not get these results. 

#### Pair 2: Tatyan M. Ali and Ken Watanabe

In [78]:
adversarial('generated-embeddings/limited/classifier.pkl', 'test-images/tatyana_ali_KW_GA.jpg', 'tatyana-m.-ali', 'ken-watanabe', 'G')


=== test-images/tatyana_ali_KW_GA.jpg ===


Exception: Unable to load image: test-images/tatyana_ali_KW_GA.jpg

In [79]:
adversarial('generated-embeddings/limited/classifier.pkl', 'test-images/ken_watanabe_TA_GA.jpg', 'ken-watanabe', 'tatyana-m.-ali', 'B')


=== test-images/ken_watanabe_TA_GA.jpg ===

=== output/ken-watanabeB0.jpg ===
ken-watanabe

=== output/ken-watanabeB1.jpg ===
ken-watanabe

=== output/ken-watanabeB2.jpg ===
ken-watanabe

=== output/ken-watanabeB3.jpg ===
ken-watanabe

=== output/ken-watanabeB4.jpg ===
ken-watanabe

=== output/ken-watanabeB5.jpg ===
ken-watanabe

=== output/ken-watanabeB6.jpg ===
ken-watanabe

=== output/ken-watanabeB7.jpg ===
ken-watanabe

=== output/ken-watanabeB8.jpg ===
ken-watanabe

=== output/ken-watanabeB9.jpg ===
ken-watanabe

=== output/ken-watanabeB10.jpg ===
ken-watanabe

=== output/ken-watanabeB11.jpg ===
ken-watanabe

=== output/ken-watanabeB12.jpg ===
ken-watanabe

=== output/ken-watanabeB13.jpg ===
ken-watanabe

=== output/ken-watanabeB14.jpg ===
ken-watanabe

=== output/ken-watanabeB15.jpg ===
ken-watanabe

=== output/ken-watanabeB16.jpg ===
ken-watanabe

=== output/ken-watanabeB17.jpg ===
ken-watanabe

=== output/ken-watanabeB18.jpg ===
ken-watanabe

=== output/ken-watanabeB19.jpg ===

ken-watanabe

=== output/ken-watanabeB166.jpg ===
ken-watanabe

=== output/ken-watanabeB167.jpg ===
ken-watanabe

=== output/ken-watanabeB168.jpg ===
ken-watanabe

=== output/ken-watanabeB169.jpg ===
ken-watanabe

=== output/ken-watanabeB170.jpg ===
ken-watanabe

=== output/ken-watanabeB171.jpg ===
ken-watanabe

=== output/ken-watanabeB172.jpg ===
ken-watanabe

=== output/ken-watanabeB173.jpg ===
ken-watanabe

=== output/ken-watanabeB174.jpg ===
ken-watanabe

=== output/ken-watanabeB175.jpg ===
ken-watanabe

=== output/ken-watanabeB176.jpg ===
ken-watanabe

=== output/ken-watanabeB177.jpg ===
ken-watanabe

=== output/ken-watanabeB178.jpg ===
ken-watanabe

=== output/ken-watanabeB179.jpg ===
ken-watanabe

=== output/ken-watanabeB180.jpg ===
ken-watanabe

=== output/ken-watanabeB181.jpg ===
ken-watanabe

=== output/ken-watanabeB182.jpg ===
ken-watanabe

=== output/ken-watanabeB183.jpg ===
ken-watanabe

=== output/ken-watanabeB184.jpg ===
ken-watanabe

=== output/ken-watanabeB185.jpg ===


### Test Case B6: Non-Human Face
The previous targeting has focused on tricking the facial recognition model, and many of the modifications have caused faced to not be detected, but we should also test whether the face detector can be tricked into detecting a human face where there isn't one. The human distinction is important as animal species may have the same general combination of facial features but their spatial arrangement is different. For example we can create a makeFace method and test it with a cat:

In [111]:
def makeFace(filename, label):
    bgrImg = cv2.imread(filename)
    rgbImg = cv2.cvtColor(bgrImg, cv2.COLOR_BGR2RGB)
    face = align.getLargestFaceBoundingBox(rgbImg)
    count = 0
    while face is None and count < 200:
        img = Image.open(filename)
        img.load()
        img_a = np.asarray(img)
        l, w, d = img_a.shape
        mult = np.random.randint(3, size=(l, w, d), dtype=np.uint8)
        r = random.randint(0,1)
        if r == 0:
            img_a = img_a + mult
        else:
            img_a = img_a - mult
        img_a = np.clip(img_a, 0, 255)
        img = Image.fromarray(img_a, 'RGB')
        filename = 'output/' + label + str(count) + '.jpg'
        img.save(filename)
        print("Testing: " + filename)
        bgrImg = cv2.imread(filename)
        rgbImg = cv2.cvtColor(bgrImg, cv2.COLOR_BGR2RGB)
        face = align.getLargestFaceBoundingBox(rgbImg)
        count += 1
    if face is not None:
        print("Success!")
    else:
        print("Not able to trick the face detector")

In [112]:
makeFace('test-images/cat.jpg', 'catfaceA')

Testing: output/catfaceA0.jpg
Testing: output/catfaceA1.jpg
Testing: output/catfaceA2.jpg
Testing: output/catfaceA3.jpg
Testing: output/catfaceA4.jpg
Testing: output/catfaceA5.jpg
Testing: output/catfaceA6.jpg
Testing: output/catfaceA7.jpg
Testing: output/catfaceA8.jpg
Testing: output/catfaceA9.jpg
Testing: output/catfaceA10.jpg
Testing: output/catfaceA11.jpg
Testing: output/catfaceA12.jpg
Testing: output/catfaceA13.jpg
Testing: output/catfaceA14.jpg
Testing: output/catfaceA15.jpg
Testing: output/catfaceA16.jpg
Testing: output/catfaceA17.jpg
Testing: output/catfaceA18.jpg
Testing: output/catfaceA19.jpg
Testing: output/catfaceA20.jpg
Testing: output/catfaceA21.jpg
Testing: output/catfaceA22.jpg
Testing: output/catfaceA23.jpg
Testing: output/catfaceA24.jpg
Testing: output/catfaceA25.jpg
Testing: output/catfaceA26.jpg
Testing: output/catfaceA27.jpg
Testing: output/catfaceA28.jpg
Testing: output/catfaceA29.jpg
Testing: output/catfaceA30.jpg
Testing: output/catfaceA31.jpg
Testing: output/ca

### Test Case B7: No Face
The cat test case failed, but let's also try makeFace on a picture of something that doesn't have a face at all - a bicycle.

In [113]:
makeFace('test-images/bicycle.jpg', 'bicycleA')

Testing: output/bicycleA0.jpg
Testing: output/bicycleA1.jpg
Testing: output/bicycleA2.jpg
Testing: output/bicycleA3.jpg
Testing: output/bicycleA4.jpg
Testing: output/bicycleA5.jpg
Testing: output/bicycleA6.jpg
Testing: output/bicycleA7.jpg
Testing: output/bicycleA8.jpg
Testing: output/bicycleA9.jpg
Testing: output/bicycleA10.jpg
Testing: output/bicycleA11.jpg
Testing: output/bicycleA12.jpg
Testing: output/bicycleA13.jpg
Testing: output/bicycleA14.jpg
Success!


In [115]:
os.rename('output/bicycleA14.jpg','test-images/bicycle-facesuccess.jpg')

The successful bicycle:
![Bicycle with noise](https://github.com/erstrong/BigDataSystemsandIntelligenceAnalytics/blob/master/AdversarialFaceRecognition/examples/bicycle-facesuccess.jpg?raw=true)
This would never trick a person, but the model detects a face anyway! Let's look at who the classifiers label it as:

In [117]:
run('generated-embeddings/limited/classifier.pkl', 'test-images/bicycle-facesuccess.jpg')


=== test-images/bicycle-facesuccess.jpg ===
samuel-l.-jackson


In [116]:
run('generated-embeddings/fullfacescrub/classifier.pkl', 'test-images/bicycle-facesuccess.jpg')


=== test-images/bicycle-facesuccess.jpg ===
tempestt-bledsoe


## Conclusion
These various experiments highlight the susceptiblity of facial recognition pipelines to adversarial examples, whether created by changing a single color channel or adding random noise. These changes may not affect a person's ability to recognize the subject of the picture but for a convolutional neural network they shift the locations of edges leading to changes in the patterns detected. 

Using the difference in dot products of embeddings may not be an ideal strategy for targeted attacks, but as shown with the image of Kristin Chenoweth targeting George Lopez, this strategy can be sufficent. Can being the key word, as with three of the images the genetic algorithm failed to provide any improvement at all. Given the random nature of the children generated, it is possible that allowing the genetic algorithm to run for more generations might have yielded results eventually, and might have yielded better results for the other pairs but what is tested here highlights the fact that this approach can be used.

## References
AI Junkie. "Genetic Algorithms in Plain English." Web. Retrieved 19 April 2018. http://www.ai-junkie.com/ga/intro/gat1.html

Amos, Brandon. "OpenFace". CMUSatyaLab, 13 October 2015. Web. Retrieved 19 April 2018. http://cmusatyalab.github.io/openface/demo-2-comparison/

Geitgey, Adam. "Machine Learning is Fun Part 8: How to Intentionally Trick Neural Networks." Medium, 16 August 2017. Web. Retrieved 19 April 2018. https://medium.com/@ageitgey/machine-learning-is-fun-part-8-how-to-intentionally-trick-neural-networks-b55da32b7196

Kazemi, Vahid, and Josephine Sullivan. "One Millisecond Face Alignment with an Ensemble of Regression Trees." Proceedings of the 2014 IEEE Conference on Computer Vision and Pattern Recognition. IEEE Computer Society, 2014.

Mallawaarachchi, Vijini."Introduction to Genetic Algorithms — Including Example Code." Toward Data Science, 7 July, 2017. Web. Retrieved 19 April 2018. https://towardsdatascience.com/introduction-to-genetic-algorithms-including-example-code-e396e98d8bf3

Ng, Hong-Wei, and Stefan Winkler. "A data-driven approach to cleaning large face datasets." Image Processing (ICIP), 2014 IEEE International Conference on. IEEE, 2014.

Schroff, Florian, Dmitry Kalenichenko, and James Philbin. "Facenet: A unified embedding for face recognition and clustering." Proceedings of the IEEE conference on computer vision and pattern recognition. 2015.


## Additional Code Citations
https://hub.docker.com/r/bamos/openface/

https://pillow.readthedocs.io/en/3.1.x/reference/Image.html

https://stackoverflow.com/questions/17595912/gaussian-smoothing-an-image-in-python

https://stackoverflow.com/questions/22937589/how-to-add-noise-gaussian-salt-and-pepper-etc-to-image-in-python-with-opencv

https://stackoverflow.com/questions/42045362/change-contrast-of-image-in-pil

http://www.dfstudios.co.uk/articles/programming/image-programming-algorithms/image-processing-algorithms-part-5-contrast-adjustment/

https://stackoverflow.com/questions/3121979/how-to-sort-list-tuple-of-lists-tuples  


## License
<a rel="license" href="http://creativecommons.org/licenses/by/3.0/us/"><img alt="Creative Commons License" src="https://i.creativecommons.org/l/by/3.0/us/88x31.png" align="left" /></a>

The text in this document by Emily Strong is licensed under CC BY 3.0 https://creativecommons.org/licenses/by/3.0/us/ 

All code in this document by Emily Strong is licensed under the MIT License https://opensource.org/licenses/MIT

OpenFace and the getRep, infer, compare and makeFace methods are adapted from code copyright Carnegie Mellon University under the Apache 2.0 License https://github.com/cmusatyalab/openface/blob/master/LICENSE

The FaceScrub data set by H.W. Ng and S. Winkler is licensed under CC BY NC ND https://creativecommons.org/licenses/by-nc-nd/3.0/. Individual images are property of their copyright holders and are not shown here nor directly provided due to this. 

The supplemental data set of images of Keira Knightley and Natalie Portman by Emily Strong is licensed under CC BY NC ND https://creativecommons.org/licenses/by-nc-nd/3.0/. Individual images are property of their copyright holders and are not shown here nor directly provided due to this. 

The images used in test cases are licensed as follows: 
* Tatyana M Ali: Image by The Bui Brothers is licensed under CC BY SA 2.0 https://creativecommons.org/licenses/by-sa/2.0/
* Kristin Chenoweth: Image by Drama League is licensed under CC BY 2.0 https://creativecommons.org/licenses/by/2.0
* Colin Firth: Image by Nicogenin is licensed under CC BY SA 2.0 https://creativecommons.org/licenses/by-sa/2.0/
* Samuel L Jackson: Image by Gage Skidmore is licenced under CC BY SA 2.0 https://creativecommons.org/licenses/by-sa/2.0/
* Keira Knightley: Image by Tony Shek is licensed under CC BY 2.0 https://creativecommons.org/licenses/by/2.0
* George Lopez: Image by Official Brooke Army Medical Center is licensed under CC BY 2.0 https://creativecommons.org/licenses/by/2.0
* Matthew Perry: Image by David Shankbone is licensed under CC BY 2.0 https://creativecommons.org/licenses/by/2.0
* Natalie Portman: Image by gdcgraphics is licensed under CC BY 3.0 https://creativecommons.org/licenses/by/3.0/deed.en
* Ken Watanabe: Image by Thore Siebrands is licensed under CC BY 2.0 https://creativecommons.org/licenses/by/2.0
* Cat: Image is in the public domain
* Bicycle: Image by timquijano is licensed under CC BY 2.0 https://creativecommons.org/licenses/by/2.0